## <center>Avaliação de produções em pesquisa segundo edital<br /> Programa de Incentivo à Pesquisa (PIP) 2024 da Fiocruz Ceará</center>

    Antonio Marcos Aires Barbosa – Fiocruz Ceará

**Objetivo:**

    Avaliar indicadores em pesquisa para ranquear currículos de proponentes às bolsas em pesquisa. São considerados os currículos dos orientadores que submeteram inscrições ao Programa de Incentivo à Pesquisa (PIP) em sua edição no ano de 2024, contemplando produções no período de 2020 a 2024, com base nos mesmos parâmetros definidos no edital Fiocruz Ceará Nº 01/2024

# <b>F00: Preparar Ambiente local</b>

### Instalações

#### Git, WSL, Contêiner Docker, ambiente virtual

In [ ]:
## Instalar o WSL e integrar ao VSCode, no terminal rodar:
## Verificar versões já instaladas
#wsl -l -v
## Atualizar para WSL2 para que as instalações de distros já rodem em WSL2 por padrão
#wsl --set-default-version 2
## Reiniciar a máquina e instalar distribuição Linux Ubuntu LTS pelo store do windows
## Configurar VScode: iniciar VScode e instalar a extensão "Remote - WSL" para desenvolver diretamente no VSCode dentro do ambiente do WSL.
# Após a instalação, na parte inferior esquerda da janela do VSCode, aparecerá o ícone verde.
# Clicar no ícone verde e selecionar "New WSL Window" ou "Reopen in WSL" se o projeto já estiver aberto.
# Agora, o VSCode estará rodando dentro do contexto do seu WSL, pode-se abrir terminais dentro do VSCode que acessarão diretamente o Linux.

## Instalar Python e o Pip:
# sudo apt update
# sudo apt install python3-pip

## Inserir dados do Git no VScode, no terminal rodar:
# git config --global user.name "nome_usuario_gi"
# git config --global user.email "email_git"

#### Instalar os gerenciador e pacotes pip e Conda

In [ ]:
## Intalar os gerenciador de pacotes PIP  no terminal do WSL executar:
# sudo apt update
# sudo apt upgrade
# sudo apt install python3-pip
# python3 -m pip install --upgrade pip

## Atualizar o gerenciador de pacotes e ferramentas de compilação
# %pip install --upgrade pip setuptools wheel

## Instalar primeiro o GraphViz antes do ygraphviz, no terminal do WSL rodar e depois reiniciar o kernel:
## Para Linux e WSL instalar a partir do terminal:
# sudo apt-get install graphviz graphviz-dev

## Para Windows, atualizar o gerenciador de pacotes e ferramentas de compilação:
# %pip install --upgrade pip setuptools wheel

## Instalar o Chocolatey (Só para Windows, não no WSL)
## Baixar e instalar o gerenciador chocolatey em https://jcutrer.com/windows/install-chocolatey-choco-windows10
# Set-ExecutionPolicy Bypass -Scope Process -Force; [System.Net.ServicePointManager]::SecurityProtocol = [System.Net.ServicePointManager]::SecurityProtocol -bor 3072; iex ((New-Object System.Net.WebClient).DownloadString('https://chocolatey.org/install.ps1'))

## Baixar e instalar o Graphviz em https://www.graphviz.org/download/
## https://savleen307.medium.com/pygraphviz-installation-in-windows-f45cc6fed981
## Seguir as instruções em https://pygraphviz.github.io/documentation/stable/install.html#id1
# O comando na página acima está errado por conter duas aspas onde não deve, executar o comando abaixo:
# python -m pip install --use-pep517 --config-settings="--global-option=build_ext" --config-settings="--global-option=-IC:\Program Files\Graphviz\include" --config-settings=--global-option="-LC:\Program Files\Graphviz\lib" pygraphviz

## Instalar o pacote no ambiente local
# %pip install pygraphviz

## Para instalar o Conda (Miniconda ou Anaconda) no WSL, baixar o script de instalação diretamente do site oficial e executá-lo manualmente.
## Passos para instalar o Miniconda como exemplo:
## Baixar script de instalação do Miniconda para Linux:
# wget https://repo.anaconda.com/miniconda/Miniconda3-latest-Linux-x86_64.sh
# bash Miniconda3-latest-Linux-x86_64.sh
# conda --version

#### Instalar requirements.txt e importar bibliotecas

In [ ]:
## Localizar requirements.txt para instalar bibliotecas no ambente
# os.listdir('./../../../../')
# %pip install -r ./../../../../requirements.txt

## Outras instalações pontuais quando necessário, por exemplo:
# import os, tqdm
# %pip install chardet
# print(tqdm.__version__)
# %pip3 install --upgrade plotly
# %pip3 install omegaconf --upgrade

#### Instalar e configurar GPU e drivers CUDA Toolkit

In [ ]:
## Instalar drivers da GPU e compilador CUDA Nvidia
## Obter comandos adequados para cada sistema em: https://developer.nvidia.com/cuda-downloads
## Exemplo para Linux com Ubuntu
# wget https://developer.download.nvidia.com/compute/cuda/repos/wsl-ubuntu/x86_64/cuda-wsl-ubuntu.pin
# sudo mv cuda-wsl-ubuntu.pin /etc/apt/preferences.d/cuda-repository-pin-600
# wget https://developer.download.nvidia.com/compute/cuda/12.4.0/local_installers/cuda-repo-wsl-ubuntu-12-4-local_12.4.0-1_amd64.deb
# sudo dpkg -i cuda-repo-wsl-ubuntu-12-4-local_12.4.0-1_amd64.deb
# sudo cp /var/cuda-repo-wsl-ubuntu-12-4-local/cuda-*-keyring.gpg /usr/share/keyrings/
# sudo apt-get update
# sudo apt-get -y install cuda-toolkit-12-4

## Instruções para instalação do PyTorch para usar a GPU em Windows
# https://sh-tsang.medium.com/tutorial-cuda-cudnn-anaconda-jupyter-pytorch-installation-in-windows-10-96b2a2f0ac57

## Para máquinas com apenas CPU
# !pip install torch torchvision

## Testar cálculo na GPU
# import torch
# x = torch.rand(5, 3)
# print(x)

#### Implementar classes para obter e preparar dados

    LattesScraper (Extrair currículos Lattes)
    SoupParser (Extrair dados de Objeto Soup)
    Neo4jPersister (Persistir em Neo4j)
    DatasetArticlesGenerator (Gerar Datasets)
    DictToHDF5 (converter dicionários para HDF5)
    ArticlesCounter (Montar qte artigos e atualização)

# <b>F01: Obter dados das Produções</b>

## Rodar testes e definir pastas

### Gerar pastas e classes de processamento

In [1]:
from pathlib import Path
from getpass import getpass
from datetime import datetime
from IPython.display import clear_output
import pandas as pd, os, re, sys, time, json, subprocess

## Configurar exibição do pandas para melhor visualizar os dados
pd.set_option('display.max_colwidth', None)
pd.set_option('colheader_justify', 'left')
pd.set_option('display.max_rows', 600)

def find_repo_root(path='.', depth=10):
    ''' 
    Busca o arquivo .git e retorna string com a pasta raiz do repositório
    '''
    # Limitar profundidade para evitar loop infinito
    if depth < 0:
        return None
    path = Path(path).absolute()
    if (path / '.git').is_dir():
        return path
    return find_repo_root(path.parent, depth-1)

## Definir a pasta de base do repositório local
base_repo_dir = find_repo_root()

## Sempre construir os caminhos usando os.path.join para compatibilidade WxL
folder_utils = os.path.join(base_repo_dir, 'utils')
folder_domain = os.path.join(base_repo_dir, 'source', 'domain')
folder_data_input = os.path.join(base_repo_dir, '_data', 'in_csv')
folder_data_output = os.path.join(base_repo_dir, '_data', 'out_json')

## Adicionar pastas locais ao sys.path para importar pacotes criados localmente
sys.path.append(folder_utils)
sys.path.append(folder_domain)
# from scraper_pasteur import PasteurScraper
# from scraper_sucupira import SucupiraScraper
# from scraper_sucupira_edge import SucupiraScraperEdge
from environment_setup import EnvironmentSetup
from chromedriver_manager import ChromeDriverManager
from neo4j_persister import Neo4jPersister
from lattes_scrapper import JSONFileManager, LattesScraper, HTMLParser, SoupParser, GetQualis, ArticlesCounter, DictToHDF5, attribute_to_be_non_empty

t00 = time.time()

### Checar Chromedriver e GoogleChrome

In [2]:
# Cria instância da classe ChromeDriverManager e verifica compatibilidade entre versões do Chrome e Chromedriver
actualizer = ChromeDriverManager()
actualizer.main()

Versões 126 Chrome e 126 Chromedriver estão compatíveis


### Obter Qualis Periódicos Plataforma Sucupira

In [3]:
# sucupira = SucupiraScraperEdge()
# sucupira.scrape_sucupira()

In [4]:
# Cria instância da classe EnvironmenSetup e preparar pastas
preparer = EnvironmentSetup()
folder_name = input("Digite o nome da pasta principal: ")
preparer.set_root_path(folder_name)
preparer.try_cpu()
preparer.try_gpu()
preparer.try_amb()
# preparer.try_browser()
preparer.preparar_pastas()

## Remover diretórios no linux
# !rm -rf /home/mak/fioce
# os.listdir('/home/mak/fioce')

All necessary directories are ensured.
Processador em uso: 
Arquitetura modelo: AMD64 Family 25 Model 33 Stepping 0, AuthenticAMD
Arquitetura em uso: 64bit
Frequência das CPU: 3801.0 MHz
  Qte CPUs físicas: 8
  Qte CPUs lógicas: 16
Carga total na CPU: 11.6%
Ocupação atual CPU: user=8.9%, system=1.1%, idle=89.6%

Espaço Total em disco: 465.15 GB
Espaço em disco usado: 439.84 GB 94.6%
Espaço em disco livre: 25.31 GB 5.4%

Capacidade memórias RAM: 63.94 GB
Utilização atual da RAM: 17.29 GB

VERSÕES DOS DRIVERS CUDA, PYTORCH E GPU
nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2023 NVIDIA Corporation
Built on Wed_Nov_22_10:30:42_Pacific_Standard_Time_2023
Cuda compilation tools, release 12.3, V12.3.107
Build cuda_12.3.r12.3/compiler.33567101_0

    PyTorch: 2.3.1+cu121
Dispositivo: cuda
Disponível: cuda True  | Inicializado: False | Capacidade: (8, 9)
Nome GPU: NVIDIA GeForce RTX 4080 SUPER  | Quantidade: 1

VERSÕES DAS PRINCIPAIS BIBLIOTECAS INSTALADAS NO ENVIROMENT
Ambiente Con

## Montar lista de nomes dos Docentes (lista_busca)

### Carregar nomes da planilha de Docentes

In [5]:
# Ler dados do arquivo Excel do Setor de Recursos Humanos
pathdata = '_data/in_xls/'
datasheet = 'fioce_colaboradores-2023.xls'

# Ler apenas os cabeçalhos do arquivo Excel
headers = pd.read_excel(pathdata+datasheet, skiprows=3, header=0, nrows=0).columns
# headers

# Usar função para indicar quais colunas devem ser eliminadas na leitura
def cols_to_keep(col_name):
    return col_name not in ['QUANT','Unnamed: 3','Unnamed: 6','Unnamed: 9','ADICIONAL OCUPACIONAL',
                            'EMPRESA/BOLSA/PROGRAMA','GESTOR','ADI','POSSE NA FIOCRUZ',
                            'VIGÊNCIA BOLSA/ENCERRAMENTO DO CONTRATO','Unnamed: 17',
                            'EMAIL INSTITUCIONAL','EMAIL PESSOAL','GENERO','DATA NASCIMENTO',
                            'Unnamed: 22','FORMAÇÃO','ENDEREÇO RESIDENCIAL']

# Filtrar cabeçalhos com base na função
selected_columns = [col for col in headers if cols_to_keep(col)]

# Ler dados do arquivo Excel do Setor de Recursos Humanos
fioce_pessoal = pd.read_excel(pathdata+datasheet, skiprows=3, header=0, usecols=selected_columns)
print(f'{len(fioce_pessoal.index)} nomes de colaboradores no total, todos vínculos e status')
print(f'{len(fioce_pessoal["VÍNCULO"].unique()):3} tipos de vínculos')

print('\nTipos de vínculos',list(fioce_pessoal['VÍNCULO'].unique()))
print('  Tipos de status',list(fioce_pessoal['STATUS'].unique()))
filtro1 = fioce_pessoal.VÍNCULO == 'SERVIDOR'
filtro2 = fioce_pessoal['STATUS'].isin(['ATIVO', 'AFASTADO'])
lista_nomes = fioce_pessoal[(filtro1) & (filtro2)]['NOME'].tolist()

print(f'\n{len(lista_nomes)} nomes para extrair currículos')
for i,nome in enumerate(lista_nomes):
    print(f'{i+1:2}. {nome}')

285 nomes de colaboradores no total, todos vínculos e status
 10 tipos de vínculos

Tipos de vínculos ['SERVIDOR', 'COORENAÇÃO GERAL', 'TERCEIRIZADO', 'BOLSISTA', 'ESTÁGIO PEC', 'UNADIG', 'NORMATEL', 'SERVIDOR-CEDIDA PARA CORREGEDORIA ', 'SERVIDOR-CEDIDA PARA FIOCRUZ PE', 'SERVIDOR-CEDIDO PARA AUDITORIA INTERNA']
  Tipos de status ['ATIVO', 'AFASTADO', 'EXONERADO', 'CONTRATO ENCERRADO', 'APOSENTADA', 'REMOÇÃO']

58 nomes para extrair currículos
 1. Alice Paula Di Sabatino Guimaraes
 2. Ana Claudia De Araújo Teixeira
 3. Ana Camila Oliveira Alves
 4. Angela Christina De Moraes Ostritz
 5. Adriana Costa Bacelo
 6. Anna Carolina Machado Marinho
 7. Antonio Marcos Aires Barbosa
 8. Anya Pimentel Gomes Fernandes Vieira Meyer
 9. Bruno Bezerra Carvalho
10. Carla Freire Celedônio Fernandes
11. Carlos Jose Araujo Pinheiro
12. Claudia Stutz Zubieta
13. Charles Cerqueira De Abreu
14. Clarice Gomes E Souza Dabés
15. Clarissa Romero Teixeira
16. Dayane Alves Costa
17. Donat Alexander De Chapeaurou

In [6]:
grupos_internos = fioce_pessoal['ÁREA'].unique()
coordenacoes=[]
grupos_tematicos=[]
for i in grupos_internos:
    # print(i)
    if 'coordenação' in str(i).lower():
        coordenacoes.append(i)
    elif str(i) != 'nan':
        grupos_tematicos.append(str(i))

In [7]:
coordenacoes.sort()
coordenacoes

['Coordenação Geral',
 'Coordenação Geral ',
 'Coordenação Geral ( EPSJV/FIOCRUZ)',
 'Coordenação Geral (QUALIDADE)',
 'Coordenação Geral (SECRETARIA EXECUTIVA)',
 'Coordenação da Gestão e Desenvolvimento Institucional ',
 'Coordenação da Gestão e Desenvolvimento Institucional   (ALMOXARIFADO)',
 'Coordenação da Gestão e Desenvolvimento Institucional (COMPRAS)',
 'Coordenação da Gestão e Desenvolvimento Institucional (COORDENAÇÃO) ',
 'Coordenação da Gestão e Desenvolvimento Institucional (FINANCEIRO)',
 'Coordenação da Gestão e Desenvolvimento Institucional (INFRAESTRUTURA / SIMAM)',
 'Coordenação da Gestão e Desenvolvimento Institucional (INFRAESTRUTURA)',
 'Coordenação da Gestão e Desenvolvimento Institucional (LOGÍSTICA)',
 'Coordenação da Gestão e Desenvolvimento Institucional (PATRIMÔNIO)',
 'Coordenação da Gestão e Desenvolvimento Institucional (PLANEJAMENTO)',
 'Coordenação da Gestão e Desenvolvimento Institucional (SGP / ST)',
 'Coordenação da Gestão e Desenvolvimento Instituc

In [8]:
grupos_tematicos.sort()
grupos_tematicos

['Bio-Manguinhos',
 'Biotecnologia',
 'Biotecnologia-GR1 (IMUNOPARASITOLOGIA)',
 'Biotecnologia-GR2 (VIGILÂNCIA GENÔMICA)',
 'Biotecnologia-GR3 (BIOTECNOLOGIA)',
 'Central Analitica - UNADIG',
 'Saúde Digital',
 'Saúde da Família',
 'Saúde e Ambiente']

In [9]:
# Outras atividades não relacionadas diretamente com pesquisa
remover = ['Angela Christina De Moraes Ostritz',
           'Bruno Bezerra Carvalho',
           'Carlos Jose Araujo Pinheiro',
           'Charles Cerqueira De Abreu',
           'Ezequiel Valentim De Melo',
           'Ivanildo Lopes Farias',
           'João Baptista Estabile Neto',
           'Kamila Matos Albuquerque',
           'Luciana Coelho Serafim',
           'Luciano Pinto Zorzanelli',
           'Luciana Silvério Alleluia Higino Da Silva',
           'Luis Fernando Pessoa De Andrade',
           'Marcelo Jorge Lopes Coutinho',
           'Nilton Luiz Costa Machado',
           'Patricia Maria Ferreira da Silva',
           'Renato Caldeira De Souza',
           'Sergio Dos Santos Reis',
           'Clarice Gomes E Souza Dabés',
           'Luciana Pereira Lindenmeyer',
           'Rodrigo Carvalho Nogueira',
           
        #    'Ana Camila Oliveira Alves',
        #    'Antonio Marcos Aires Barbosa',
        #    'Venúcia Bruna Magalhães Pereira',
           ]

trocar = {
    'Maximiliano Loiola Ponte De Souza': 'Maximiliano Ponte',
    'Raphael Trevizani Roque': 'Raphael Trevizani',
    }

# Adicionar pós-doc e demais membros de equipes de projetos
adicionar = [
    'Ana Carolina Matias Dinelly Pinto',
    'Geraldo Rodrigues Sartori',
    'Elaine Silva Nascimento Andrade',
    'Cecili Barrozo Mendes',
    'Christiane França Martins',
    'Ketlen Christine Ohse',
    'Clarissa Perdigao Mello Ferraz',
    'Allysson Allan de Farias',
    'Júlio César Martins Ximenes',
    'Wallady da Silva Barroso',
    'Lucas Lima de Carvalho',
    'Manuel Alves dos Santos Júnior',
    'Valdir Ferreira de Paula Junior',
    'Felipe Augusto Rocha Rodrigues',
    'Talita Abrante Leite',
    'Fátima de Cássia Evangelista de Oliveira',
    'Hélcio Silva dos Santos',
    'Rodolfo de Melo Nunes',
    'Ana Karine Rocha de Melo Leite',
    'Conceição da Silva Martins Rebouças',
    'Maria Francilene Souza Silva',
    'Anita Oliveira Brito Pereira Bezerra Martins',
    'Isaac Moura Araújo',
    'Débora Gaspar'   
]

lista_busca=[]
for i in lista_nomes:
    if i.strip() in trocar.keys():
        lista_busca.append(trocar.get(i))
    elif i.strip() not in remover:
        lista_busca.append(i)
for i in adicionar:
    if i.strip().lower() in [x.strip().lower() for x in lista_nomes]:
        pass
    elif i.strip() not in remover:
        lista_busca.append(i.strip().title())

# Limitando quantidade para testes
# lista_busca = lista_busca[:5]

print(f'{len(lista_busca)} currículos a extrair da plataforma Lattes')

62 currículos a extrair da plataforma Lattes


### Carregar nomes de arquivo .csv

In [10]:
# import os, pandas as pd
# from environment_setup import EnvironmentSetup
# preparer = EnvironmentSetup()

# ## Montar lista_nomes com arquivo .csv
# pathfilename = os.path.join(folder_data_input,'nomesdocentes.csv')
# lista_busca = pd.read_csv(pathfilename,header=None)[0].values

## <b>F01a: Extrair dados dos Docentes</b>

### Definir termos de vínculo para buscas por nomes

In [11]:
repo_root = preparer.find_repo_root(os.getcwd())
pasta_dados = os.path.join(repo_root,'data','output')
termos_busca = ['Fiocruz', 'Oswaldo Cruz', 'Imunopatologia', 'Ministerio da Saude', 'RENORBIO', 'Biotecnologia', 'Saúde']
print(f'{len(lista_busca)} currículos Lattes a extrair')

62 currículos Lattes a extrair


### Extrair currículos Docentes da plataforma Lattes
     Tempo: 0.4min/currículo em extração serial, paralelizada ??
    Espaço: 0,11MB por currículo, 108Gb/milhão (em JSON)

In [12]:
## Passar parâmetro only_doctors para False para extrair também níveis mestrado e graduação
t1 = time.time()
scraper = LattesScraper(termos_busca, 'bolt://localhost:7687', 'neo4j', 'password', only_doctors=False)
lista_busca = [scraper.normalizar_nome(x) for x in lista_busca]
dict_list_docents = scraper.scrape(lista_busca, termos_busca)
print(f'\n{scraper.tempo(t1,time.time())} para busca de {len(lista_busca)} nomes com extração de dados de {len(dict_list_docents)} dicionários')

Buscando currículos com qualquer nível de formação
 1/62: alice paula di sabatino guimaraes
       002 artigos extraídos
       Extração bem-sucedida
 2/62: ana claudia de araujo teixeira
        2 currículos homônimos: ana claudia de araujo teixeira
                         Fiocruz | False | ['Ana Claudia Teixeira de Araujo ']
                    Oswaldo Cruz | False | ['Ana Claudia Teixeira de Araujo ']
                  Imunopatologia | False | ['Ana Claudia Teixeira de Araujo ']
             Ministerio da Saude | False | ['Ana Claudia Teixeira de Araujo ']
                        RENORBIO | False | ['Ana Claudia Teixeira de Araujo ']
                   Biotecnologia | False | ['Ana Claudia Teixeira de Araujo ']
                           Saúde | False | ['Ana Claudia Teixeira de Araujo ']
                         Fiocruz | True | ['Ana Cláudia de Araújo Teixeira  Doutorado em Educação Brasileira pela Universidade Federal do Ceará, Brasil(2008) Pesquisadora em Saúde Pública da Funda

### Identificar currículos remanescentes

In [13]:
termos_busca = ['Fiocruz', 'Fundação Oswaldo Cruz', 'Biotecnologia', 'RENORBIO', 'saúde']
scraper = LattesScraper(termos_busca, 'bolt://localhost:7687', 'neo4j', 'password', only_doctors=False)

lista_restante = scraper.avaliar_remanescentes(lista_busca, dict_list_docents)

Buscando currículos com qualquer nível de formação
62 currículos a buscar no total
60 currículos já extraídos
(01) Alice Paula Di Sabatino Guimarães
(02) Ana Cláudia de Araújo Teixeira
(03) Ana Camila Oliveira Alves
(04) Adriana Costa Bacelo
(05) Anna Carolina Machado Marinho
(06) Antonio Marcos Aires Barbosa
(07) Anya Pimentel Gomes Fernandes Vieira Meyer
(08) Carla Freire Celedonio Fernandes
(09) Claudia Stutz Zubieta
(10) Clarissa Romero Teixeira
(11) Dayane Alves Costa
(12) Donat Alexander de Chapeaurouge
(13) Eduardo Ruback dos Santos
(14) Fabio Miyajima
(15) Fernando Braga Stehling Dias
(16) Fernando Ferreira Carneiro
(17) Galba Freire Moita
(18) Giovanny Augusto Camacho Antevere Mazzarotto
(19) Gilvan Pessoa Furtado
(20) Ivana Cristina de Holanda Cunha Barreto
(21) Jaime Ribeiro Filho
(22) João Hermínio Martins da Silva
(23) José Luís Passos Cordeiro
(24) Luiz Odorico Monteiro de Andrade
(25) Marcela Helena Gambim Fonseca
(26) Marcos Roberto Lourenzoni
(27) Márcio Flávio Moura d

### Complementar com dados prévios

In [14]:
# jfm = JSONFileManager()
# filename = 'docents_dict_list_old.json'
# dict_list_docents_old, formatted_creation_date, formatted_modification_date, time_count, unit = jfm.load_from_json(os.path.join(folder_data_input,filename))
# for n,i in enumerate(dict_list_docents_old):
#     nome_old = scraper.normalizar_nome(i.get('Identificação')['Nome'])
#     print(f'{n+1:02}. {nome_old}')

# lst_extraidos = [scraper.normalizar_nome(x.get('Identificação')['Nome']) for x in dict_list_docents]
# for i in dict_list_docents_old:
#     nome_old = scraper.normalizar_nome(i.get('Identificação')['Nome'])
#     if nome_old not in lst_extraidos and nome_old in [scraper.normalizar_nome(x) for x in lista_busca]:
#         print(f"  Recuperado: {nome_old}")        
#         dict_list_docents.append(i)

# print(f"\n{len(dict_list_docents)} currículos carregados na lista de dicionários")
# termos_busca = ['Fiocruz', 'Fundação Oswaldo Cruz', 'Biotecnologia', 'RENORBIO', 'saúde']
# scraper = LattesScraper(termos_busca, 'bolt://localhost:7687', 'neo4j', 'password', only_doctors=False)
# lista_restante = scraper.avaliar_remanescentes(lista_busca, dict_list_docents)
# print(f'\nBusca por {len(lista_busca)} nomes com extração de dados de {len(dict_list_docents)} dicionários')

### Adicionar nomes/termos, se necessário

In [15]:
# ciipf = ['Caroline Pereira Bittencourt Passaes',
# 'Ana Carolina Matias Dinelly Pinto',
# 'Clarissa Perdigao Mello Ferraz',
# 'Júlio César Martins Ximenes']

# for i in ciipf:
#     if i not in lista_restante:
#         lista_restante.append(i)
# for j in lista_restante:
#     print(f'   {j}')

In [16]:
# lista_restante.remove('clarissa perdigao melo')
# lista_restante.remove('christiane franca martins teodoro')
# lista_restante.remove('elaine silva nascimento')

In [17]:
# lista_restante.append('clarissa perdigao mello ferraz')
# lista_restante.append('christiane franca martins')
# lista_restante.append('elaine silva nascimento andrade')
lista_restante

['christiane franca martins', 'helcio silva dos santos']

In [18]:
termos_busca.append('Ceará')
termos_busca.append('Farmacêuticas')

### Extrair currículos remanescentes ou adicionais

In [19]:
# lista_dict_combinado = extract_remanescents(lista_restante, dict_list_actual)
lista_dict_combinado = scraper.extract_remanescents(lista_restante, dict_list_docents, termos_busca)
filepath = os.path.join(folder_data_input,'dict_list_docents.json')

Resta extrair 2 currículos:
['christiane franca martins', 'helcio silva dos santos']
--------------------------------------------------------------------------------------------------------------
Buscando currículos com qualquer nível de formação
 1/2: christiane franca martins
        2 currículos homônimos: christiane franca martins
                         Fiocruz | False | ['Christiane França Martins  Doutorado em Ciências Farmacêuticas pela Universidade Federal de Goiás, Brasil(2022)']
           Fundação Oswaldo Cruz | False | ['Christiane França Martins  Doutorado em Ciências Farmacêuticas pela Universidade Federal de Goiás, Brasil(2022)']
                   Biotecnologia | False | ['Christiane França Martins  Doutorado em Ciências Farmacêuticas pela Universidade Federal de Goiás, Brasil(2022)']
                        RENORBIO | False | ['Christiane França Martins  Doutorado em Ciências Farmacêuticas pela Universidade Federal de Goiás, Brasil(2022)']
                           

In [20]:
print(f'{len(lista_dict_combinado)} currículos extraídos')
print('\n\nExemplo de dados dos artigos:')
[x.get('Produções') for x in lista_dict_combinado][0].get('Artigos completos publicados em periódicos')[0]

62 currículos extraídos


Exemplo de dados dos artigos:


{'ano': '2021',
 'fator_impacto_jcr': '',
 'ISSN': '20452322',
 'titulo': 'SARS-CoV-2 genomic surveillance in Rondônia, Brazilian Western Amazon',
 'revista': 'Scientific Reports',
 'autores': 'BOTELHO-SOUZA, LUAN FELIPO2021BOTELHO-SOUZA, LUAN FELIPO ; NOGUEIRA-LIMA, FELIPE SOUZA ; ROCA, TÁRCIO PEIXOTO ; NAVECA, FELIPE GOMES ; DE OLIVERIA DOS SANTOS, ALCIONE ; MAIA, ADRIANA CRISTINA SALVADOR ; DA SILVA, CICILEIA CORREIA ; DE MELO MENDONÇA, ALINE LINHARES FERREIRA ; LUGTENBURG, CELINA APARECIDA BERTONI ; AZZI, CAMILA FLÁVIA GOMES ; FONTES, JULIANA LOCA FURTADO ; CAVALCANTE, SUELEN ; DE CÁSSIA PONTELLO RAMPAZZO, RITA ; SANTOS, CAIO HENRIQUE NEMETH ;DI SABATINO GUIMARÃES, ALICE PAULA; MÁXIMO, FERNANDO RODRIGUES ; VILLALOBOS-SALCEDO, JUAN MIGUEL ; VIEIRA, DEUSILENE SOUZA . ',
 'data_issn': '20452322',
 'DOI': 'http://dx.doi.org/10.1038/s41598-021-83203-2'}

### Atualizar Qualis Periódicos pela Plataforma Sucupira

In [21]:
## JÁ INCLUIDO NO MÉTODO DE SALVAMENTO

# from lattes_scrapper import GetQualis
# stratifier = GetQualis()

# # Definir caminho e nome para escrever o arquivo com dados periódicos qualis dos docentes
# print('\nAdicionando Qualis Periódicos')
# pathfilename = os.path.join(folder_data_input,'docents_dict_list.json')

# # Atualizar a lista de dicionários dict_list_docents com o Qualis para cara Artigo
# stratifier.buscar_qualis_e_atualizar_arquivo(lista_dict_combinado, pathfilename)

In [22]:
# lista_dict_combinado

In [23]:
# # Confirmar se a chave 'Qualis' foi adicionada ao dicionário dos Artigos em dict_list_docents
# [x.get('Produções') for x in lista_dict_combinado][0].get('Artigos completos publicados em periódicos')[0]

### Salvar dados de currículos de Docentes

In [25]:
from lattes_scrapper import GetQualis
stratifier = GetQualis()

# Acrescentar Qualis periódicos aos dicionários de docentes
print('\nAdicionando Qualis Periódicos')
pathfilename = os.path.join(folder_data_input,'docents_dict_list.json')
stratifier.buscar_qualis_e_atualizar_arquivo(lista_dict_combinado, pathfilename)
scraper.save_to_json(lista_dict_combinado, pathfilename)

print(f'{len(lista_dict_combinado)} dicionários com currículos completos extraídos')
print('\n\nExemplo de dados dos artigos:')
[x.get('Produções') for x in lista_dict_combinado][0].get('Artigos completos publicados em periódicos')[0]

62 dicionários com currículos completos extraídos


Exemplo de dados dos artigos:


{'ano': '2021',
 'fator_impacto_jcr': '',
 'ISSN': '20452322',
 'titulo': 'SARS-CoV-2 genomic surveillance in Rondônia, Brazilian Western Amazon',
 'revista': 'Scientific Reports',
 'autores': 'BOTELHO-SOUZA, LUAN FELIPO2021BOTELHO-SOUZA, LUAN FELIPO ; NOGUEIRA-LIMA, FELIPE SOUZA ; ROCA, TÁRCIO PEIXOTO ; NAVECA, FELIPE GOMES ; DE OLIVERIA DOS SANTOS, ALCIONE ; MAIA, ADRIANA CRISTINA SALVADOR ; DA SILVA, CICILEIA CORREIA ; DE MELO MENDONÇA, ALINE LINHARES FERREIRA ; LUGTENBURG, CELINA APARECIDA BERTONI ; AZZI, CAMILA FLÁVIA GOMES ; FONTES, JULIANA LOCA FURTADO ; CAVALCANTE, SUELEN ; DE CÁSSIA PONTELLO RAMPAZZO, RITA ; SANTOS, CAIO HENRIQUE NEMETH ;DI SABATINO GUIMARÃES, ALICE PAULA; MÁXIMO, FERNANDO RODRIGUES ; VILLALOBOS-SALCEDO, JUAN MIGUEL ; VIEIRA, DEUSILENE SOUZA . ',
 'data_issn': '20452322',
 'DOI': 'http://dx.doi.org/10.1038/s41598-021-83203-2',
 'Qualis': 'A1'}

## <b>F01b: Ler dados salvos</b>

### Listar arquivos JSON gerados

In [1]:
import os

folder_data_input = os.path.join(os.getcwd(),'_data','in_csv')
os.listdir(folder_data_input)

['categorias_capes.txt',
 'classe_artigos_completos.txt',
 'classificações_publicadas_todas_as_areas_avaliacao1672761192111.xlsx',
 'cnpq_tabela-areas-conhecimento.pdf',
 'combined_dict_list.json',
 'dict_list_discents_combined.json',
 'dict_list_temp.json',
 'discents_dict_list.json',
 'docentes_farmacologia.csv',
 'docents_dict_list.json',
 'docents_dict_list_202407.json',
 'docents_dict_list_old.json',
 'docents_dict_list_old2.json',
 'docents_farmacology_dict_list.json',
 'escalas_quantica-cosmologica.txt',
 'gii_history_data.csv',
 'indicadores.csv',
 'LISTA DOS NOMES DOS ORIENTADORES DOS PROJETOS INSCRITOS PAR BOLSA FUNCAP 2024.docx',
 'mermaid_modelo_pesqusia.txt',
 'Modelo_hipergrafo_dinâmico.txt',
 'nomesdocentes.csv',
 'portal_fiocruz_tecnologias.csv',
 'ppgcs',
 'prompts_hardware.txt',
 'qlattes',
 'temp_dict_list.json',
 'veiculos.csv']

In [2]:
from pathlib import Path
from getpass import getpass
from datetime import datetime
from IPython.display import clear_output
import pandas as pd, os, re, sys, time, pytz, json, subprocess
pd.set_option('display.max_colwidth', None)
pd.set_option('colheader_justify', 'left')
pd.set_option('display.max_rows', 600)

def find_repo_root(path='.', depth=10):
    ''' 
    Busca o arquivo .git e retorna string com a pasta raiz do repositório
    '''
    # Limitar profundidade para evitar loop infinito
    if depth < 0:
        return None
    path = Path(path).absolute()
    if (path / '.git').is_dir():
        return path
    return find_repo_root(path.parent, depth-1)

## Definir a pasta de base do repositório local
base_repo_dir = find_repo_root()

## Sempre construir os caminhos usando os.path.join para compatibilidade WSL e Linux
folder_utils = os.path.join(base_repo_dir, 'utils')
folder_domain = os.path.join(base_repo_dir, 'source', 'domain')
folder_data_input = os.path.join(base_repo_dir, '_data', 'in_csv')
folder_data_output = os.path.join(base_repo_dir, '_data', 'output')
sys.path.append(folder_utils)
sys.path.append(folder_domain)

from environment_setup import EnvironmentSetup
from chromedriver_manager import ChromeDriverManager
from lattes_scrapper import JSONFileManager, LattesScraper, HTMLParser, SoupParser, GetQualis, ArticlesCounter, DiscentCollaborationCounter, DictToHDF5, attribute_to_be_non_empty
from neo4j_persister import Neo4jPersister
# from scraper_sucupira_edge import SucupiraScraperEdge
# from scraper_sucupira import SucupiraScraper
# from scraper_pasteur import PasteurScraper

# Carregar para variável dict_list_docents os dicionários com dados dos Docentes
jfm = JSONFileManager()
jfm.list_json(folder_data_input)
filename = 'docents_dict_list.json'

dict_list_docents, formatted_creation_date, formatted_modification_date, time_count, unit = jfm.load_from_json(os.path.join(folder_data_input,filename))
print(f"\n{len(dict_list_docents)} currículos carregados na lista de dicionários '{filename}'")
print(f"Arquivo criado inicialmente em {formatted_creation_date} carregado com sucesso")
print(f"Extração realizada em {formatted_modification_date} a {time_count} {unit}")

Arquivos disponíveis na pasta para dados de entrada:
  combined_dict_list.json
  dict_list_discents_combined.json
  dict_list_temp.json
  discents_dict_list.json
  docents_dict_list.json
  docents_dict_list_202407.json
  docents_dict_list_old.json
  docents_dict_list_old2.json
  docents_farmacology_dict_list.json
  temp_dict_list.json

62 currículos carregados na lista de dicionários 'docents_dict_list.json'
Arquivo criado inicialmente em 23/07/2024 22:55:20 carregado com sucesso
Extração realizada em 30/07/2024 22:05:08 a 2.8 dias


### Visualizar nomes extraídos

In [3]:
jfm = JSONFileManager()

filename = 'docents_dict_list.json'
pathfilename = os.path.join(folder_data_input, filename)
dict_list_docents_complete, formatted_creation_date, formatted_modification_date, time_count, unit = jfm.load_from_json(pathfilename)
lista_nomes_extraidos = [i.get('Identificação').get('Nome') for i in dict_list_docents_complete]

print(f'{len(lista_nomes_extraidos)} currículos extraídos')
lista_nomes_extraidos

62 currículos extraídos


['Alice Paula Di Sabatino Guimarães',
 'Ana Cláudia de Araújo Teixeira',
 'Ana Camila Oliveira Alves',
 'Adriana Costa Bacelo',
 'Anna Carolina Machado Marinho',
 'Antonio Marcos Aires Barbosa',
 'Anya Pimentel Gomes Fernandes Vieira Meyer',
 'Carla Freire Celedonio Fernandes',
 'Claudia Stutz Zubieta',
 'Clarissa Romero Teixeira',
 'Dayane Alves Costa',
 'Donat Alexander de Chapeaurouge',
 'Eduardo Ruback dos Santos',
 'Fabio Miyajima',
 'Fernando Braga Stehling Dias',
 'Fernando Ferreira Carneiro',
 'Galba Freire Moita',
 'Giovanny Augusto Camacho Antevere Mazzarotto',
 'Gilvan Pessoa Furtado',
 'Ivana Cristina de Holanda Cunha Barreto',
 'Jaime Ribeiro Filho',
 'João Hermínio Martins da Silva',
 'José Luís Passos Cordeiro',
 'Luiz Odorico Monteiro de Andrade',
 'Marcela Helena Gambim Fonseca',
 'Marcos Roberto Lourenzoni',
 'Márcio Flávio Moura de Araújo',
 'Margareth Borges Coutinho Gallo',
 'Marlos de Medeiros Chaves',
 'Maximiliano Ponte',
 'Raphael Trevizani',
 'Regis Bernardo B

### Visualizar quantitativo de artigos extraídos

In [4]:
## Contagem de artigos para simples confererência
print(f'{len(dict_list_docents)} dicionários montados')
qte_artigos=0
qte_titulos=0
for k,i in enumerate(dict_list_docents):
    try:
        qte_jcr = len(i.get('Produções').get('Artigos completos publicados em periódicos'))
    except:
        qte_jcr = 0
    try:
       qte_jcr2 = len(i['JCR2'])
    except:
       qte_jcr2 = 0
    qte_artigos+=qte_jcr
    qte_titulos+=qte_jcr2
    status=qte_jcr2-qte_jcr
    print(f"{k:>2}C {qte_jcr:>03}A {qte_jcr2:>03}T Dif:{status:>03} {i.get('Identificação').get('name')} ")

print(f'\nTotal de artigos em todos períodos: {qte_artigos}')
print(f'Total de títulos em todos períodos: {qte_titulos}')

62 dicionários montados
 0C 002A 002T Dif:000 None 
 1C 009A 009T Dif:000 None 
 2C 002A 002T Dif:000 None 
 3C 025A 025T Dif:000 None 
 4C 010A 010T Dif:000 None 
 5C 002A 002T Dif:000 None 
 6C 105A 105T Dif:000 None 
 7C 049A 049T Dif:000 None 
 8C 007A 007T Dif:000 None 
 9C 045A 045T Dif:000 None 
10C 010A 010T Dif:000 None 
11C 043A 043T Dif:000 None 
12C 006A 006T Dif:000 None 
13C 064A 064T Dif:000 None 
14C 023A 023T Dif:000 None 
15C 066A 066T Dif:000 None 
16C 011A 011T Dif:000 None 
17C 012A 012T Dif:000 None 
18C 026A 026T Dif:000 None 
19C 074A 074T Dif:000 None 
20C 109A 109T Dif:000 None 
21C 029A 029T Dif:000 None 
22C 045A 045T Dif:000 None 
23C 087A 087T Dif:000 None 
24C 020A 020T Dif:000 None 
25C 028A 028T Dif:000 None 
26C 149A 149T Dif:000 None 
27C 018A 018T Dif:000 None 
28C 007A 007T Dif:000 None 
29C 045A 045T Dif:000 None 
30C 004A 004T Dif:000 None 
31C 042A 042T Dif:000 None 
32C 061A 061T Dif:000 None 
33C 096A 096T Dif:000 None 
34C 054A 054T Dif:000 No

## Contar artigos e data de atualização dos currículos

In [5]:
# [x.get('Produções') for x in dict_list_docents][3].keys()

In [6]:
atualizador = ArticlesCounter(dict_list_docents)
dtf_atualizado = atualizador.extrair_data_atualizacao(dict_list_docents)
dtf_atualizado

id_lattes         curriculos                                      
0   8793885517658468             Alice Paula Di Sabatino Guimarães  \
1   4719434295908748                Ana Cláudia de Araújo Teixeira   
2   3711456559794028                     Ana Camila Oliveira Alves   
3   8861663346303670                          Adriana Costa Bacelo   
4   7628730583729553                 Anna Carolina Machado Marinho   
5   7085533025242495                  Antonio Marcos Aires Barbosa   
6   7659758489387356    Anya Pimentel Gomes Fernandes Vieira Meyer   
7   3922481112087617              Carla Freire Celedonio Fernandes   
8   9103171701657660                         Claudia Stutz Zubieta   
9   5208987549081354                      Clarissa Romero Teixeira   
10  3737057462808079                            Dayane Alves Costa   
11  3279548172969453               Donat Alexander de Chapeaurouge   
12  6386175381185758                     Eduardo Ruback dos Santos   
13  0998235420634887                                Fabio Miyajima   
14  1210738427769812                  Fernando Braga Stehling Dias   
15  8414094465792735                    Fernando Ferreira Carneiro   
16  9365792416334714                            Galba Freire Moita   
17  4491426793431771  Giovanny Augusto Camacho Antevere Mazzarotto   
18  4259673144880085                         Gilvan Pessoa Furtado   
19  0926082188345417       Ivana Cristina de Holanda Cunha Barreto   
20  5885477643638071                           Jaime Ribeiro Filho   
21  4614096538855002                João Hermínio Martins da Silva   
22  3430534497997843                     José Luís Passos Cordeiro   
23  4138758876612437              Luiz Odorico Monteiro de Andrade   
24  9063434685117456                 Marcela Helena Gambim Fonseca   
25  1350673719062370                     Marcos Roberto Lourenzoni   
26  3560955068874194                 Márcio Flávio Moura de Araújo   
27  2733793442953892               Margareth Borges Coutinho Gallo   
28  5961912954763405                     Marlos de Medeiros Chaves   
29  7890789338463575                             Maximiliano Ponte   
30  7223174055569374                             Raphael Trevizani   
31  2521004210048823                  Regis Bernardo Brandim Gomes   
32  0447073555893530                              Roberto Nicolete   
33  6831739238509460       Roberto Wagner Júnior Freire de Freitas   
34  0636763091396917               Sharmênia de Araújo Soares Nuto   
35  9013874934045331                           Vanira Matos Pessoa   
36  9284843601128833               Venúcia Bruna Magalhães Pereira   
37  6908395306417399                   Fernanda Savicki de Almeida   
38  9647606420923547             Ana Carolina Matias Dinelly Pinto   
39  2651140454673862                     Geraldo Rodrigues Sartori   
40  2139438003787249               Elaine Silva Nascimento Andrade   
41  3339883916812154                         Cecili Barrozo Mendes   
42  3560074724328069                         Ketlen Christine Ohse   
43  3966193953515177                Clarissa Perdigao Mello Ferraz   
44  0112236864523667                      Allysson Allan de Farias   
45  0431255933614473                   Júlio César Martins Ximenes   
46  1499537335717268                      Wallady da Silva Barroso   
47  2391601741443755                        Lucas Lima de Carvalho   
48  7110258791537662                Manuel Alves dos Santos Júnior   
49  5648585816153564               Valdir Ferreira de Paula Junior   
50  5324733625643254                Felipe Augusto Rocha Rodrigues   
51  6272502717173789                          Talita Abrante Leite   
52  3010146839394113      Fátima de Cássia Evangelista de Oliveira   
53  4154148778084155                         Rodolfo de Melo Nunes   
54  3057934708334626                Ana Karine Rocha de Melo Leite   
55  1853562744182714           Conceição da Silva Martins Rebouças   
56  043670098

In [7]:
## Verificar as chaves disponíveis em cada dicionário
# for i,j in enumerate(dict_list_docents):
#     print(f'{i:02} {j.keys()}')

## Ver dados da planilha da plataforma Sucupira com dados de todo Qualis Periódicos
# fonte_planilha = 'classificações_publicadas_todas_as_areas_avaliacao1672761192111.xlsx'
# dados_qualis = pd.read_excel(os.path.join(LattesScraper.find_repo_root(),'_data','in_xls',fonte_planilha))
# dados_qualis

# <b>F02: Avaliar pontuação currículos de Orientadores</b>

## Produções dentro do Período 2020 a 2024

Calcular conforme os seguintes indicadores:

### 1. Artigos Publicados em Periódicos	Pontuação

- Fator de Impacto JCR ≥ 1,01	                      x 8 pontos
- Fator de Impacto JCR entre 0,51 e 1,0	              x 6 pontos
- Inclusão na base de dados Scielo	                  x 1 ponto
- Inclusão na base de dados Web of Science ou Pubmed  x 2 pontos

Obs: Artigos incluídos em mais de uma base cientifica recebem 2 pontos relativos a maior pontuação, sem acúmulo.

### 2. Trabalhos Publicados em Eventos Científicos	Pontuação

- Resumo Estendido/ Artigo Completo (teto 5 trabalhos) x 2 pontos
- Resumo Simples (teto 10 trabalhos)	               x 1 ponto

### 3. Livros	

- Livro Publicado com ISBN (mínimo 80 páginas)	       x 3 pontos
- Organização de Livro	                               x 3 pontos
- Capítulo de Livro	                                   x 2 pontos

### 4. Softwares e Patentes	

- Registro de Softwares		                           x 2 pontos
- Pedido de patente depositada no INPI	               x 3 pontos
- Pedido de patente deferido pelo INPI	               x 4 pontos

### 5. Orientações Concluídas	

- Tese de Doutorado	                                   x 2 pontos
- Dissertação de Mestrado	                           x 2 pontos
- TCC (teto 10 TCCs)	                               x 1 ponto

### 6. Orientações Concluídas de IC	

- PIBIC/PIBIT/FUNCAP/CNPq	                           x 1 ponto


## Avaliar pontuações para Edital 2024/01 Fiocruz Ceará

In [8]:
# Definir os anos do período de interesse
ano_inicio = 2020
ano_final = 2024

## Definir a lista de orientadores que se inscreveram no Edital
orientadores = [
    'JAIME RIBEIRO FILHO',
    'REGIS BERNARDO BRANDIM GOMES',
    'FABIO MIYAJIMA',
    'ROBERTO NICOLETE',
    'MARCOS ROBERTO LOURENZONI',
    'JOÃO HERMINIO MARTINS DA SILVA',
    'ANA CAROLINA MATIAS DINELLY PINTO',
    'GILVAN PESSOA FURTADO',
    'GERALDO RODRIGUES SARTORI',
    'ELAINE SILVA NASCIMENTO ANDRADE',
    'CECILI BARROZO MENDES',
    'CHRISTIANE FRANÇA MARTINS',
    'KETLEN CHRISTINE OHSE',
    'CLARISSA PERDIGÃO MELLO FERRAZ',
    'ALLYSSON ALLAN DE FARIAS',
    'JÚLIO CESAR MARTINS XIMENES',
    'DONAT ALEXANDER DE CHAPEAUROUGE',
    'ADRIANA COSTA BACELO',
]

df_geral, df_orientadores = atualizador.calcular_pontuacoes(dict_list_docents, ano_inicio, ano_final, orientadores_filtro=orientadores)
print(f'Apuração da pontuação nos currículos de orientadores, conforme Edital 2024/01 Fiocruz Ceará, referente produções dentro do período {ano_inicio} a {ano_final}')
df_orientadores

Apuração da pontuação nos currículos de orientadores, conforme Edital 2024/01 Fiocruz Ceará, referente produções dentro do período 2020 a 2024


Somatório_Pontos  Pnt_Artigos   
Jaime Ribeiro Filho                609.0             592.0        \
Roberto Nicolete                   219.0             184.0         
Fabio Miyajima                     183.0             168.0         
Ana Carolina Matias Dinelly Pinto  152.0             144.0         
Joao Herminio Martins da Silva     129.0             112.0         
Marcos Roberto Lourenzoni          110.0              88.0         
Regis Bernardo Brandim Gomes       100.0              88.0         
Geraldo Rodrigues Sartori           88.0              72.0         
Gilvan Pessoa Furtado               84.0              72.0         
Christiane Franca Martins           47.0              46.0         
Adriana Costa Bacelo                42.0              38.0         
Cecili Barrozo Mendes               40.0              40.0         
Elaine Silva Nascimento Andrade     40.0              40.0         
Allysson Allan de Farias            35.0              24.0         
Clarissa Perdigao Mello Ferraz      32.0              32.0         
Julio Cesar Martins Ximenes         12.0               8.0         
Ketlen Christine Ohse                3.0               0.0         
Donat Alexander de Chapeaurouge      0.0               0.0         

                                   Pnt_Orientações  Pnt_Public.Congressos   
Jaime Ribeiro Filho                17.0             0.0                    \
Roberto Nicolete                   24.0             0.0                     
Fabio Miyajima                     11.0             0.0                     
Ana Carolina Matias Dinelly Pinto   8.0             0.0                     
Joao Herminio Martins da Silva     13.0             0.0                     
Marcos Roberto Lourenzoni          22.0             0.0                     
Regis Bernardo Brandim Gomes       12.0             0.0                     
Geraldo Rodrigues Sartori          16.0             0.0                     
Gilvan Pessoa Furtado              12.0             0.0                     
Christiane Franca Martins           1.0             0.0                     
Adriana Costa Bacelo                4.0             0.0                     
Cecili Barrozo Mendes               0.0             0.0                     
Elaine Silva Nascimento Andrade     0.0             0.0                     
Allysson Allan de Farias           11.0             0.0                     
Clarissa Perdigao Mello Ferraz      0.0             0.0                     
Julio Cesar Martins Ximenes         4.0             0.0                     
Ketlen Christine Ohse               3.0             0.0                     
Donat Alexander de Chapeaurouge     0.0             0.0                     

                                   Pnt_Livros/Capítulos  Pnt_Patentes   
Jaime Ribeiro Filho                0.0                    0.0          \
Roberto Nicolete                   0.0                   11.0           
Fabio Miyajima                     0.0                    4.0           
Ana Carolina Matias Dinelly Pinto  0.0                    0.0           
Joao Herminio Martins da Silva     0.0                    4.0           
Marcos Roberto Lourenzoni          0.0                    0.0           
Regis Bernardo Brandim Gomes       0.0                    0.0           
Geraldo Rodrigues Sartori          0.0                    0.0           
Gilvan Pessoa Furtado              0.0                    0.0           
Christiane Franca Martins          0.0                    0.0           
Adriana Costa Bacelo               0.0                    0.0           
Cecili Barrozo Mendes              0.0                    0.0           
Elaine Silva Nascimento Andrade    0.0                    0.0           
Allysson Allan de Farias           0.0                    0.0           
Clarissa Perdigao Mello Ferraz     0.0                    0.0           
Julio Cesar Martins Ximenes        0.0                    0.0           
Ketlen Christine Ohse              0.

In [9]:
print(f'Apuração geral de pontuação conforme Edital 2024/01 Fiocruz Ceará referente produções dentro do período {ano_inicio} a {ano_final}')
df_geral

Apuração geral de pontuação conforme Edital 2024/01 Fiocruz Ceará referente produções dentro do período 2020 a 2024


Somatório_Pontos  Pnt_Artigos   
Helcio Silva dos Santos                       1438.0            1356.0       \
Jaime Ribeiro Filho                            609.0             592.0        
Marcio Flavio Moura de Araujo                  355.0             340.0        
Rodolfo de Melo Nunes                          300.0             280.0        
Anya Pimentel Gomes Fernandes Vieira Meyer     275.0             262.0        
Roberto Wagner Junior Freire de Freitas        219.0             206.0        
Roberto Nicolete                               219.0             184.0        
Isaac Moura Araujo                             217.0             216.0        
Maria Francilene Souza Silva                   208.0             202.0        
Fabio Miyajima                                 183.0             168.0        
Fatima de Cassia Evangelista de Oliveira       158.0             154.0        
Luiz Odorico Monteiro de Andrade               158.0             124.0        
Carla Freire Celedonio Fernandes               152.0             142.0        
Ana Carolina Matias Dinelly Pinto              152.0             144.0        
Anita Oliveira Brito Pereira Bezerra Martins   150.0             144.0        
Ivana Cristina de Holanda Cunha Barreto        148.0             102.0        
Conceicao da Silva Martins Reboucas            136.0             128.0        
Sharmenia de Araujo Soares Nuto                130.0             120.0        
Fernando Ferreira Carneiro                     130.0             118.0        
Joao Herminio Martins da Silva                 129.0             112.0        
Marcos Roberto Lourenzoni                      110.0              88.0        
Marcela Helena Gambim Fonseca                  104.0             104.0        
Regis Bernardo Brandim Gomes                   100.0              88.0        
Geraldo Rodrigues Sartori                       88.0              72.0        
Jose Luis Passos Cordeiro                       86.0              86.0        
Gilvan Pessoa Furtado                           84.0              72.0        
Felipe Augusto Rocha Rodrigues                  76.0              64.0        
Fernando Braga Stehling Dias                    74.0              64.0        
Maximiliano Ponte                               65.0              56.0        
Vanira Matos Pessoa                             62.0              48.0        
Anna Carolina Machado Marinho                   49.0              48.0        
Christiane Franca Martins                       47.0              46.0        
Adriana Costa Bacelo                            42.0              38.0        
Valdir Ferreira de Paula Junior                 40.0              40.0        
Cecili Barrozo Mendes                           40.0              40.0        
Elaine Silva Nascimento Andrade                 40.0              40.0        
Clarissa Romero Teixeira                        40.0              40.0        
Allysson Allan de Farias                        35.0              24.0        
Claudia Stutz Zubieta                           32.0              32.0        
Eduardo Ruback dos Santos                       32.0              32.0        
Clarissa Perdigao Mello Ferraz                  32.0              32.0        
Ana Claudia de Araujo Teixeira                  24.0              16.0        
Giovanny Augusto Camacho Antevere Mazzarotto    24.0              16.0        
Antonio Marcos Aires Barbosa                    20.0               8.0        
Ana Karine Rocha de Melo Leite                  19.0               0.0        
Ana Camila Oliveira Alves                       16.0              16.0        
Dayane Alves Costa                              16.0              16.0        
Julio Cesar Martins Ximenes                     12.0               8.0        
Manuel Alves dos Santos Junior                  12.0               8.0        
Talita Abrante Leite                            11.0               8.0        
Venucia Bruna Mag

# <b>F03: Avaliar áreas de atuação e especialidade

## Obter as áreas de atuação de cada orientador/docente

In [10]:
dicionarios_interesse = [
    'Identificação', 
    'Idiomas',
    'Formação',
    'Atuação Profissional',
    'Linhas de Pesquisa',
    ]

## Ver detalhes de forma recursiva em uma determinada estrutura de dados em dicionários aninhados
def avaliar_tipo_instancias_arvore(estrutura_dados, nivel=1, identacao=""):
    """
    Função recursiva que avalia o tipo e a quantidade de instâncias em cada nível da estrutura de dados, exibindo-a em formato de árvore.

    Args:
        estrutura_dados (list|dict): A estrutura de dados a ser avaliada.
        nivel (int): Nível atual da recurssão (inicia em 1).
        identacao (str): String de indentação para cada nível (inicia vazia).

    Returns:
        None: A função imprime os resultados na tela e não retorna nada.
    """

    if isinstance(estrutura_dados, list):
        print(f"{identacao}N{nivel}. Lista: {len(estrutura_dados)} elementos")
        for item in estrutura_dados:
            avaliar_tipo_instancias_arvore(item, nivel + 1, identacao + "    ")

    elif isinstance(estrutura_dados, dict):
        print(f"{identacao}N{nivel}. Mapa: {estrutura_dados.keys()}")
        for chave, valor in estrutura_dados.items():
            print(f"{identacao}  {chave}:")
            avaliar_tipo_instancias_arvore(valor, nivel + 1, identacao + "    ")

    elif isinstance(estrutura_dados, str):
        print(f"{identacao}N{nivel}. String: {estrutura_dados}")

## Ver somente chaves de subdicionário de segundo nível na chave de primeiro nível e dicionário passado como parâmetro
from pprint import pprint

def contar_subchaves(dict_list_docents, chave_dicionario):
    qte_maxsubkeys=0
    max_subkeys=[]
    for n,j in enumerate([x.get(chave_dicionario).keys() for x in dict_list_docents]):
        nome = dict_list_docents[n].get(chave_dicionario).get(subchave_dicionario)
        max_subkeys.append((n, len(list(j))))
        if len(list(j)) >= qte_maxsubkeys:
            qte_maxsubkeys = len(list(j))
            curriculo_maxsubkeys = dict_list_docents[n].get('Identificação').get('Nome')
    print(max_subkeys)
    return curriculo_maxsubkeys, qte_maxsubkeys

def ver_subchaves(dict_list_docents, chave_dicionario):
    for n,j in enumerate([x.get(chave_dicionario).keys() for x in dict_list_docents]):
        nome = dict_list_docents[n].get('Identificação').get('Nome')
        print('-'*125)
        print(nome)
        pprint(list(j))

def ver_conteudo_lista(dict_list_docents, chave_dicionario):
    for n,j in enumerate([x.get(chave_dicionario) for x in dict_list_docents]):
        nome = dict_list_docents[n].get('Identificação').get('Nome')
        print('-'*125)
        print(nome)
        pprint(list(j), width=125)

In [11]:
# Varrer cada dicionário na lista de dicionários carregada do arquivo de extração salvo localmente
# for dict_pesq in dict_list_docents[:3]:
#     avaliar_tipo_instancias_arvore(dict_pesq)

In [12]:
curriculo_maxsubkeys, qte_maxsubkeys = contar_subchaves(dict_list_docents)

NameError: name 'chave_dicionario' is not defined

In [51]:
curriculo_maxsubkeys

'Ivana Cristina de Holanda Cunha Barreto'

In [46]:
dict_list_docents[17].get('Identificação').get('Nome')

'Giovanny Augusto Camacho Antevere Mazzarotto'

In [67]:
dict_list_docents[19].get('Linhas de Pesquisa')

[{'Descrição': 'Tecnologias para a Estratégia Saúde da Família',
  'Detalhes': ''},
 {'Descrição': 'Estratégias de Educação Permanente e desenvolvimento profissional em Sistemas de Saúde',
  'Detalhes': ''},
 {'Descrição': 'Saúde Digital', 'Detalhes': ''},
 {'Descrição': 'Saúde Digital', 'Detalhes': ''},
 {'Descrição': 'Estratégia Saúde da Família', 'Detalhes': ''},
 {'Descrição': 'Tecnologias para a Estratégia Saúde da Família',
  'Detalhes': ''}]

In [73]:
dict_list_docents[19].get('Atuação Profissional')

[{'Instituição': 'Fundação Osvaldo Cruz, FIOCRUZ CE, Brasil.',
  'Ano': '2019 - Atual',
  'Descrição': '',
  'Outras informações': 'Vínculo: , Enquadramento Funcional:'},
 {'Instituição': 'Instituto Atlântico, IA, Brasil.',
  'Ano': '2018 - 2020',
  'Descrição': '',
  'Outras informações': 'Vínculo: Consultora, Enquadramento Funcional: Consultora, Carga horária: 10'},
 {'Instituição': 'Fundação Oswaldo Cruz, FIOCRUZ, Brasil.',
  'Ano': '2015 - Atual',
  'Descrição': '',
  'Outras informações': 'Vínculo: Servidor Público, Enquadramento Funcional: Especialista em C&T Prod. Inov. em Saúde, Carga horária: 40 Linhas de pesquisa em Saúde Digital e Estratégia Saúde da Família'},
 {'Instituição': 'Fundação Oswaldo Cruz, FIOCRUZ, Brasil.',
  'Ano': '03/2017 - Atual',
  'Descrição': '',
  'Outras informações': 'Ensino, MESTRADO PROFISSIONAL EM SAÚDE DA FAMÍLIA - RENASF/MPSF, Nível: Pós-Graduação Disciplinas ministradas Atenção Integral Seminários Atenção e Gestão Educação em Saúde I Gestão do Pr

In [95]:
from datetime import datetime
from dateutil.parser import parse

def calcular_tempo_atuacao(dados_profissionais):
    """Calcula o tempo de atuação em cada instituição e destaca as atuações em curso.

    Args:
        dados_profissionais: Lista de dicionários com dados de atuações profissionais.

    Returns:
        Um dicionário com o tempo de atuação total em cada instituição e as atuações em curso.
    """

    tempo_atuacao = {}
    atuacoes_em_curso = []
    ano_corrente = datetime.now().year

    for atuacao in dados_profissionais:
        instituicao = atuacao['Instituição']
        ano = atuacao['Ano']

        # Substitui "Atual" pelo ano corrente
        if "Atual" in ano:
            ano = ano.replace("Atual", str(ano_corrente))

        try:
            inicio, fim = map(parse, ano.split(' - '))
        except ValueError:
            try:
                inicio, fim = map(lambda x: datetime.strptime(x, "%Y"), ano.split(' - '))
            except ValueError:
                print(f"Aviso: Formato de data inválido em '{ano}'. Pulando...")
                continue

        em_curso = "Atual" in atuacao['Ano']  # Verifica se a atuação está em curso

        tempo_total = (fim.year - inicio.year) * 12 + (fim.month - inicio.month) + 1
        tempo_atuacao[instituicao] = tempo_atuacao.get(instituicao, 0) + tempo_total // 12

        if em_curso:
            atuacoes_em_curso.append(f"{instituicao} ({inicio.year} - Atual)")

    return tempo_atuacao, atuacoes_em_curso

# Dicionário para armazenar o tempo total em cada instituição
tempo_atuacao_total = {}
# Lista para armazenar as atuações em curso
atuacoes_em_curso_total = []

# Itera sobre os dicionários em dict_list_docents
for entrada in dict_list_docents:
    if isinstance(entrada, dict) and 'Identificação' in entrada and 'Atuação Profissional' in entrada:
        nome = entrada['Identificação']['Nome']
        dados_profissionais = entrada['Atuação Profissional']

        # Se dados_profissionais não for uma lista, transforma em lista
        if not isinstance(dados_profissionais, list):
            dados_profissionais = [dados_profissionais]

        tempo_atuacao, atuacoes_em_curso = calcular_tempo_atuacao(dados_profissionais)

        # Imprime o nome da pessoa
        print(nome)
        print()  # Adiciona uma linha em branco

        # Imprime o tempo de atuação em cada instituição
        print("Tempo de atuação em cada instituição:")
        for instituicao, tempo in tempo_atuacao.items():
            print(f"- {instituicao}: {tempo} anos")

        # Imprime as atuações em curso
        print("\nAtuações em curso:")
        for atuacao in atuacoes_em_curso:
            print(f"- {atuacao}")

        # Imprime uma linha separadora
        print("-" * 30)  # Imprime 30 traços
        print()  # Adiciona uma linha em branco

Alice Paula Di Sabatino Guimarães

Tempo de atuação em cada instituição:
- FUNDAÇÃO OSWALDO CRUZ/CENTRO DE PESQUISAS RENÉ RACHOU, FIOCRUZ/CPQRR, Brasil.: 1 anos
- Fundação Oswaldo Cruz - Unidade Rondônia, FIOCRUZ RO, Brasil.: 0 anos

Atuações em curso:
- Fundação Oswaldo Cruz - Unidade Rondônia, FIOCRUZ RO, Brasil. (2015 - Atual)
------------------------------

Ana Cláudia de Araújo Teixeira

Tempo de atuação em cada instituição:
- Fundação Oswaldo Cruz - Fiocruz Ceará, FIOCRUZ CEARÁ, Brasil.: 9 anos
- Fundação Oswaldo Cruz, FIOCRUZ, Brasil.: 1 anos
- Universidade de Brasília, UnB, Brasil.: 2 anos
- Universidade Federal do Ceará, UFC, Brasil.: 0 anos
- Escola de Saúde Pública do Ceará, ESP/CE, Brasil.: 1 anos
- Secretaria de Saúde do Estado do Ceará, SESA, Brasil.: 1 anos
- Sociedade de Ensino Superior Faculdade Integrada do Ceará, FIC*, Brasil.: 2 anos
- Universidade de Fortaleza, UNIFOR, Brasil.: 0 anos
- Universidade Estadual do Ceará e Universidade Centro de Estudos Integrados, UEC

In [85]:
# Exemplo de uso
dados_profissionais = dict_list_docents[5]['Atuação Profissional']

# Garante que dados_profissionais seja uma lista
if not isinstance(dados_profissionais, list):
    dados_profissionais = [dados_profissionais]

tempo_atuacao, atuacoes_em_curso = calcular_tempo_atuacao(dados_profissionais)

print(tempo_atuacao)
print(atuacoes_em_curso)

ValueError: invalid literal for int() with base 10: 'Atual'

In [81]:
dict_list_docents[19].get('Atuação Profissional')

[{'Instituição': 'Fundação Osvaldo Cruz, FIOCRUZ CE, Brasil.',
  'Ano': '2019 - Atual',
  'Descrição': '',
  'Outras informações': 'Vínculo: , Enquadramento Funcional:'},
 {'Instituição': 'Instituto Atlântico, IA, Brasil.',
  'Ano': '2018 - 2020',
  'Descrição': '',
  'Outras informações': 'Vínculo: Consultora, Enquadramento Funcional: Consultora, Carga horária: 10'},
 {'Instituição': 'Fundação Oswaldo Cruz, FIOCRUZ, Brasil.',
  'Ano': '2015 - Atual',
  'Descrição': '',
  'Outras informações': 'Vínculo: Servidor Público, Enquadramento Funcional: Especialista em C&T Prod. Inov. em Saúde, Carga horária: 40 Linhas de pesquisa em Saúde Digital e Estratégia Saúde da Família'},
 {'Instituição': 'Fundação Oswaldo Cruz, FIOCRUZ, Brasil.',
  'Ano': '03/2017 - Atual',
  'Descrição': '',
  'Outras informações': 'Ensino, MESTRADO PROFISSIONAL EM SAÚDE DA FAMÍLIA - RENASF/MPSF, Nível: Pós-Graduação Disciplinas ministradas Atenção Integral Seminários Atenção e Gestão Educação em Saúde I Gestão do Pr

In [80]:
[x for x in dict_list_docents[19].get('Atuação Profissional')]

[{'Instituição': 'Fundação Osvaldo Cruz, FIOCRUZ CE, Brasil.',
  'Ano': '2019 - Atual',
  'Descrição': '',
  'Outras informações': 'Vínculo: , Enquadramento Funcional:'},
 {'Instituição': 'Instituto Atlântico, IA, Brasil.',
  'Ano': '2018 - 2020',
  'Descrição': '',
  'Outras informações': 'Vínculo: Consultora, Enquadramento Funcional: Consultora, Carga horária: 10'},
 {'Instituição': 'Fundação Oswaldo Cruz, FIOCRUZ, Brasil.',
  'Ano': '2015 - Atual',
  'Descrição': '',
  'Outras informações': 'Vínculo: Servidor Público, Enquadramento Funcional: Especialista em C&T Prod. Inov. em Saúde, Carga horária: 40 Linhas de pesquisa em Saúde Digital e Estratégia Saúde da Família'},
 {'Instituição': 'Fundação Oswaldo Cruz, FIOCRUZ, Brasil.',
  'Ano': '03/2017 - Atual',
  'Descrição': '',
  'Outras informações': 'Ensino, MESTRADO PROFISSIONAL EM SAÚDE DA FAMÍLIA - RENASF/MPSF, Nível: Pós-Graduação Disciplinas ministradas Atenção Integral Seminários Atenção e Gestão Educação em Saúde I Gestão do Pr

In [72]:
def listar_instituicoes
lista_instituicoes = [x.get('Instituição') for x in dict_list_docents[19].get('Atuação Profissional')]
instituicoes_unicas = list(set(lista_instituicoes))
instituicoes_unicas

['Sociedade Cearense de Pediatria, SOCEP, Brasil.',
 'Universidade Estadual Vale do Acaraú, UVA-CE, Brasil.',
 'Prefeitura Municipal de Icapuí, PMI, Brasil.',
 'Instituto de Estudos, Pesquisas e Projetos da UECE, IEPRO, Brasil.',
 'Fundação Oswaldo Cruz, FIOCRUZ, Brasil.',
 'Escola de Saúde Pública do Ceará, ESP/CE, Brasil.',
 'Universidade Federal do Ceará, UFC, Brasil.',
 'Prefeitura Municipal de Quixadá, PMQ, Brasil.',
 'Fundação Osvaldo Cruz, FIOCRUZ CE, Brasil.',
 'Secretaria de Saúde do Estado do Ceará, SESA*, Brasil.',
 'Prefeitura Municipal de Sobral, PMS, Brasil.',
 'Escola de Formação Em Saúde da Família Visconde de Sabóia, EFSFVS, Brasil.',
 'Instituto Atlântico, IA, Brasil.']

In [65]:
for curriculo in dict_list_docents:
    nome = curriculo.get('Identificação').get('Nome')
    linhas = [x.get('Descrição') for x in curriculo.get('Linhas de Pesquisa')]
    print(nome)
    pprint(linhas)

Alice Paula Di Sabatino Guimarães
[]
Ana Cláudia de Araújo Teixeira
['Desenvolvimento, Injustiça Ambiental e Saúde: o caso da Mineração de Urânio '
 'e Fosfato no Ceará',
 'Objetivo: A partir da produção compartilhada de conhecimentos, busca-se: '
 'desvelar o contexto de risco e as implicações da implantação da mineração de '
 'urânio e fosfato prevista para Santa Quitéria-CE no que diz respeito ao '
 'trabalho, o ambiente, a saúde e os modos de vida das comunidades atingidas; '
 'Contribuir com o desenvolvimento de metodologias e instrumentos que '
 'incorporem os princípios da avaliação de equidade ambiental visando à '
 'investigação das relações produção, ambiente e saúde nos territórios de '
 'influência do projeto de mineração de urânio e fosfato; Contribuir com a '
 'formulação de bases conceituais e metodológicas visando à construção das '
 'concepções de Vigilância de Base Territorial Local e de Vigilância Popular '
 'em Saúde; Subsidiar o SUS no âmbito da atenção primária à 

In [60]:
for dict_pesq in dict_list_docents[17:18]:
    avaliar_tipo_instancias_arvore(dict_pesq)

N1. Mapa: dict_keys(['Identificação', 'Idiomas', 'Formação', 'Atuação Profissional', 'Linhas de Pesquisa', 'Áreas', 'Produções', 'ProjetosPesquisa', 'ProjetosExtensão', 'ProjetosDesenvolvimento', 'ProjetosOutros', 'Patentes e registros', 'Bancas', 'Orientações', 'JCR2'])
  Identificação:
    N2. Mapa: dict_keys(['Nome', 'ID Lattes', 'Última atualização'])
      Nome:
        N3. String: Giovanny Augusto Camacho Antevere Mazzarotto
      ID Lattes:
        N3. String: 4491426793431771
      Última atualização:
        N3. String: 08/07/2024
  Idiomas:
    N2. Lista: 2 elementos
        N3. Mapa: dict_keys(['Idioma', 'Proficiência'])
          Idioma:
            N4. String: Inglês
          Proficiência:
            N4. String: Compreende Bem, Fala Razoavelmente, Lê Bem, Escreve Razoavelmente.
        N3. Mapa: dict_keys(['Idioma', 'Proficiência'])
          Idioma:
            N4. String: Esperanto
          Proficiência:
            N4. String: Compreende Bem, Fala Razoavelmente, Lê B

In [58]:
dicionario = dict_list_docents
chave_dicionario = 'Linhas de Pesquisa'

for estrutura_dados in dicionario:
    if isinstance(estrutura_dados, dict):
        try:
            ver_subchaves(dicionario, chave_dicionario)
        except:
            print(f'Não foi possível ler {estrutura_dados}')
    elif isinstance(estrutura_dados, list):
        try:
            ver_conteudo_lista(dicionario, chave_dicionario)
        except:
            print(f'Não foi possível ler {estrutura_dados}')

Não foi possível ler {'Identificação': {'Nome': 'Alice Paula Di Sabatino Guimarães', 'ID Lattes': '8793885517658468', 'Última atualização': '05/06/2023'}, 'Idiomas': [{'Idioma': 'Inglês', 'Proficiência': 'Compreende Bem, Lê Bem.'}, {'Idioma': 'Espanhol', 'Proficiência': 'Compreende Razoavelmente, Fala Razoavelmente, Lê Razoavelmente.'}], 'Formação': {'Acadêmica': [{'Ano': '2019 - 2021', 'Descrição': 'Mestrado profissional em Saúde Pública. Fundação Oswaldo Cruz, FIOCRUZ, Brasil. Título: Caderno Eletrônico de Laboratório como instrumento de sinergia, inovação e susten-tabilidade científica, Ano de Obtenção: 2021. Orientador: Laís Silveira Costa. Coorientador: Renata Almeida de Souza. Grande área: Ciências da Saúde'}, {'Ano': '2007 - 2009', 'Descrição': 'Especialização em Gestão e Tecnologia da Qualidade.  (Carga Horária: 374h). Centro Federal de Educação Tecnológica de Minas Gerais, CEFET/MG, Brasil. Título: Redução do índice de atraso das análises físico-químicas na Hipolabor Farmacêut

## Obter as linhas de pesquisa de cada orientador/docente

## Obter as palavras-chave predominantes nos currículos

## Obter Grupos de Pesquisa no DGP/CNPq 

In [ ]:
import os
# os.listdir('C:\\Users\\marco\\Downloads')

In [ ]:
## montar um dataframe com nomes dos membros dos grupos de pesquisa do DGP CNPq
folder_download = 'C:\\Users\\marco\\Downloads'
def montardf_dgp():
    try:
        file = 'dgp2023_grupos_pesquisa.csv'
        pathfilename = os.path.join(folder_download, file)
        print(pathfilename)

        # Especifique a codificação correta (substitua 'latin-1' pela codificação real do seu arquivo)
        df_dgp = pd.read_csv(pathfilename, header=0, encoding='latin-1')  

    except Exception as e:
        print('Erro ao ler o arquivo CSV:')
        print(e)
        return

    return df_dgp

def montardf_participantes_dgp():
    try:
        file = 'dgp2023_participantes_grupos_pesquisa.csv'
        pathfilename = os.path.join(folder_download, file)
        print(pathfilename)

        # Especifique a codificação correta (substitua 'latin-1' pela codificação real do seu arquivo)
        df_dgp = pd.read_csv(pathfilename, header=0, encoding='latin-1')  

    except Exception as e:
        print('Erro ao ler o arquivo CSV:')
        print(e)
        return

    return df_dgp

df_dgp = montardf_dgp()
print(f'Chaves do arquivo de grupos: {df_dgp.keys()}')

df_participantes = montardf_participantes_dgp()
print(f'Chaves do arquivo de participantes: {df_participantes.keys()}')

C:\Users\marco\Downloads\dgp2023_grupos_pesquisa.csv
Chaves do arquivo de grupos: Index(['ANO_DO_CENSO', 'DATA_INICIO_DA_COLETA', 'DATA_FIM_DA_COLETA',
       'IDENTIFICADOR_DO_GRUPO', 'NOME_DO_GRUPO', 'ANO_FORMACAO',
       'REGIAO_GRUPO_PESQUISA', 'UF_GRUPO_PESQUISA', 'CIDADE_GRUPO_PESQUISA',
       'GRANDE_AREA_PREDOMINANTE', 'AREA_PREDOMINANTE', 'NOME_DA_INSTITUICAO',
       'SIGLA_DA_INSTITUICAO', 'CATEGORIA_ADMINISTRATIVA', 'NATUREZA_JURIDICA',
       'SETOR_ATIVIDADE_ECONOMICA', 'QTD_LINHA_PESQUISA',
       'QTD_PESQUISADOR_GRUPO', 'QTD_ESTUDANTES_GRUPO', 'QTD_TECNICO_GRUPO',
       'QTD_COLABORADOR_GRUPO', 'QUANTIDADEDEPESQUISADORDOUTOR',
       'QUANTDOUTORANDOS', 'QUANTMESTRANDOS', 'QUANTGRADUANDOS'],
      dtype='object')
C:\Users\marco\Downloads\dgp2023_participantes_grupos_pesquisa.csv
Chaves do arquivo de participantes: Index(['TIPO_DE_PARTICIPACAO', 'PAIS_NASCIMENTO_PARTICIPANTE',
       'NACIONALIDADE_PARTICIPANTE', 'TITULACAO_PARTICIPANTE',
       'SEXO_PARTICIPANTE', 

In [ ]:
filtro_instituicao = df_dgp['SIGLA_DA_INSTITUICAO'] == 'FIOCRUZ'
dfdgp_fiocruz = df_dgp[filtro_instituicao]
print(f'{len(dfdgp_fiocruz.index)} grupos de pesquisa da Fiocruz Nacional')
# dfdgp_fiocruz

394 grupos de pesquisa da Fiocruz Nacional


### Dados dos grupos de pesquisa Fiocruz Ceará

In [ ]:
lista_espelhos = [
    'https://dgp.cnpq.br/dgp/espelhogrupo/368850',
    'https://dgp.cnpq.br/dgp/espelhogrupo/773438',
    'https://dgp.cnpq.br/dgp/espelhogrupo/192437',
    'https://dgp.cnpq.br/dgp/espelhogrupo/0837407474908287',
    'https://dgp.cnpq.br/dgp/espelhogrupo/772170',
    'https://dgp.cnpq.br/dgp/espelhogrupo/662667',
    'http://dgp.cnpq.br/dgp/espelhogrupo/528799']

In [ ]:
filtro_estado = df_dgp['UF_GRUPO_PESQUISA'] == 'Ceará'
dfdgp_fiocruz_ce = dfdgp_fiocruz[filtro_estado]
dfdgp_fiocruz_ce = dfdgp_fiocruz_ce.drop(columns=['DATA_INICIO_DA_COLETA','DATA_FIM_DA_COLETA','REGIAO_GRUPO_PESQUISA','UF_GRUPO_PESQUISA','CIDADE_GRUPO_PESQUISA','NOME_DA_INSTITUICAO','NATUREZA_JURIDICA','ANO_DO_CENSO','CATEGORIA_ADMINISTRATIVA'])

print(f'{len(dfdgp_fiocruz_ce.index)} grupos de pesquisa da Fiocruz no Ceará')
nomes_grupos_fioce = list(dfdgp_fiocruz_ce['NOME_DO_GRUPO'])
nomes_grupos_fioce

7 grupos de pesquisa da Fiocruz no Ceará


['Grupo de Estudos em Vida Silvestre (GEVS)',
 'Biologia estrutural e funcional em Biofármacos',
 'Saúde do Campo, da Floresta e das Águas no contexto da Ecologia de Saberes',
 'Saúde da Família',
 'Epidemiologia Molecular e Vigilância Translacional',
 'GEPeSS - Grupo de Engenharia de Proteínas e Soluções para Saúde',
 'Lariisa Saúde Digital - Laboratório de Redes Integradas e Inteligentes em Saúde']

In [ ]:
dfdgp_fiocruz_ce.keys()

Index(['IDENTIFICADOR_DO_GRUPO', 'NOME_DO_GRUPO', 'ANO_FORMACAO',
       'GRANDE_AREA_PREDOMINANTE', 'AREA_PREDOMINANTE', 'SIGLA_DA_INSTITUICAO',
       'SETOR_ATIVIDADE_ECONOMICA', 'QTD_LINHA_PESQUISA',
       'QTD_PESQUISADOR_GRUPO', 'QTD_ESTUDANTES_GRUPO', 'QTD_TECNICO_GRUPO',
       'QTD_COLABORADOR_GRUPO', 'QUANTIDADEDEPESQUISADORDOUTOR',
       'QUANTDOUTORANDOS', 'QUANTMESTRANDOS', 'QUANTGRADUANDOS'],
      dtype='object')

In [ ]:
print(dfdgp_fiocruz_ce.keys())
dfdgp_fiocruz_ce.columns=['IDENTIFICADOR','NOME_GRUPO','ANO_FORM','GRANDE_AREA','AREA','SIGLA','SETOR_ECONOMICO','LINHAS','PESQUISADORES','ESTUDANTES','TECNICOS','COLABORADORES','DOUTORES','DOUTORANDOS','MESTRANDOS','GRADUANDOS']
dfdgp_fiocruz_ce

Index(['IDENTIFICADOR_DO_GRUPO', 'NOME_DO_GRUPO', 'ANO_FORMACAO',
       'GRANDE_AREA_PREDOMINANTE', 'AREA_PREDOMINANTE', 'SIGLA_DA_INSTITUICAO',
       'SETOR_ATIVIDADE_ECONOMICA', 'QTD_LINHA_PESQUISA',
       'QTD_PESQUISADOR_GRUPO', 'QTD_ESTUDANTES_GRUPO', 'QTD_TECNICO_GRUPO',
       'QTD_COLABORADOR_GRUPO', 'QUANTIDADEDEPESQUISADORDOUTOR',
       'QUANTDOUTORANDOS', 'QUANTMESTRANDOS', 'QUANTGRADUANDOS'],
      dtype='object')


IDENTIFICADOR      
870    9631978230775159  \
6190    694942952339445   
14655  7130787156028964   
18539   837407474908287   
20520  7615283714338484   
30248  3401121986800593   
36422  3809489769719608   

      NOME_GRUPO                                                                         
870                                          Grupo de Estudos em Vida Silvestre (GEVS)  \
6190                                    Biologia estrutural e funcional em Biofármacos   
14655       Saúde do Campo, da Floresta e das Águas no contexto da Ecologia de Saberes   
18539                                                                 Saúde da Família   
20520                               Epidemiologia Molecular e Vigilância Translacional   
30248                  GEPeSS - Grupo de Engenharia de Proteínas e Soluções para Saúde   
36422  Lariisa Saúde Digital - Laboratório de Redes Integradas e Inteligentes em Saúde   

       ANO_FORM GRANDE_AREA          AREA            SIGLA      
870    2017      Ciências Biológicas        Ecologia  FIOCRUZ  \
6190   2022      Ciências Biológicas   Biotecnologia  FIOCRUZ   
14655  2013        Ciências da Saúde  Saúde Coletiva  FIOCRUZ   
18539  2013        Ciências da Saúde  Saúde Coletiva  FIOCRUZ   
20520  2022      Ciências Biológicas        Genética  FIOCRUZ   
30248  2020      Ciências Biológicas   Biotecnologia  FIOCRUZ   
36422  2017        Ciências da Saúde  Saúde Coletiva  FIOCRUZ   

      SETOR_ECONOMICO                                                                    
870    M.72.1 - Pesquisa e desenvolvimento experimental em ciências físicas e naturais  \
6190   M.72.1 - Pesquisa e desenvolvimento experimental em ciências físicas e naturais   
14655  M.72.1 - Pesquisa e desenvolvimento experimental em ciências físicas e naturais   
18539  M.72.1 - Pesquisa e desenvolvimento experimental em ciências físicas e naturais   
20520  M.72.1 - Pesquisa e desenvolvimento experimental em ciências físicas e naturais   
30248  M.72.1 - Pesquisa e desenvolvimento experimental em ciências físicas e naturais   
36422  M.72.1 - Pesquisa e desenvolvimento experimental em ciências físicas e naturais   

       LINHAS  PESQUISADORES  ESTUDANTES  TECNICOS  COLABORADORES  DOUTORES   
870    1       15              3           0        0               9        \
6190   3        4             22           0        0               3         
14655  6       32              6           0        2              11         
18539  3       13              3           1        0              10         
20520  5       10             15           5        1               8         
30248  9       12             16           0        0              10         
36422  2       36             19          10        1              33         

       DOUTORANDOS  MESTRANDOS  GRADUANDOS  
870     4           1           2           
6190    4           6           5           
14655   6           1           3           
18539   2           0           0           
20520   5           6           6           
30248  10           4           1           
36422  10           5           1

In [ ]:
# dfdgp_ce['SIGLA_DA_INSTITUICAO'].unique()
# df_dgp['CIDADE_GRUPO_PESQUISA'].unique()
# filtro_instituicao_ceara = dfdgp_ce['SIGLA_DA_INSTITUICAO'] == 'FIOCRUZ'

# Explorar conteúdo de dicionários extraídos

In [ ]:
## Ver chaves de dicionário de primeiro nível no arquivo de dados
from pprint import pprint

max_keys=[]
for n,i in enumerate([x.keys() for x in dict_list_docents]):
    max_keys.append((n, len(list(i))))
print(max_keys)
pprint(list(i))

[(0, 15), (1, 15), (2, 15), (3, 15), (4, 15), (5, 15), (6, 15), (7, 15), (8, 15), (9, 15), (10, 15), (11, 15), (12, 15), (13, 15), (14, 15), (15, 15), (16, 15), (17, 15), (18, 15), (19, 15), (20, 15), (21, 15), (22, 15), (23, 15), (24, 15), (25, 15), (26, 15), (27, 15), (28, 15), (29, 15), (30, 15), (31, 15), (32, 15), (33, 15), (34, 15), (35, 15), (36, 15), (37, 15), (38, 15), (39, 15), (40, 15), (41, 15), (42, 15), (43, 15), (44, 15), (45, 15), (46, 15), (47, 15), (48, 15), (49, 15), (50, 15), (51, 15), (52, 15), (53, 15), (54, 15), (55, 15), (56, 15), (57, 15), (58, 15), (59, 15), (60, 15), (61, 15)]
['Identificação',
 'Idiomas',
 'Formação',
 'Atuação Profissional',
 'Linhas de Pesquisa',
 'Áreas',
 'Produções',
 'ProjetosPesquisa',
 'ProjetosExtensão',
 'ProjetosDesenvolvimento',
 'ProjetosOutros',
 'Patentes e registros',
 'Bancas',
 'Orientações',
 'JCR2']


In [ ]:
## Ver chaves de subdicionário de segundo nível no dicionário 'Produções' do arquivo de dados
from pprint import pprint

max_subkeys=[]
for n,j in enumerate([x.get('Produções').keys() for x in dict_list_docents]):
    max_subkeys.append((n, len(list(j))))
print(max_subkeys)
pprint(list(j))

[(0, 5), (1, 11), (2, 3), (3, 10), (4, 5), (5, 3), (6, 13), (7, 8), (8, 5), (9, 4), (10, 5), (11, 3), (12, 7), (13, 12), (14, 6), (15, 14), (16, 11), (17, 10), (18, 7), (19, 17), (20, 8), (21, 4), (22, 12), (23, 16), (24, 5), (25, 9), (26, 12), (27, 10), (28, 5), (29, 16), (30, 2), (31, 5), (32, 12), (33, 12), (34, 10), (35, 14), (36, 2), (37, 8), (38, 6), (39, 5), (40, 9), (41, 4), (42, 4), (43, 5), (44, 15), (45, 5), (46, 2), (47, 6), (48, 6), (49, 5), (50, 10), (51, 3), (52, 7), (53, 8), (54, 9), (55, 5), (56, 6), (57, 3), (58, 7), (59, 0), (60, 3), (61, 11)]
['Artigos completos publicados em periódicos',
 'Citações',
 'Livros publicados/organizados ou edições',
 'Capítulos de livros publicados',
 'Trabalhos completos publicados em anais de congressos',
 'Resumos expandidos publicados em anais de congressos',
 'Resumos publicados em anais de congressos',
 'Apresentações de Trabalho',
 'Assessoria e consultoria',
 'Trabalhos técnicos',
 'Entrevistas, mesas redondas, programas e comen

In [ ]:
## Ver chaves de subdicionário de segundo nível no dicionário 'Produções' do arquivo de dados
# Chamar a função recursiva para cada dicionário na lista, filtrando por "Orientações"
# chave='Orientações'
# for docente in dict_list_docents:
#     atualizador.imprimir_chaves_recursivo(docente, nivel1_filtro=chave)

In [ ]:
## Ver quantidade de chaves de subdicionário do dicionário de Produções, segundo nível no arquivo de dados
# max_subkeys=[]
# for n,i in enumerate([x.get('Produções').keys() for x in dict_list_docents]):
#     max_subkeys.append((n,len(list(i))))
# print(max_subkeys)

In [ ]:
## Ver anos de cada uma das publicações dos artigos completos em periódicos
# for n,i in enumerate([x for x in dict_list_docents]):
#     try:
#         artigos = i.get('Produções').get('Artigos completos publicados em periódicos')
#         anos = [x.get('ano') for x in artigos]
#         print(anos)
#     except:
#         print('Artigos não encontrados para este currículo')

In [ ]:
# dict_points
# [x.get('Orientações') for x in dict_list_docents]

# import re
# import collections
# from pprint import pprint
# tipos=[]

# # Verificar orientações concluídas de IC nos dados de docentes
# for i in [x.get('Orientações').get('Orientações e supervisões concluídas') for x in dict_list_docents if x.get('Orientações')]:
#     if i is not None:
#         for tipo in i:
#             if tipo.keys() not in tipos:
#                 tipos.append(tipo.keys()) 
#             try:
#                 qic = tipo.get('Dissertação de mestrado')
#             except:
#                 qic = 0
#             if qic:
#                 lista = [x for x in qic.values()]
#     else:
#         qic = 0

# for i in tipos:
#     print(list(i)[0])

In [ ]:
from pprint import pprint
# Leitura de todas as chaves e subchaves de dicionários
todas_chaves_principais = []
todas_subchaves_producoes = []
todas_subchaves_patentes = []
todas_subchaves_orientacoes = []
ano_inicial = 2020
ano_termino = 2024
verbose = False
for x in dict_list_docents:
    chaves_dicionarios = [c for c in x]
    for i in chaves_dicionarios:
        if i not in todas_chaves_principais:
            todas_chaves_principais.append(i)
    dict_id = x.get('Identificação')
    dict_prods = x.get('Produções')
    dict_orients = x.get('Orientações')
    dict_patents = x.get('Patentes e registros')
    lista_subchaves_producoes=[x for x in dict_prods.keys()]
    lista_subchaves_orientacoes=[x for x in dict_orients.keys()]
    lista_subchaves_patentes=[x for x in dict_patents.keys()]
    for i in lista_subchaves_producoes:
        if i not in todas_subchaves_producoes:
            todas_subchaves_producoes.append(i)
    for i in lista_subchaves_orientacoes:
        if i not in todas_subchaves_orientacoes:
            todas_subchaves_orientacoes.append(i)
    for i in lista_subchaves_patentes:
        if i not in todas_subchaves_patentes:
            todas_subchaves_patentes.append(i)
    ## Subdciocionários por tipos de produções
    artigos = dict_prods.get('Artigos completos publicados em periódicos')
    livros_publicados = dict_prods.get('Livros publicados/organizados ou edições')
    capitulos_livros  = dict_prods.get('Capítulos de livros publicados')
    organizacao_livro = dict_prods.get('Capítulos de livros publicados')
    trabalho_congresso = dict_prods.get('Trabalhos completos publicados em anais de congressos')

In [ ]:
todas_chaves_principais

['Identificação',
 'Idiomas',
 'Formação',
 'Atuação Profissional',
 'Linhas de Pesquisa',
 'Áreas',
 'Produções',
 'ProjetosPesquisa',
 'ProjetosExtensão',
 'ProjetosDesenvolvimento',
 'ProjetosOutros',
 'Patentes e registros',
 'Bancas',
 'Orientações',
 'JCR2']

In [ ]:
todas_subchaves_producoes

['Artigos completos publicados em periódicos',
 'Resumos publicados em anais de congressos',
 'Apresentações de Trabalho',
 'Outras produções bibliográficas',
 'Entrevistas, mesas redondas, programas e comentários na mídia',
 'Livros publicados/organizados ou edições',
 'Capítulos de livros publicados',
 'Resumos expandidos publicados em anais de congressos',
 'Resumos publicados em anais de congressos (artigos)',
 'Trabalhos técnicos',
 'Demais trabalhos',
 'Citações',
 'Trabalhos completos publicados em anais de congressos',
 'Produtos tecnológicos',
 'Artigos  aceitos para publicação',
 'Assessoria e consultoria',
 'Programas de computador sem registro',
 'Processos ou técnicas',
 'Outras produções artísticas/culturais',
 'Textos em jornais de notícias/revistas',
 'Redes sociais, websites e blogs',
 'Artes Visuais',
 'Música']

In [ ]:
todas_subchaves_orientacoes

['Orientações e supervisões concluídas',
 'Orientações e supervisões em andamento']

In [ ]:
todas_subchaves_patentes

['Patente', 'Programa de computador', 'Marca registrada']

In [ ]:
todas_patentes = []
for x in dict_list_docents:
    nome = x.get('Identificação').get('Nome')
    patentes_registros = x.get('Patentes e registros')
    todas_patentes.append(patentes_registros)


In [ ]:
todas_patentes

[{},
 {},
 {},
 {},
 {},
 {},
 {},
 {'Patente': {'1': {'ano': 2007,
    'texto': 'Petzinger, E. ; GEYER, J. ;FERNANDES, C.F.; GERSTBERGER ; RAFALZIK, S. . Protein P4 as a marker protein for cholinergic neurons of the CNS.  2007,  Alemanha.Patente:                 Patente no Exterior.             Número do registro: WO2008104151A1, título: "Protein P4 as a marker protein for cholinergic neurons of the CNS" Depósito: 28/02/2007Instituição(ões) financiadora(s): Justus-Liebig Universität.',
    'autores': []}}},
 {},
 {},
 {'Patente': {'1': {'ano': 2011,
    'texto': 'COSTA, J.P. ;FREITAS, R. M.; SOARES, M. F. L. R. ; ALMEIDA, R. N. ;COSTA, D. A.; FORTES, A. C. . Aplicações do fitol em formulações farmacêuticas com propriedades ansiolítica e antidepressiva.  2011,  Brasil.Patente:                 Privilégio de Inovação.             Número do registro: PI11063971, título: "Aplicações do fitol em formulações farmacêuticas com propriedades ansiolítica e antidepressiva" , Instituição de regist

In [ ]:
print(f'Pontuação geral por artigos publicados ponderados pelo JCR no período {ano_inicio} a {ano_final}')
df_artigos_geral = df_resultado.sort_values(by=['Total Pontos'], ascending=False)
df_artigos_geral

In [ ]:
from pprint import pprint
# Leitura de todas as chaves e subchaves de dicionários
todas_chaves_principais = []
todas_subchaves_producoes = []
todas_subchaves_orientacoes = []
ano_inicial = 2020
ano_termino = 2024
verbose = False
for x in dict_list_docents:
    chaves_dicionarios = [c for c in x]
    for i in chaves_dicionarios:
        if i not in todas_chaves_principais:
            todas_chaves_principais.append(i)
    dict_id = x.get('Identificação')
    dict_prods = x.get('Produções')
    dict_orients = x.get('Orientações')
    lista_subchaves_producoes=[x for x in dict_prods.keys()]
    lista_subchaves_orientacoes=[x for x in dict_orients.keys()]
    for i in lista_subchaves_producoes:
        if i not in todas_subchaves_producoes:
            todas_subchaves_producoes.append(i)
    for i in lista_subchaves_orientacoes:
        if i not in todas_subchaves_orientacoes:
            todas_subchaves_orientacoes.append(i)

    ## Subdciocionários por tipos de produções
    artigos = dict_prods.get('Artigos completos publicados em periódicos')
    livros_publicados = dict_prods.get('Livros publicados/organizados ou edições')
    capitulos_livros  = dict_prods.get('Capítulos de livros publicados')
    organizacao_livro = dict_prods.get('Capítulos de livros publicados')
    trabalho_congresso = dict_prods.get('Trabalhos completos publicados em anais de congressos')
    patentes_registros = dict_prods.get('Patentes e registros')

    ### CONTAGENS
    ## Contagem da publicação de artigos em periódicos
    qte_jcr_faltante=0
    qte_jcr_inferior=0
    qte_jcr_superior=0
    pontos_artsemjci = 0
    pontos_artjcimenor = 0
    pontos_artjcimaior = 0
    pontos_public=0
    
    artigos_todos_tempos=0
    artigos_dentro_periodo=0
    
    if artigos:
        if verbose:        
            print(f'Dicionário de artigos:')
            pprint(artigos, width=120)
        for i in artigos:
            artigos_todos_tempos+=1
            try:
                try:
                    ano_artigo = int(i.get('ano'))
                except:
                    ano_artigo = ano_inicial
                if ano_inicial <= ano_artigo <= ano_termino:
                    artigos_dentro_periodo+=1
                    try:
                        impacto = float(i.get('fator_impacto_jcr'))
                        if impacto>=0.5:
                            qte_jcr_inferior+=1
                        elif impacto>=1.1:
                            qte_jcr_superior+=1
                    except:
                        qte_jcr_faltante+=1                      
            except Exception as e:
                print(f'        Erro ao extrair artigo: {e}')
                print(f'        Artigo com problema: {i}')

    qte_artperiodicos=qte_jcr_faltante+qte_jcr_inferior+qte_jcr_superior

    ## Contagem da publicação de livros e capítulos
    qte_livros=0
    qte_capitulos=0
    pontos_livpub=0
    pontos_capliv=0
    if livros_publicados:
        if verbose:        
            print(f'Dicionário de livros:')
            pprint(livros_publicados)
        qte_livros = len([x for x in livros_publicados])
    if capitulos_livros:
        qte_capitulos = len([x for x in capitulos_livros])
    
    ## Contagem de Orientações Concluídas
    qte_ic=0
    qte_grad=0
    qte_espec=0
    qte_mest=0
    qte_dout=0
    qte_orientacoes_total=0
    qte_orientacoes=0
    pontos_orient_ic=0
    pontos_orient_grad=0
    pontos_orient_mest=0
    pontos_orient_dout=0
    pontos_orient=0

    concluidas = dict_orients.get('Orientações e supervisões concluídas')
    if concluidas:
        if verbose:
            print(f'Dicionário de orientações concluídas:')
            pprint(concluidas, width=120)
        for i in concluidas:
            dict_ic = i.get('Iniciação científica')
            if dict_ic:
                try:
                    for chave, valor in dict_ic.items():
                        qte_orientacoes_total+=1
                        ano_match = re.search(r'\b(\d{4})\b', valor)
                        if ano_match:
                            ano_orientacao = int(ano_match.group(1))
                            if ano_inicial <= ano_orientacao <= ano_termino:
                                qte_orientacoes+=1                    
                                qte_ic += 1
                except Exception as e:
                    print(f'        Erro em extração de IC: {e}')
            dict_grad = i.get('Trabalho de conclusão de curso de graduação')
            if dict_grad:
                try:
                    for chave, valor in dict_grad.items():
                        qte_orientacoes_total+=1
                        ano_match = re.search(r'\b(\d{4})\b', valor)
                        if ano_match:
                            ano_orientacao = int(ano_match.group(1))
                            if ano_inicial <= ano_orientacao <= ano_termino:
                                qte_orientacoes+=1                      
                                qte_grad += 1
                except Exception as e:
                    print(f'        Erro em extração de Graduação: {e}')
            dict_espe = i.get('Monografia de conclusão de curso de aperfeiçoamento/especialização')
            if dict_espe:
                try:
                    for chave, valor in dict_espe.items():
                        qte_orientacoes_total+=1
                        ano_match = re.search(r'\b(\d{4})\b', valor)
                        if ano_match:
                            ano_orientacao = int(ano_match.group(1))
                            if ano_inicial <= ano_orientacao <= ano_termino:
                                qte_orientacoes+=1                      
                                qte_espec +=1
                except Exception as e:
                    qte_espec = 0
                    print(f'        Erro em extração de Especialização: {e}')   
            dict_mest = i.get('Dissertação de mestrado')
            if dict_mest:
                try:
                    for chave, valor in dict_mest.items():
                        qte_orientacoes_total+=1
                        ano_match = re.search(r'\b(\d{4})\b', valor)
                        if ano_match:
                            ano_orientacao = int(ano_match.group(1))
                            if ano_inicial <= ano_orientacao <= ano_termino:
                                qte_orientacoes+=1  
                                qte_mest +=1
                except Exception as e:
                    print(f'        Erro em extração de Mestrado: {e}')
            dict_dout = i.get('Tese de doutorado')
            if dict_dout:                
                try:
                    for chave, valor in dict_dout.items():
                        qte_orientacoes_total+=1
                        ano_match = re.search(r'\b(\d{4})\b', valor)
                        if ano_match:
                            ano_orientacao = int(ano_match.group(1))
                            if ano_inicial <= ano_orientacao <= ano_termino:
                                qte_orientacoes+=1                      
                                qte_dout +=1
                except Exception as e:
                    print(f'        Erro em extração de Doutorado: {e}')

        qte_tcc = qte_grad+qte_espec

    ## Contagem dos Trabalhos completos publicados em anais de congressos
    qte_trabcongresso_total=0
    qte_trabcongresso=0
    pontos_congresso=0
    if trabalho_congresso:
        if verbose:
            print(f'Dicionário de trabalhos em congressos:')
            pprint(trabalho_congresso, width=120)        
        qte_trabcongresso_total = len([x for x in trabalho_congresso])
        for chave, valor in trabalho_congresso.items():
            ano_match = re.search(r'\b(\d{4})\b', valor)
            if ano_match:
                ano_trabalho = int(ano_match.group(1))
                if ano_inicial <= ano_trabalho <= ano_termino:
                    qte_trabcongresso+=1
    
    ### PONDERAÇÕES
    ## Ponderação das Publicações de artigos completos em periódicos
    pontos_artsemjci = qte_jcr_faltante*0
    pontos_artjcimenor = qte_jcr_inferior*6
    pontos_artjcimaior = qte_jcr_superior*8
    pontos_public = pontos_artsemjci+pontos_artjcimenor+pontos_artjcimaior

    ## Ponderação das Publicações de Livros e Capítulos
    # - Livro publicado com ISBN = 3p (mínimo 80 páginas)
    # - Organização de livro     = x 3p
    # - Capítulo de livro        = x 2p
    pontos_livpub = qte_livros*3
    pontos_capliv = qte_capitulos*2
    pontos_livros = pontos_livpub+pontos_capliv

    ## Ponderações de Trabalhos publicados em anais de congressos
    # - Resumo Estendido/ Artigo Completo (teto 5 trabalhos) x 2 pontos
    # - Resumo Simples (teto 10 trabalhos)	                 x 1 ponto
    pontos_congresso = qte_trabcongresso*2
    if pontos_congresso>10:
        pontos_congresso=10

    ## Ponderação das Orientações
    # Orientações Concluídas	
    # - Tese de Doutorado	       x 2 pontos
    # - Dissertação de Mestrado	   x 2 pontos
    # - TCC (teto 10 TCCs)	       x 1 ponto
    # Orientações Concluídas de IC 
    # - PIBIC/PIBIT/FUNCAP/CNPq	   x 1 ponto    
    pontos_orient_ic+=qte_ic*1
    pontos_orient_grad+=qte_tcc*1
    if pontos_orient_grad > 10:
        pontos_orient_grad = 10
    pontos_orient_mest+=qte_mest*2
    pontos_orient_dout+=qte_dout*2
  
    ## Totalização dos pontos
    pontos_orient=pontos_orient_ic+pontos_orient_grad+pontos_orient_mest+pontos_orient_dout

    ## IMPRESSÃO   
    print('='*125)
    print(dict_id.get('Nome'))
    print(f'    {qte_trabcongresso:3} Trabalhos publicados em congresso no período do edital (de um total de {qte_trabcongresso_total})')    
    print(f'    {qte_artperiodicos:3} Artigos publicados em perióridos  no período do edital (de um total de {artigos_todos_tempos})')
    print(f'    {qte_orientacoes:3} Orientações acadêmicas concluídas no periodo do edital (de um total de {qte_orientacoes_total})')
    # print(f'    {pontos_orient_ic:02} pontos por orientar {qte_ic:02} alunos de Iniciação Científica: ')
    # print(f'    {pontos_orient_grad:02} pontos por orientar {qte_tcc:02} alunos de Graduação/Especialização')
    # pontos_orient_mest = qte_mest*2
    # print(f'    {pontos_orient_mest:02} pontos por orientar {qte_mest:02} alunos de Mestrados')
    # pontos_orient_dout = qte_dout*2
    # print(f'    {pontos_orient_dout:02} pontos por orientar {qte_dout:02} alunos de Doutorados')

    print(f'{pontos_public+pontos_livros+pontos_congresso+pontos_orient:4} pontos no total, detalhados conforme a seguir:')
    print(f'    {pontos_public:4}pnt por publicar artigo completo: {qte_jcr_superior:02} JCI >= 1.1; {qte_jcr_inferior:02} JCI entre 0.5 a 1.1; {qte_jcr_faltante:02} sem JCI no Lattes')
    print(f'    {pontos_livros:4}pnt por publicar livro/capitulos: {qte_livros:02} livro completo publicado/organizado; {qte_capitulos:02} capítulos de livros publicado')
    print(f'    {pontos_congresso:4}pnt por trabalho publ. congresso: {qte_trabcongresso:02} trabalhos publicados em anais de congressos')
    print(f'    {pontos_orient:4}pnt por todas orientações concl.: {qte_ic:02} iniciação científica; {qte_tcc:02} graduações/especialização; {qte_mest:02} mestrados; {qte_dout:02} doutorados')        

In [ ]:
chaves_producoes = ['Artigos completos publicados em periódicos', 
                    'Citações', 
                    'Capítulos de livros publicados', 
                    'Resumos expandidos publicados em anais de congressos', 
                    'Resumos publicados em anais de congressos', 
                    'Resumos publicados em anais de congressos (artigos)', 
                    'Artigos  aceitos para publicação', 
                    'Apresentações de Trabalho', 
                    'Assessoria e consultoria', 
                    'Programas de computador sem registro', 
                    'Produtos tecnológicos', 
                    'Trabalhos técnicos', 
                    'Entrevistas, mesas redondas, programas e comentários na mídia'])

In [ ]:
j = {'Tese de doutorado': {'1.': 'Anna Carolina Machado Marinho. Expressão, caracterização estrutural e ensaios de estabilidade de nanocorpos e construtos relacionados, com vistas ao incremento da soroterapia antiofídica. Início: 2020. Tese (Doutorado em Doutorado em Ciências Farmacêuticas da Universidade Federal do Ceará)  - Fundação Oswaldo Cruz CE. (Orientador).'}}
len([x for x in j.get('Tese de doutorado')])

In [ ]:
artigos

In [ ]:
livros

In [ ]:
trabalhos

In [ ]:
from pprint import pprint
for x in dict_list_docents:
    dict_prods = x.get('Produções')
    # pprint([x for x in dict_prods.keys()])
    if dict_prods:
        tecnologias = [dict_prods.get('Produtos tecnológicos')]
        ignorar = ['curso','plano','protocolo ']
        if tecnologias:
            if 
            print(tecnologias)
    else:
        print('Produtos tecnológicos não encontrados')

In [ ]:
tipos=[]

for i in [x.get('Livros publicados/organizados ou edições') for x in dict_list_docents if x.get('Livros publicados/organizados ou edições')]:
    if i is not None:
        for tipo in i:
            if tipo.keys() not in tipos:
                tipos.append(tipo.keys()) 
            try:
                qic = tipo.get('Dissertação de mestrado')
            except:
                qic = 0
            if qic:
                lista = [x for x in qic.values()]
    else:
        print('Subchaves não encontradas')
        qic = 0

for i in tipos:
    print(list(i)[0])

In [ ]:
import re
import collections
from pprint import pprint
tipos=[]

producoes_subkeys = ['Artigos completos publicados em periódicos', 
    'Citações',
    'Livros publicados/organizados ou edições',
    'Capítulos de livros publicados',
    'Trabalhos completos publicados em anais de congressos',
    'Resumos expandidos publicados em anais de congressos',
    'Resumos publicados em anais de congressos',
    'Apresentações de Trabalho',
    'Assessoria e consultoria',
    'Trabalhos técnicos',
    'Entrevistas, mesas redondas, programas e comentários na mídia']

# Verificar orientações concluídas de IC nos dados de docentes
for i in [x.get('Orientações').get('Orientações e supervisões concluídas') for x in dict_list_docents if x.get('Orientações')]:
    if i is not None:
        for tipo in i:
            if tipo.keys() not in tipos:
                tipos.append(tipo.keys()) 
            try:
                qic = tipo.get('Dissertação de mestrado')
            except:
                qic = 0
            if qic:
                lista = [x for x in qic.values()]
    else:
        qic = 0

for i in tipos:
    print(list(i)[0])

In [ ]:
keylevel_one = 'Produções'
keylevel_two = 'Artigos completos publicados em periódicos'
data_measure = 'fator_impacto_jcr'
curriculo_id = 44
ano_inicio = 2020
ano_final = 2024

class_mapping = {
    '0p (sem JCR)': 0,
    '6p (0.5 < JCR <= 1.0)': 0,
    '8p (JCR > 1.0)': 0
}

# <b>F04: Avaliar programa de pós PPGCS Fiocruz-MG

## Indicadores do Programa PPGCS

### 1. Pontuação por Fator de Impacto (PFI >=600)
- Meta: PFI >= 600 em pelo menos 70% dos docentes

    Indicador: Total de pontos conforme periódicos das publicações no período
     Objetivo: Publicar trabalhos em periódicos de elevado impacto
               
         Meta: 70% dos docentes permanentes com PFI >= 600 pontos no quadriênio
               (150/ano e ao menos 03 artigos A, no mínimo 02 em A1, ou 04 artigos A2);
 
      Cálculo: Soma ponderada pela estratificação Qualis de acordo com o que segue:
        A1 = 100 pontos
        A2 = 80 pontos
        B1 = 60 pontos
        B2 = 40 pontos
        B3 = 20 pontos
        B4 = 10 pontos
        B5 = 2 pontos.


Parâmetro para classificaçao do periódico:

        A1: FI Periódico ou CPD >= 4,300
        A2: FI Periódico ou CPD entre 2,950 e 4,299
        B1: FI Periódico ou CPD entre 1,800 e 2,949
        B2: FI Periódico ou CPD entre 1,100 e 1,799
        B3: FI Periódico ou CPD entre 0,300 e 1,099
        B4: FI Periódico ou CPD entre 0,001 e 0,299, (ou Scielo, Scimago, PubMed ou Web of Science)
        B5: Periódicos sem FI ou CPD e indexado nas lases Lilacs ou Latindex    

### 2. Produção Conjunta docentes/discentes (IPC >= 50%):
    Indicador: Índice de publicações com discentes por orientador (IPC)
     Objetivo: Em, pelo menos, 50 % dos artigos publicados deve constar discentes do programa
         Meta: IPC >= 50,00
      
      Cálculo:

$$\sum_{k=1}^{n}\, 100 * \frac{QPCD}{QPAT}$$

        onde:
               n = Artigos completos publicado em periódicos indexados
            QPCD = Qte. Publicação de Artigos com discentes do Programa na lista de autores
            QPAT = Qte. Publicação de Artigos Total no período avaliado



## Ponderação por extrato Qualis

#### Contar artigos estratificados pelo Qualis Periódicos

In [ ]:
# Definir os anos do período de interesse
ano_inicio = 2020
ano_final = 2024
atualizador.contar_qualis(dict_list_docents, ano_inicio, ano_final)

#### Classificar artigos no período pelo Qualis Periódicos

Obs.: 'Não encontrado' significa que o ISSN da revista da publicação não consta na lista de revistas avaliadas no Qualis Periódico

In [ ]:
# Definir os anos do período de interesse
ano_inicio = 2020
ano_final = 2024
atualizador.apurar_qualis_periodo(dict_list_docents, ano_inicio, ano_final).fillna('')

In [ ]:
# Definir os anos do período de interesse
ano_inicio = 2020
ano_final = 2024
df_pontuacao = atualizador.apurar_pontos_periodo(dict_list_docents, ano_inicio, ano_final)
df_pontuacao

# <b>F05: Obter produções dos Discentes do programa</b>

## Montar lista_busca para dados de Discentes

### Carregar nomes de planilha com dados de Discentes

In [ ]:
preparer = EnvironmentSetup()
discent_collab_counter = DiscentCollaborationCounter(dict_list_docents)

# fonte_planilha = 'ppgcs_estudantes_2021-2024.xlsx'
fonte_planilha = 'fioce_lista_alunos.xlsx'
dados_discentes = pd.read_excel(os.path.join(LattesScraper.find_repo_root(),'_data','in_xls',fonte_planilha), header=0)
dados_discentes

In [ ]:
# Ler dados do arquivo Excel do Setor de Recursos Humanos
pathdata = '_data/in_xls/'
datasheet = 'fioce_lista_alunos.xlsx'

# Ler apenas os cabeçalhos do arquivo Excel
headers = pd.read_excel(pathdata+datasheet, skiprows=0, header=0, nrows=0).columns
# headers

# Indicar quais colunas devem ser eliminadas na leitura
def cols_to_keep(col_name):
    return col_name not in []

# Filtrar cabeçalhos com base na função
selected_columns = [col for col in headers if cols_to_keep(col)]

# Ler dados do arquivo Excel do Setor de Recursos Humanos
fioce_alunos = pd.read_excel(pathdata+datasheet, skiprows=0, header=0, usecols=selected_columns)
print(f'{len(fioce_alunos.index)} quantidade total de alunos, todos vínculos e status')
print(f'{len(fioce_alunos["nome"].unique()):3} nomes únicos')

print('\nTipos de vínculos',list(fioce_alunos['vinculo'].unique()))
print(f"Quantidades por Nível de graduação\n{fioce_alunos['vinculo'].value_counts()}")

print('\n  Tipos de status',list(fioce_alunos['ativo'].unique()))
print('Quantidades por Tipos de status\n',(fioce_alunos['ativo'].value_counts()))
filtro1 = fioce_alunos['vinculo'].isin(['Graduação', 'Mestrado', 'Doutorado', 'Pós-Doc', 'Profsaúde'])
filtro2 = fioce_alunos['ativo'].isin([True, False])
# filtro2 = fioce_alunos['ativo'].isin([True])
lista_nomes = fioce_alunos[(filtro1) & (filtro2)]['nome'].unique().tolist()

print(f'\n{len(lista_nomes)} nomes de alunos em todos os status')
lista_busca_alunos = []
for i,nome in enumerate(lista_nomes):
    if nome.strip().title() not in lista_busca_alunos:
        lista_busca_alunos.append(nome.strip().title())
        print(f'{i+1:2}. {nome.title()}')

print(f'\n{len(lista_busca_alunos)} nomes únicos de alunos para extrair currículos')

## <b>Processar extração de dados de Discentes</b>
    (~80min/93nomes)

In [ ]:
# discent_collab_counter = DiscentCollaborationCounter(dict_list_docents)
# print(f'{len(lista_busca_alunos)} discentes relacionados aos programas')

# lista_normalizada_discentes=[]
# for i in lista_busca_alunos:
#     lista_normalizada_discentes.append(discent_collab_counter.iniciais_nome(i))

# t1 = time.time()
# termos_busca = ['Cruz', 'Família', 'Biotecnologia', 'Ceará']
# scraper = LattesScraper(termos_busca, 
#                         'bolt://localhost:7687', 'neo4j', 'password', 
#                         only_doctors=False)

# # Extrai e monta JSON com a lista de dicionários
# discents_dict_list = scraper.scrape(lista_busca_alunos, termos_busca)
# print(f'\n{scraper.tempo(t1,time.time())} para busca de {len(lista_busca_alunos)} nomes com extração de dados de {len(discents_dict_list)} dicionários')

In [ ]:
# ## Contagem de artigos para simples confererência
# print(f'{len(discents_dict_list)} dicionários montados')
# qte_artigos=0
# qte_titulos=0
# for k,i in enumerate(discents_dict_list):
#     try:
#         qte_jcr = len(i.get('Produções').get('Artigos completos publicados em periódicos'))
#     except:
#         qte_jcr = 0
#     try:
#         qte_jcr2 = len(i['JCR2'])
#     except:
#         qte_jcr2 = 0

#     qte_artigos+=qte_jcr
#     qte_titulos+=qte_jcr2
#     status=qte_jcr2-qte_jcr
#     print(f"{k:>2}C {qte_jcr:>03}A {qte_jcr2:>03}T Dif:{status:>03} {i.get('Identificação').get('name')} ")

# print(f'\nTotal de artigos em todos períodos: {qte_artigos}')
# print(f'Total de títulos em todos períodos: {qte_titulos}')

### Identificar currículos remanescentes

In [ ]:
# termos_busca = ['Cruz', 'Família', 'Biotecnologia', 'Ceará']
# lista_restante = scraper.avaliar_remanescentes(lista_busca_alunos, discents_dict_list)

### Adicionar nomes ou novos termos, se necessário

In [ ]:
# # lista_restante.append('Caroline Pereira Bittencourt Passaes')
# for i in lista_restante:
#     print(f'   {i}')

### Extrair currículos remanescentes ou adicionais

In [ ]:
# # lista_dict_combinado = extract_remanescents(lista_restante, dict_list_actual)
# lista_dict_combinado = scraper.extract_remanescents(lista_restante, discents_dict_list, termos_busca)
# filepath = os.path.join(folder_data_input,'dict_list_discents.json')

In [ ]:
# print(f'{len(lista_dict_combinado)} dicionários de discentes extraídos')
# try:
#     exemplo = [x.get('Produções') for x in lista_dict_combinado][0].get('Artigos completos publicados em periódicos')[0]
#     if exemplo:
#         print('\n\nExemplo de dados dos artigos:')
#         print(exemplo)
# except:
#     pass

In [ ]:
from lattes_scrapper import GetQualis
stratifier = GetQualis()

# Acrescentar Qualis periódicos aos dicionários de docentes
print('\nAdicionando Qualis Periódicos')
pathfilename = os.path.join(folder_data_input,'discents_dict_list.json')
stratifier.buscar_qualis_e_atualizar_arquivo(lista_dict_combinado, pathfilename)
scraper.save_to_json(lista_dict_combinado, pathfilename)

print(f'{len(lista_dict_combinado)} dicionários com currículos completos extraídos')
print('\n\nExemplo de dados dos artigos:')
try:
    exemplo = [x.get('Produções') for x in lista_dict_combinado][0].get('Artigos completos publicados em periódicos')[0]
    if exemplo:
        print('\n\nExemplo de dados dos artigos:')
        print(exemplo)
except:
    pass

## Ler dados salvos de Discentes

### Listar arquivos salvos na pasta de entrada

In [ ]:
folder_data_input = os.path.join(os.getcwd(),'_data','in_csv')
os.listdir(folder_data_input)

### Carregar dados completos dos Discentes

In [ ]:
filename = 'discents_dict_list.json'
pathfilename = os.path.join(folder_data_input, filename)
dict_list_discents, formatted_creation_date, formatted_modification_date, time_count, unit = jfm.load_from_json(pathfilename)
print(f'{len(dict_list_discents)} Total de currículos extaídos')
[i.get('Identificação').get('Nome') for i in dict_list_discents]

In [ ]:
# Verificar orientações nos dados de docentes
# [x.get('Orientações') for x in dict_list_discents if x.get('Orientações')]

## <b>Avaliar colaboração discente/docentes</b>

In [ ]:
# for dic in dict_list_discents:
#     a = dic.get('Produções', {}).get('Artigos completos publicados em periódicos', {})
#     print(a)

In [ ]:
#### TO-DO #### corrigir busca pelo nome de discentes nos dados de pulicação de docentes.
discent_collab_counter = DiscentCollaborationCounter(dict_list_docents)
colaboracoes, percentuais = discent_collab_counter.get_articles_coauthorings(dict_list_docents, ano_inicio=2017, ano_final=2024)

In [ ]:
len(colaboracoes)

In [ ]:
len(percentuais)

In [ ]:
len(df_pontuacao.index)

In [ ]:
## Acrescentar a coluna de percentual de colaboração docente/discente
df_pontuacao['colab_disc'] = percentuais
filepath = os.path.join(os.path.join("./","_data","powerbi",'fioce_prodpubl_2017_2024.xlsx'))
df_pontuacao.to_excel(filepath)

In [ ]:
print(f'{len(df_pontuacao.index)} pesquisadores')
df_pontuacao

In [ ]:
pathfilename = os.path.join(os.path.join("./","_data","powerbi",'fioce_prodpubl_discentcollab_2017_2024.xlsx'))
df_pontuacao.to_excel(pathfilename)

## <b>Acrescentar Qualis Periódicos</b>

### Abrir dados localmente de Docentes e Discentes

In [ ]:
from pathlib import Path
from getpass import getpass
from datetime import datetime
from pprint import pprint
from IPython.display import clear_output
import pandas as pd, os, re, sys, time, pytz, json, subprocess

## Configurar exibição do pandas para melhor visualizar os dados
pd.set_option('display.max_colwidth', None)
pd.set_option('colheader_justify', 'left')
pd.set_option('display.max_rows', 600)

def find_repo_root(path='.', depth=10):
    ''' 
    Busca o arquivo .git e retorna string com a pasta raiz do repositório
    '''
    # Limitar profundidade para evitar loop infinito
    if depth < 0:
        return None
    path = Path(path).absolute()
    if (path / '.git').is_dir():
        return path
    return find_repo_root(path.parent, depth-1)

## Definir a pasta de base do repositório local
base_repo_dir = find_repo_root()

## Sempre construir os caminhos usando os.path.join para compatibilidade WxL
folder_utils = os.path.join(base_repo_dir, 'utils')
folder_domain = os.path.join(base_repo_dir, 'source', 'domain')
folder_data_xls = os.path.join(base_repo_dir, '_data', 'in_xls')
folder_data_input = os.path.join(base_repo_dir, '_data', 'in_csv')
folder_data_output = os.path.join(base_repo_dir, '_data', 'output')

## Adicionar pastas locais ao sys.path para importar pacotes criados localmente
sys.path.append(folder_utils)
sys.path.append(folder_domain)
from scraper_pasteur import PasteurScraper
from environment_setup import EnvironmentSetup
from scraper_sucupira import SucupiraScraper
from scraper_sucupira_edge import SucupiraScraperEdge
from chromedriver_manager import ChromeDriverManager
from neo4j_persister import Neo4jPersister
from lattes_scrapper import JSONFileManager, LattesScraper, HTMLParser, SoupParser, GetQualis, ArticlesCounter, DiscentCollaborationCounter, DictToHDF5, attribute_to_be_non_empty

# Carregar o conteúdo do arquivo 'dict_list.json' para a variável dict_list
jfm = JSONFileManager()
jfm.list_json(folder_data_input)

# Carregar o conteúdo do arquivo da extração de docentes para a variável dict_list_docents
filename_docents = 'docents_dict_list.json'
dict_list_docents, formatted_creation_date, formatted_modification_date, time_count, unit = jfm.load_from_json(os.path.join(folder_data_input,filename_docents))

print(f"\n{len(dict_list_docents)} currículos carregados na lista de dicionários de docentes '{filename_docents}'")
print(f"Arquivo criado inicialmente em {formatted_creation_date} carregado com sucesso")
print(f"Extração realizada em {formatted_modification_date} a {time_count} {unit}")
print('\nExemplo dos dados das publicações de docentes:')
pprint([x.get('Produções') for x in dict_list_docents][-1].get('Artigos completos publicados em periódicos')[0])

# Carregar o conteúdo do arquivo da extração de discentes para a variável dict_list_discents
filename_discents = 'discents_dict_list.json'
dict_list_discents, formatted_creation_date_discents, formatted_modification_date_discents, time_count, unit = jfm.load_from_json(os.path.join(folder_data_input,filename_discents))

print(f"\n{len(dict_list_discents)} currículos carregados na lista de dicionários de discentes '{filename_discents}'")
print(f"Arquivo criado inicialmente em {formatted_creation_date_discents} carregado com sucesso")
print(f"Extração realizada em {formatted_modification_date_discents} a {time_count} {unit}")
print('\nExemplo dos dados das publicações de discentes:')
pprint([x.get('Produções') for x in dict_list_discents][1].get('Artigos completos publicados em periódicos')[0])

### Atualizar dados dos Qualis Periódicos

In [ ]:
# stratifier = GetQualis()

# print('\nAdicionar Qualis Periódicos a publicações dos docentes...')
# pathfilename = os.path.join(folder_data_input,'docents_dict_list.json')
# json_data_discents = stratifier.buscar_qualis_e_atualizar_arquivo(dict_list_docents, pathfilename)

# print('\nAdicionar Qualis Periódicos a publicações dos discentes...')
# pathfilename = os.path.join(folder_data_input,'discents_dict_list.json')
# json_data_discents = stratifier.buscar_qualis_e_atualizar_arquivo(dict_list_discents, pathfilename)

# print('\nExemplo atualizado dos dados das publicações de docentes:')
# # Verificar se o dado Qualis está presente no arquivo de dados de docentes
# pprint([x.get('Produções') for x in dict_list_docents][-1].get('Artigos completos publicados em periódicos')[0])

# print('\nExemplo atualizado dos dados das publicações de discentes:')
# # Verificar se o dado Qualis está presente no arquivo de dados de discentes
# pprint([x.get('Produções') for x in dict_list_discents][1].get('Artigos completos publicados em periódicos')[0])

## Montar Grafo com NetworkX

In [ ]:
# %pip install community
# %pip install sentence_transformers

In [ ]:
## Teste de criação de link simbólico
# import os

# try:
#     os.symlink("arquivo_original.txt", "link_simbolico.txt")
#     print("Link simbólico criado com sucesso!")
# except OSError as e:
#     print(f"Erro ao criar o link simbólico: {e}")

In [ ]:
import torch
import logging
import networkx as nx
import community as community_louvain
from neo4j import GraphDatabase
from sentence_transformers import SentenceTransformer
from sklearn.metrics.cluster import adjusted_rand_score
# from sklearn.metrics.pairwise import cosine_similarity # apresentou erro de sincronização CUDA
from torch.nn.functional import cosine_similarity  # Similaridade do cosseno no PyTorch
from transformers import AutoTokenizer, AutoModel

# Configurar o logger
logging.basicConfig(filename='app_semantic_similarity.log', level=logging.INFO, 
                    format='%(asctime)s - %(levelname)s - %(message)s')

def test_gpu():
    """
    Testa se a GPU está disponível e retorna informações sobre ela.
    """
    if torch.cuda.is_available():
        logging.info("GPU disponível. Informações:")
        logging.info(torch.cuda.get_device_name(0))
        logging.info(f"Memória total: {torch.cuda.get_device_properties(0).total_memory / 1024**2:.2f} MB")
        return True
    else:
        logging.warning("GPU não disponível.")
        return False

def is_gpu_memory_sufficient(model_name):
    """
    Verifica se a memória da GPU é suficiente para o modelo especificado.
    """
    try:
        model = SentenceTransformer(model_name)
        del model
        return True
    except RuntimeError as e:
        if "CUDA out of memory" in str(e):
            logging.warning(f"Memória da GPU insuficiente para o modelo {model_name}.")
            return False
        else:
            raise

def clear_gpu_memory():
    """
    Limpa a memória da GPU.
    """
    torch.cuda.empty_cache()
    logging.info("Memória da GPU limpa.")

class Neo4jError(Exception):
    """Exceção personalizada para erros relacionados ao Neo4j."""
    pass

class CommunityDetectionError(Exception):
    """Exceção personalizada para erros na detecção de comunidades."""
    pass

def get_graph_from_neo4j(uri, user, password, query):
    """
    Conecta ao Neo4j, executa a consulta Cypher e retorna o grafo NetworkX.
    """
    try:
        driver = GraphDatabase.driver(uri, auth=(user, password))
    except Exception as e:
        logging.error(f"Erro ao conectar ao Neo4j: {e}")
        raise ConnectionError(f"Erro ao conectar ao Neo4j: {e}")

    with driver.session() as session:
        try:
            result = session.run(query)
        except Exception as e:
            logging.error(f"Erro ao executar a consulta Cypher: {e}")
            raise Neo4jError(f"Erro ao executar a consulta Cypher: {e}")

        G = nx.Graph()
        for record in result:
            try:
                node1 = record['n']
                node2 = record['r']

                # Adicionar nós ao grafo
                G.add_node(node1.id, label=list(node1.labels)[0], name=node1.get('name', ''))
                if node2:
                    G.add_node(node2.id, label=node2.type)

                    # Adicionar aresta ao grafo
                    G.add_edge(node1.id, node2.id)
            except Exception as e:
                logging.error(f"Erro ao processar os dados do Neo4j: {e}")
                raise ValueError(f"Erro ao processar os dados do Neo4j: {e}")

    driver.close()
    return G

def semantic_approximation_and_modularity(graph, label1, label2, threshold_range, model_name='bert-base-uncased'):
    """
    Calcula a aproximação semântica entre dois labels de nós e avalia a modularidade.

    Args:
        graph: Grafo NetworkX contendo os nós e arestas.
        label1: Primeiro label de nó.
        label2: Segundo label de nó.
        threshold_range: Range de valores de threshold para testar.
        model_name: Nome do modelo a ser usado para cálculo de embeedings.

    Returns:
        Dicionário com resultados para cada threshold, incluindo:
            - modularity: Valor de modularidade.
            - communities: Dicionário com as comunidades encontradas.
            - edges: Lista de arestas adicionadas ao grafo.
    """

    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    model = AutoModel.from_pretrained(model_name).to(device)

    results = {}

    # Obter nós com os labels especificados
    nodes_label1 = [node for node, data in graph.nodes(data=True) if data.get('label') == label1]
    nodes_label2 = [node for node, data in graph.nodes(data=True) if data.get('label') == label2]

    if not nodes_label1 or not nodes_label2:
        raise ValueError(f"Labels de nós não encontrados no grafo: {label1}, {label2}")

    for threshold in threshold_range:
        edges_to_add = []
        for node1 in nodes_label1:
            for node2 in nodes_label2:
                try:
                    text1 = graph.nodes[node1].get('name', '')
                    text2 = graph.nodes[node2].get('name', '')

                    # Tokenizar e obter embeddings com PyTorch
                    inputs1 = tokenizer(text1, return_tensors="pt", padding=True, truncation=True).to(device)
                    inputs2 = tokenizer(text2, return_tensors="pt", padding=True, truncation=True).to(device)
                    with torch.no_grad():
                        outputs1 = model(**inputs1)
                        outputs2 = model(**inputs2)
                    embedding1 = outputs1.pooler_output.cpu().numpy()  # Converter para numpy
                    embedding2 = outputs2.pooler_output.cpu().numpy()  # Converter para numpy

                    similarity = cosine_similarity(torch.from_numpy(embedding1), torch.from_numpy(embedding2))[0][0].item()  # Converter para escalar
                except Exception as e:
                    logging.error(f"Erro ao calcular a similaridade entre embeddings: {e}")
                    raise

                if similarity >= threshold:
                    edges_to_add.append((node1, node2))    

        # Criar subgrafo com os nós e arestas relevantes
        subgraph = graph.subgraph(nodes_label1 + nodes_label2 + ['CompetenciaPesquisa'])
        subgraph.add_edges_from(edges_to_add)

        # Calcular modularidade
        try:
            partition = community_louvain.best_partition(subgraph)
            modularity = community_louvain.modularity(partition, subgraph)
        except Exception as e:
            logging.error(f"Erro ao detectar comunidades: {e}")
            raise CommunityDetectionError(f"Erro ao detectar comunidades: {e}")

        results[threshold] = {
            'modularity': modularity,
            'communities': partition,
            'edges': edges_to_add
        }

    return results                    

In [ ]:

# def semantic_approximation_and_modularity(graph, label1, label2, threshold_range, model_name='paraphrase-distilroberta-base-v2'):
#     """
#     Calcula a aproximação semântica entre dois labels de nós e avalia a modularidade.

#     Args:
#         graph: Grafo NetworkX contendo os nós e arestas.
#         label1: Primeiro label de nó.
#         label2: Segundo label de nó.
#         threshold_range: Range de valores de threshold para testar.
#         model_name: Nome do modelo SentenceTransformer a ser usado (opcional).

#     Returns:
#         Dicionário com resultados para cada threshold, incluindo:
#             - modularity: Valor de modularidade.
#             - communities: Dicionário com as comunidades encontradas.
#             - edges: Lista de arestas adicionadas ao grafo.
#     """

#     if test_gpu():
#         if not is_gpu_memory_sufficient(model_name):
#             model_name = 'all-mpnet-base-v2'  # Modelo menor
#             logging.info(f"Usando modelo menor: {model_name}")
#     else:
#         logging.info("Usando CPU.")

#     clear_gpu_memory()  # Limpar a memória da GPU antes de usar o modelo

#     try:
#         # Tentar usar a GPU primeiro
#         model = SentenceTransformer(model_name)
#     except RuntimeError as e:
#         if "CUDA" in str(e):
#             logging.warning(f"Erro de CUDA: {e}. Forçando o uso da CPU...")
#             # Forçar o uso da CPU
#             model = SentenceTransformer(model_name, device='cpu')
#         else:
#             raise  # Re-lançar a exceção se não for um erro CUDA

#     results = {}

#     # Obter nós com os labels especificados
#     nodes_label1 = [node for node, data in graph.nodes(data=True) if data.get('label') == label1]
#     nodes_label2 = [node for node, data in graph.nodes(data=True) if data.get('label') == label2]

#     if not nodes_label1 or not nodes_label2:
#         raise ValueError(f"Labels de nós não encontrados no grafo: {label1}, {label2}")

#     for threshold in threshold_range:
#         edges_to_add = []
#         for node1 in nodes_label1:
#             for node2 in nodes_label2:
#                 try:
#                     text1 = graph.nodes[node1].get('name', '')
#                     text2 = graph.nodes[node2].get('name', '')
#                     embedding1 = model.encode(text1).reshape(1, -1)
#                     embedding2 = model.encode(text2).reshape(1, -1)
#                     similarity = cosine_similarity(embedding1, embedding2)[0][0]
#                 except Exception as e:
#                     logging.error(f"Erro ao calcular a similaridade entre embeddings: {e}")
#                     raise

#                 if similarity >= threshold:
#                     edges_to_add.append((node1, node2))

#         # Criar subgrafo com os nós e arestas relevantes
#         subgraph = graph.subgraph(nodes_label1 + nodes_label2 + ['CompetenciaPesquisa'])
#         subgraph.add_edges_from(edges_to_add)

#         # Calcular modularidade
#         try:
#             partition = community_louvain.best_partition(subgraph)
#             modularity = community_louvain.modularity(partition, subgraph)
#         except Exception as e:
#             logging.error(f"Erro ao detectar comunidades: {e}")
#             raise CommunityDetectionError(f"Erro ao detectar comunidades: {e}")

#         results[threshold] = {
#             'modularity': modularity,
#             'communities': partition,
#             'edges': edges_to_add
#         }

#     return results

In [ ]:
# Exemplo de uso
uri = "bolt://localhost:7687"
user = "neo4j"
password = "password"

query = """
MATCH (n)
WHERE NOT n:Revista OR EXISTS(()-[:PUBLICADO_EM]->(n))
OPTIONAL MATCH (n)-[r]-() 
RETURN n, r
"""

G = get_graph_from_neo4j(uri, user, password, query)
results = semantic_approximation_and_modularity(G, 'AreaAvaliacao', 'GrandeArea', [0.5, 0.6, 0.7, 0.8])
print(results)

In [ ]:
results

# <b>F06: Montar grafo/análise de redes</b>

In [ ]:
uri = "bolt://localhost:7687"
user = "neo4j"
password = "password"
persister = Neo4jPersister(uri, user, password)

### Persistir dados de revistas (14min 31.625 periódicos)

In [ ]:
## Persiste dados da lista Sucupira no Neo4j dados de > 31.000 revistas
# t1 = time.time()
# persister.persistir_revistas_da_planilha()
# print(f'\n{preparer.tempo(t1,time.time())} para persistir dados de todas 31.625 revistas da Plataforma Sucupira')

### Persistir dados dos docentes

In [ ]:
persister.persist_docent_nodes(dict_list_docents)

In [ ]:
persister.persist_areas_nodes(dict_list_docents)

In [ ]:
persister.persist_producoes_pesquisador(dict_list_docents)

In [ ]:
persister.persist_pesquisador_grande_area_relationships(dict_list_docents)

### Persistir dados de discentes

In [ ]:
persister.persist_discent_nodes(dict_list_discents)

In [ ]:
persister.persist_producoes_pesquisador(dict_list_discents)

In [ ]:
persister.persist_areas_nodes(dict_list_discents)

In [ ]:
persister.persist_pesquisador_grande_area_relationships(dict_list_discents)

### Persistir dados de orientações

In [ ]:
t1 = time.time()
preparer = EnvironmentSetup()
persister.persist_advices_relationships(dict_list_docents)
print(f'\n{preparer.tempo(t1,time.time())} para persistir dados de todas orientações nos dados de docentes')

In [ ]:
# [x.keys() for x in dict_list_docents]
[x.get('Produções') for x in dict_list_docents][1].get('Artigos completos publicados em periódicos')[0]

In [ ]:
[x.get('Orientações') for x in dict_list_docents][4]

In [ ]:
[x.get('Orientações') for x in dict_list_discents][2]

In [ ]:
print(f'\n{preparer.tempo(t00,time.time())} para recuperar, processar e persistir dados.')

# <b>F07: Visualizar grafos e análises geradas</b>

In [ ]:
uri = "bolt://localhost:7687"
user = "neo4j"
password = "password"
persister = Neo4jPersister(uri, user, password)

In [ ]:
persister.desenhar_grafo_revistas_capes()

In [ ]:
# %pip install groq
# %pip install langchain-groq

# Interação via LLM Llama3

In [ ]:
import os
from groq import Groq

keys,_,_,_,_ = jfm.load_from_json(os.path.join('../../../','secrets.json'))
client = Groq(
    api_key=keys.get('groq'),
)

chat_completion = client.chat.completions.create(
    messages=[
        {
            "role": "user",
            "content": "Explain the importance of fast language models",
        }
    ],
    # model="llama3-8b-8192",
    model = 'llama3-70b-8192',
)

print(chat_completion.choices[0].message.content)

In [ ]:
import os
from groq import Groq

keys,_,_,_,_ = jfm.load_from_json(os.path.join('../../../','secrets.json'))
client = Groq(
    api_key=keys.get('groq'),
)

chat_completion = client.chat.completions.create(
    messages=[
        {
            "role": "user",
            "content": "Gerenate a anime history about StarWars, and present the response in Brazilian Portuguese",
        }
    ],
    # model="llama3-8b-8192",
    model = 'llama3-70b-8192',
)

print(chat_completion.choices[0].message.content)

In [ ]:
import os
from groq import Groq

keys,_,_,_,_ = jfm.load_from_json(os.path.join('../../../','secrets.json'))
client = Groq(
    api_key=keys.get('groq'),
)

chat_completion = client.chat.completions.create(
    messages=[
        {
            "role": "user",
            "content": "Explain the importance of fast language models",
        }
    ],
    # model="llama3-8b-8192",
    model = 'llama3-70b-8192',
)

print(chat_completion.choices[0].message.content)

In [ ]:
## Cypher from Natural Language
from typing import List, Optional
import json

from pydantic import BaseModel
from groq import Groq

groq = Groq(
    api_key=keys.get('groq'),
)

# Data model for LLM to generate
class Ingredient(BaseModel):
    name: str
    quantity: str
    quantity_unit: Optional[str]


class Recipe(BaseModel):
    recipe_name: str
    ingredients: List[Ingredient]
    directions: List[str]


def get_recipe(recipe_name: str) -> Recipe:
    chat_completion = groq.chat.completions.create(
        messages=[
            {
                "role": "system",
                "content": "You are a recipe database that outputs recipes in JSON.\n"
                # Pass the json schema to the model. Pretty printing improves results.
                f" The JSON object must use the schema: {json.dumps(Recipe.model_json_schema(), indent=2)}",
            },
            {
                "role": "user",
                "content": f"Fetch a recipe for {recipe_name}",
            },
        ],
        model="llama3-8b-8192",
        temperature=0,
        # Streaming is not supported in JSON mode
        stream=False,
        # Enable JSON mode setting the response format
        response_format={"type": "json_object"},
    )
    return Recipe.model_validate_json(chat_completion.choices[0].message.content)


def print_recipe(recipe: Recipe):
    print("Recipe:", recipe.recipe_name)

    print("\nIngredients:")
    for ingredient in recipe.ingredients:
        print(
            f"- {ingredient.name}: {ingredient.quantity} {ingredient.quantity_unit or ''}"
        )
    print("\nDirections:")
    for step, direction in enumerate(recipe.directions, start=1):
        print(f"{step}. {direction}")


recipe = get_recipe("apple pie")
print_recipe(recipe)

In [ ]:
from groq import Groq
import os
import json

client = Groq(api_key = keys.get('groq'))
MODEL = 'llama3-70b-8192'


# Example dummy function hard coded to return the score of an NBA game
def get_game_score(team_name):
    """Get the current score for a given NBA game"""
    if "warriors" in team_name.lower():
        return json.dumps({"game_id": "401585601", "status": 'Final', "home_team": "Los Angeles Lakers", "home_team_score": 121, "away_team": "Golden State Warriors", "away_team_score": 128})
    elif "lakers" in team_name.lower():
        return json.dumps({"game_id": "401585601", "status": 'Final', "home_team": "Los Angeles Lakers", "home_team_score": 121, "away_team": "Golden State Warriors", "away_team_score": 128})
    elif "nuggets" in team_name.lower():
        return json.dumps({"game_id": "401585577", "status": 'Final', "home_team": "Miami Heat", "home_team_score": 88, "away_team": "Denver Nuggets", "away_team_score": 100})
    elif "heat" in team_name.lower():
        return json.dumps({"game_id": "401585577", "status": 'Final', "home_team": "Miami Heat", "home_team_score": 88, "away_team": "Denver Nuggets", "away_team_score": 100})
    else:
        return json.dumps({"team_name": team_name, "score": "unknown"})

def run_conversation(user_prompt):
    # Step 1: send the conversation and available functions to the model
    messages=[
        {
            "role": "system",
            "content": "You are a function calling LLM that uses the data extracted from the get_game_score function to answer questions around NBA game scores. Include the team and their opponent in your response."
        },
        {
            "role": "user",
            "content": user_prompt,
        }
    ]
    tools = [
        {
            "type": "function",
            "function": {
                "name": "get_game_score",
                "description": "Get the score for a given NBA game",
                "parameters": {
                    "type": "object",
                    "properties": {
                        "team_name": {
                            "type": "string",
                            "description": "The name of the NBA team (e.g. 'Golden State Warriors')",
                        }
                    },
                    "required": ["team_name"],
                },
            },
        }
    ]
    response = client.chat.completions.create(
        model=MODEL,
        messages=messages,
        tools=tools,
        tool_choice="auto",
        max_tokens=4096
    )

    response_message = response.choices[0].message
    tool_calls = response_message.tool_calls
    # Step 2: check if the model wanted to call a function
    if tool_calls:
        # Step 3: call the function
        # Note: the JSON response may not always be valid; be sure to handle errors
        available_functions = {
            "get_game_score": get_game_score,
        }  # only one function in this example, but you can have multiple
        messages.append(response_message)  # extend conversation with assistant's reply
        # Step 4: send the info for each function call and function response to the model
        for tool_call in tool_calls:
            function_name = tool_call.function.name
            function_to_call = available_functions[function_name]
            function_args = json.loads(tool_call.function.arguments)
            function_response = function_to_call(
                team_name=function_args.get("team_name")
            )
            messages.append(
                {
                    "tool_call_id": tool_call.id,
                    "role": "tool",
                    "name": function_name,
                    "content": function_response,
                }
            )  # extend conversation with function response
        second_response = client.chat.completions.create(
            model=MODEL,
            messages=messages
        )  # get a new response from the model where it can see the function response
        return second_response.choices[0].message.content

user_prompt = "What was the score of the Warriors game?"
print(run_conversation(user_prompt))

# Outros testes e experimentos

In [ ]:
def avaliar_tipo_instancias_arvore(estrutura, nivel=1, identacao=""):
    """
    Função recursiva que avalia o tipo e a quantidade de instâncias em cada nível da estrutura, exibindo-a em formato de árvore.

    Args:
        estrutura (list|dict): A estrutura a ser avaliada.
        nivel (int): Nível atual da recurssão (inicia em 1).
        identacao (str): String de indentação para cada nível (inicia vazia).

    Returns:
        None: A função imprime os resultados na tela e não retorna nada.
    """

    if isinstance(estrutura, list):
        print(f"{identacao}N{nivel}. Lista: {len(estrutura)} elementos")
        for item in estrutura:
            avaliar_tipo_instancias_arvore(item, nivel + 1, identacao + "    ")

    elif isinstance(estrutura, dict):
        print(f"{identacao}N{nivel}. Mapa: {estrutura.keys()}")
        for chave, valor in estrutura.items():
            print(f"{identacao}  {chave}:")
            avaliar_tipo_instancias_arvore(valor, nivel + 1, identacao + "    ")

    elif isinstance(estrutura, str):
        print(f"{identacao}N{nivel}. String: {estrutura}")

for dict_pesq in dict_list_docents[:3]:
    avaliar_tipo_instancias_arvore(dict_pesq)

In [ ]:
for dict_pesq in dict_list_docents:
    if isinstance(dict_pesq, list):
        print(f'L1. Lista: {dict_pesq}')
    elif isinstance(dict_pesq, dict):
        print(f'L1. Mapa: {dict_pesq.keys()}')
        for tipo in dict_pesq.values():
            if isinstance(tipo, list):
                print(f'    L2. Lista: {tipo}')
            elif isinstance(tipo, dict):
                print(f'    L2. Mapa: {tipo}')
                for subtipo in tipo.values():
                    if isinstance(subtipo, list):
                        print(f'        L3. Lista: {len(subtipo)} elementos')
                        for subsubtipo in subtipo:
                            if isinstance(subsubtipo, list):
                                print(f'            L4. Lista: {subsubtipo}')
                            elif isinstance(subsubtipo, dict):
                                print(f'            L4. Mapa: {subsubtipo.keys()}')
                                for subsubsubtipo in subsubtipo.values():
                                    if isinstance(subsubsubtipo, list):
                                        print(f'                L5. Lista: {subsubsubtipo}')
                                    elif isinstance(subsubsubtipo, dict):
                                        print(f'                L5. Mapa: {subsubsubtipo.keys()}')
                                    elif isinstance(subsubsubtipo, str):
                                        print(f'                L5. String: {subsubsubtipo}')                                  
                            elif isinstance(subsubtipo, str):
                                print(f'            L4. String: {subsubtipo}')     
                    elif isinstance(subtipo, dict):
                        print(f'        L3. Mapa: {subtipo.keys()}')
                        for subsubtipo in subtipo.values():
                            if isinstance(subsubtipo, list):
                                print(f'            L4. Lista: {subsubtipo}')
                            elif isinstance(subsubtipo, dict):
                                print(f'            L4. Mapa: {subsubtipo.keys()}')
                            elif isinstance(subsubtipo, str):
                                print(f'            L4. String: {subsubtipo}')                             
                    elif isinstance(tipo, str):
                        print(f'        L3. String: {subtipo}')                
            elif isinstance(tipo, str):
                print(f'    L2. String: {tipo}')
    elif isinstance(dict_pesq, str):
        print(f'L1. String: {dict_pesq}')


In [ ]:
dict_list[20:21]

In [ ]:
list(dict_list[20].get('Identificação').items())

In [ ]:
list(dict_list[5].get('Idiomas'))

In [ ]:
list(x.get('Descrição') for x in dict_list[5].get('Linhas de Pesquisa'))

In [ ]:
list(dict_list[5].get('Áreas').values())

In [ ]:
tipos=[]
for pesq in dict_list:
    for t, s in pesq.get('Produções').items():
        if t not in tipos:
            tipos.append(t)
            print(t, type(s))

In [ ]:
list(dict_list[1].get('Produções').get('Artigos completos publicados em periódicos')[0].keys())

In [ ]:
list(dict_list[5].get('Atuação Profissional'))

In [ ]:
list(dict_list[5].get('Formação').items())

## Classe para gerar dados para grafos

In [ ]:
# from neo4j import GraphDatabase
# import json

# class Neo4jConnection:
#     def __init__(self, uri, user, password):
#         self._driver = GraphDatabase.driver(uri, auth=(user, password))

#     def close(self):
#         self._driver.close()

#     def persist_data(self, data):
#         with self._driver.session() as session:
#             for person_data in data:
#                 person_id = person_data['Identificação']['ID Lattes']
#                 prepared_data, relationships = self._prepare_data(person_data, person_id)
#                 session.write_transaction(self._create_person_node, person_id, prepared_data)
#                 self._create_relationships(session, person_id, relationships)

#     @staticmethod
#     def _create_person_node(tx, person_id, person_data):
#         tx.run(
#             "MERGE (p:Person {id_lattes: $person_id}) "
#             "SET p += $person_data",
#             person_id=person_id,
#             person_data=person_data
#         )

#     def _prepare_data(self, data, person_id):
#         prepared_data = {}
#         relationships = []
#         for key, value in data.items():
#             if isinstance(value, dict):
#                 label = key.capitalize().replace(' ', '_')
#                 prepared_data.update({f'{label}_{k}': v for k, v in value.items()})
#                 sub_prepared_data, sub_relationships = self._prepare_data(value, person_id)
#                 prepared_data.update(sub_prepared_data)
#                 relationships.extend(sub_relationships)
#                 relationships.append((label, {'label': 'Person', 'person_id': person_id}))
#             elif isinstance(value, list):
#                 for idx, item in enumerate(value):
#                     if isinstance(item, dict):
#                         nested_label = f'{key}_{idx}'
#                         nested_prepared_data, nested_relationships = self._prepare_data(item, person_id)
#                         prepared_data.update({f'{nested_label}_{k}': v for k, v in item.items()})
#                         prepared_data.update(nested_prepared_data)
#                         relationships.extend(nested_relationships)
#                         relationships.append((nested_label, {'label': key.capitalize().replace(' ', '_'), 'person_id': person_id}))
#                     elif isinstance(item, str):
#                         # Tratar strings
#                         if ":" in item:
#                             label, value = item.split(":", 1)
#                             prepared_data[f'{key}_{idx}'] = value.strip()
#                             relationships.append((label.strip(), {'label': key.capitalize().replace(' ', '_'), 'person_id': person_id}))
#                         else:
#                             prepared_data[f'{key}_{idx}'] = item.strip()
#         return prepared_data, relationships

#     def _create_relationships(self, session, person_id, relationships):
#         for label, parent_id in relationships:
#             query = (
#                 f"MATCH (p:Person {{id_lattes: '{person_id}'}}) "
#                 f"MATCH (n:{label} {{id_lattes: '{person_id}_{label}'}}) "
#                 f"MERGE (p)-[:HAS_{label}]->(n)"
#             )
#             if parent_id:
#                 query += (
#                     f" MERGE (parent:{parent_id['label']} {{id_lattes: '{parent_id['person_id']}'}}) "
#                     f"MERGE (parent)-[:HAS_{label}]->(n)"
#                 )
#             session.run(query)

# # Dados de conexão com o banco de dados Neo4j
# uri = "bolt://localhost:7687"
# user = "neo4j"
# password = "password"

# # Conecta-se ao banco de dados Neo4j e persiste os dados
# connection = Neo4jConnection(uri, user, password)
# connection.persist_data(dict_list)
# connection.close()

In [ ]:
# dict_list

In [ ]:
# from datetime import datetime
# from neo4j import GraphDatabase
# import ast

# class GraphPreparer:
#     def __init__(self, uri, user, password):
#         self._uri = uri
#         self._user = user
#         self._password = password
#         self._driver = None

#     def connect(self):
#         self._driver = GraphDatabase.driver(self._uri, auth=(self._user, self._password))

#     def prepare_data_from_file(self, file_path):
#         nodes = []
#         relationships = []

#         with open(file_path, 'r', encoding='utf-8') as file:
#             data = json.load(file)

#         for person_data in data:
#             print(person_data.keys())
#             person_id = person_data['Identificação'].get('ID Lattes')
#             nodes.append(('Pesquisador', {'id_lattes': person_id}))
            
#             for language in person_data.get('Idiomas', []):
#                 language_name = language['Idioma']
#                 proficiency = language['Proficiência']
#                 nodes.append(('Idioma', {'nome_idioma': language_name, 'proficiencia': proficiency}))
#                 relationships.append(('Pesquisador', {'id_lattes': person_id}, 'FALA', {'nome_idioma': language_name}))
            
#             for academic_info in person_data.get('Formação', {}).get('Acadêmica', []):
#                 description = academic_info['Descrição']
#                 nodes.append(('Curso', {'descricao': description}))
#                 relationships.append(('Pesquisador', {'id_lattes': person_id}, 'REALIZOU', {'descricao': description}))
                
#             for professional_info in person_data.get('Atuação Profissional', []):
#                 institution = professional_info['Instituição']
#                 description = professional_info['Descrição']
#                 relationships.append(('Pesquisador', {'id_lattes': person_id}, 'ATUA', {'instituicao': institution, 'descricao': description}))

#         return nodes, relationships

#     def persist_data(self, data_for_neo4j):
#         try:
#             with self._driver.session() as session:
#                 for data in data_for_neo4j:
#                     if data[0] == 'Node':
#                         label, properties = data[1:]
#                         session.write_transaction(self._create_node, label, **properties)
#                     elif data[0] == 'Relationship':
#                         start_label, rel_type, end_label = data[1:]
#                         session.write_transaction(self._create_relationship, start_label, rel_type, end_label)
#         except Exception as e:
#             print(f"Error persisting data: {e}")

#     @staticmethod
#     def _create_node(tx, label, **properties):
#         query = f"CREATE (n:{label} $props)"
#         tx.run(query, props=properties)

#     @staticmethod
#     def _create_relationship(tx, start_label, rel_type, end_label):
#         query = "MATCH (a:{start_label}), (b:{end_label}) " \
#                 "CREATE (a)-[r:{rel_type}]->(b)"
#         tx.run(query, start_label=start_label, rel_type=rel_type, end_label=end_label)

#     def close(self):
#         if self._driver is not None:
#             self._driver.close()

# # Exemplo de utilização:
# graph_preparer = GraphPreparer(uri="bolt://localhost:7687", user="neo4j", password="password")
# graph_preparer.connect()

# filepath = os.path.join(folder_data_input,'dict_list.json')

In [ ]:
# dict_list[0]['Idioma']

In [ ]:
# filepath

In [ ]:
# nodes, relationships = graph_preparer.prepare_data_from_file(filepath)

In [ ]:
# data_for_neo4j = nodes + relationships
# graph_preparer.persist_data(data_for_neo4j)

# graph_preparer.close()


In [ ]:
# from neo4j import GraphDatabase
# from datetime import datetime

# uri = "bolt://localhost:7687"
# user = "neo4j"
# password = "password"
# graph_preparer = GraphPreparer(uri, user, password) # Instanciar classe GraphPreparer
# graph_preparer.connect() # Conectar ao banco de dados Neo4j
# graph_preparer.process_data(dict_list) # Processar e persistir dados

# # Transformar os dados para o formato adequado do Neo4j
# dados_para_neo4j = graph_preparer.transform_data_for_neo4j(dict_list)
# graph_preparer.persist_nodes_and_relationships(dados_para_neo4j) # PersistiR nós e relações no Neo4j

In [ ]:
# dict_list

In [ ]:
# dados_para_neo4j[:15]

In [ ]:
# from neo4j import GraphDatabase
# # Agora você pode inserir os dados no Neo4j utilizando sua biblioteca de acesso ao banco de dados Neo4j, por exemplo:
# neo4j_driver = GraphDatabase.driver("bolt://localhost:7687", auth=("neo4j", "password"))
# with neo4j_driver.session() as session:
#     for item in data_for_neo4j:
#         label, properties = item
#         cypher_query = f"CREATE (:{label} $properties)"
#         session.run(cypher_query, properties=properties)

In [ ]:
# # Função para criar nós e relações
# def create_nodes_and_relationships(tx, nodes_and_relationships):
#     for item in nodes_and_relationships:
#         if len(item) == 3:  # Se for uma relação
#             origin_node, rel_type, dest_node = item
#             tx.run(
#                 f"MATCH (a), (b) WHERE a.name = $origin_node AND b.name = $dest_node "
#                 "CREATE (a)-[r:" + rel_type + "]->(b)",
#                 origin_node=origin_node, dest_node=dest_node
#             )

# # Conectando ao banco de dados Neo4j e executando a transação
# with GraphDatabase.driver(uri, auth=(user, password)) as driver:
#     with driver.session() as session:
#         session.write_transaction(create_nodes_and_relationships, relacoes)

In [ ]:
# import json

# class Neo4jGraphGenerator:
#     def __init__(self, dict_list):
#         self.dict_list = dict_list
#         self.graph_data = {'nodes': [], 'relationships': []}

#     def generate_graph_json(self):
#         for item in self.dict_list:
#             id_lattes = item.get('Identificação', {}).get('ID Lattes')
#             pesquisador = item.get('Identificação', {}).get('Nome')
            
#             # Adicionar nó de pessoa (Person)
#             person_node = {'id': id_lattes, 'label': 'Person', 'name': pesquisador}
#             self.graph_data['nodes'].append(person_node)

#             areas = item.get('Áreas', {})
#             for area in areas.values():
#                 # Adicionar nó de Grande Área (GrandeArea)
#                 grande_area_node = {'id': area['Grande Área'], 'label': 'GrandeArea', 'description': area['Grande Área']}
#                 self.graph_data['nodes'].append(grande_area_node)
#                 self.graph_data['relationships'].append({'source': id_lattes, 'target': area['Grande Área'], 'type': 'BELONGS_TO'})
                
#                 for subarea in area.get('Subáreas', []):
#                     # Adicionar nó de Área (Area)
#                     area_node = {'id': subarea['Área'], 'label': 'Area', 'description': subarea['Área']}
#                     self.graph_data['nodes'].append(area_node)
#                     self.graph_data['relationships'].append({'source': area['Grande Área'], 'target': subarea['Área'], 'type': 'BELONGS_TO'})
                    
#                     # Adicionar nó de Subárea (Subarea)
#                     subarea_node = {'id': subarea['Subárea'], 'label': 'Subarea', 'description': subarea['Subárea']}
#                     self.graph_data['nodes'].append(subarea_node)
#                     self.graph_data['relationships'].append({'source': subarea['Área'], 'target': subarea['Subárea'], 'type': 'BELONGS_TO'})

#         return json.dumps(self.graph_data, indent=4)

In [ ]:
# generator = Neo4jGraphGenerator(dict_list)
# generator.generate_graph_json()

In [ ]:
# import json
# import re
# from neo4j import GraphDatabase

# class AreasHandler:

#     def __init__(self, uri, user, password):
#         self._driver = GraphDatabase.driver(uri, auth=(user, password))

#     def close(self):
#         self._driver.close()
        
#     def consult_areas_atuacao(self, name):
#         with self._driver.session() as session:
#             result = session.run("MATCH (p:Person {name: $name}) RETURN p.`Áreas de atuação` as areas_atuacao", name=name)
#             record = result.single()
#             if record:
#                 return record['areas_atuacao']
#             return None

#     def debug_and_convert(self, areas_str):
#         try:
#             return json.loads(areas_str)
#         except json.JSONDecodeError:
#             print(f"Failed to deserialize JSON string: {areas_str}")
#             return None

#     def extract_subarea(self, area_detail):
#         # Extract the 'Subárea' content from the area detail
#         match = re.search(r'Subárea: ([^/]+)', area_detail)
#         if match:
#             return match.group(1).strip()
#         return None

#     def extract_areas(self, area_detail):
#         # Extract the 'Grande Área', 'Área', and 'Subárea' contents from the area detail
#         grande_area_match = re.search(r'Grande área: ([^/]+)', area_detail)
#         area_match = re.search(r'Área: ([^/]+)', area_detail)
#         subarea_match = re.search(r'Subárea: ([^/]+)', area_detail)
        
#         grande_area = grande_area_match.group(1).strip() if grande_area_match else None
#         area = area_match.group(1).strip() if area_match else None
#         subarea = subarea_match.group(1).strip() if subarea_match else None
        
#         return grande_area, area, subarea

#     def create_areas_relations(self, name):
#         # Get 'Áreas de atuação' properties
#         areas_properties = self.consult_areas_atuacao(name)

#         # Convert the serialized JSON strings back into dictionaries
#         try:
#             deserialized_areas_properties = self.debug_and_convert(areas_properties)
#         except Exception as e:
#             print(f"Error deserializing 'Áreas de atuação' properties: {e}")
#             return

#         successful_areas_creations = 0

#         with self._driver.session() as session:
#             for _, area_detail in deserialized_areas_properties.items():
#                 try:
#                     # Extracting Grande Área, Área, and Subárea from the details
#                     match = re.match(r'Grande área: (.*?) / Área: (.*?) / Subárea: (.*?)(?:/Especialidade: (.*?))?\.?$', area_detail)
#                     if not match:
#                         print(f"Unexpected format for 'Áreas de atuação' detail: {area_detail}")
#                         continue
#                     grande_area, area, subarea = match.groups()[:3]

#                     # Creating or merging nodes for Subárea, Área, and Grande Área
#                     session.run("MERGE (s:Subárea {name: $subarea})", subarea=subarea)
#                     session.run("MERGE (a:Área {name: $area})", area=area)
#                     session.run("MERGE (ga:GrandeÁrea {name: $grande_area})", grande_area=grande_area)

#                     # Creating or merging relationships. Using MERGE ensures no duplicate relationships are created.
#                     session.run("MATCH (p:Person {name: $name}), (s:Subárea {name: $subarea}) MERGE (p)-[r:ATUA_EM]->(s)", name=name, subarea=subarea)
#                     session.run("MATCH (ga:GrandeÁrea {name: $grande_area}), (a:Área {name: $area}) MERGE (ga)-[r:CONTÉM_ÁREA]->(a)", grande_area=grande_area, area=area)
#                     session.run("MATCH (a:Área {name: $area}), (s:Subárea {name: $subarea}) MERGE (a)-[r:CONTEM_SUBÁREA]->(s)", area=area, subarea=subarea)

#                     successful_areas_creations += 1
#                 except Exception as e:
#                     print(f"Error processing 'Áreas de atuação' detail '{area_detail}': {e}")

#             # Inform the user about areas
#             print(f"{successful_areas_creations} 'Áreas de atuação' relations successfully created.")

In [ ]:
# uri = "bolt://localhost:7687"
# user = "neo4j"
# password = "password"

# handleareas = AreasHandler(uri, user, password)
# name = 'Antonio Marcos Aires Barbosa'
# handleareas.consult_areas_atuacao(name)

In [ ]:
# from neo4j import GraphDatabase
# import urllib.parse
# import json
# import re

# class AdvisorHandler:

#     def __init__(self, uri, user, password):
#         self._driver = GraphDatabase.driver(uri, auth=(user, password))

#     def close(self):
#         self._driver.close()

#     @staticmethod
#     def convert_to_primitives(input_data):
#         if input_data is None:
#             return None
#         if isinstance(input_data, dict):
#             for key, value in input_data.items():
#                 if isinstance(value, dict):  
#                     input_data[key] = json.dumps(AdvisorHandler.convert_to_primitives(value), ensure_ascii=False)
#                 else:
#                     input_data[key] = AdvisorHandler.convert_to_primitives(value)
#             return input_data
#         elif isinstance(input_data, list):
#             return [AdvisorHandler.convert_to_primitives(item) for item in input_data]
#         elif isinstance(input_data, str):
#             if 'http://' in input_data or 'https://' in input_data:
#                 parts = input_data.split(" ")
#                 new_parts = [urllib.parse.quote(part) if part.startswith(('http://', 'https://')) else part for part in parts]
#                 return " ".join(new_parts)
#             return input_data
#         elif isinstance(input_data, (int, float, bool)):
#             return input_data
#         else:
#             return str(input_data)

#     @staticmethod
#     def debug_and_convert(input_data):
#         try:
#             return AdvisorHandler.convert_to_primitives(input_data)
#         except:
#             print("Conversion failed for:", input_data)
#             raise

#     def consult_orientacoes(self, name):
#         with self._driver.session() as session:
#             query = (
#                 "MATCH (p:Person {name: $name})"
#                 "RETURN p.Orientações AS orientacoes"
#             )
#             result = session.run(query, name=name)
#             orient_data = result.single()["orientacoes"]
#             if orient_data is None:
#                 raise ValueError(f"No data found for 'Orientações' attribute for Person '{name}'")
#             orient_properties_list = json.loads(orient_data)
#             return orient_properties_list

#     def create_advisor_relations(self, name):
#         # Get Orientações properties
#         orient_properties = self.consult_orientacoes(name)

#         # Convert the serialized JSON strings back into dictionaries
#         try:
#             deserialized_orient_properties = self.debug_and_convert(orient_properties)
#         except Exception as e:
#             print(f"Error deserializing Orientações properties: {e}")
#             return

#         # Advisory relationship mapping
#         advisory_types = {
#             "Dissertação de mestrado": "ORIENTOU_MESTRADO",
#             "Tese de doutorado": "ORIENTOU_DOUTORADO",
#             "Trabalho de conclusão de curso de graduação": "ORIENTOU_GRADUAÇÃO"
#         }

#         successful_advisory_creations = 0

#         with self._driver.session() as session:
#             for orientacao_category, advisories in deserialized_orient_properties.items():
#                 if isinstance(advisories, str):
#                     try:
#                         advisories = json.loads(advisories)
#                     except json.JSONDecodeError:
#                         print(f"Failed to deserialize JSON string in 'Orientações' for category '{orientacao_category}': {advisories}")
#                         continue

#                 if not isinstance(advisories, dict):
#                     print(f"Unexpected data type in 'Orientações' for category '{orientacao_category}': {advisories}")
#                     continue

#                 for advisory_type, relationships in advisories.items():
#                     relation_label = advisory_types.get(advisory_type)
#                     if not relation_label:
#                         continue  # skip if the advisory type is not one of the specified ones

#                     for _, detail in json.loads(relationships).items():
#                         try:
#                             student_name = detail.split(".")[0]
#                             title = detail.split(".")[1]
                            
#                             # Extract the year from the detail string
#                             year_match = re.search(r'(\d{4})', detail)
#                             year = year_match.group(1) if year_match else None

#                             # Create or merge the Orientações node
#                             node_query = (
#                                 "MERGE (a:Orientações {Title: $title}) "
#                                 "ON CREATE SET a.StudentName = $student_name, a.Tipo = $advisory_type, a.Year = $year "
#                                 "ON MATCH SET a.Tipo = $advisory_type, a.Year = $year "  # Ensure the 'Tipo' and 'Year' are always updated
#                                 "RETURN a"
#                             )
#                             session.run(node_query, title=title, student_name=student_name, advisory_type=advisory_type, year=year)

#                             # Create or update the advisory relationship
#                             relation_query = (
#                                 f"MATCH (p:Person {{name: $name}}), (a:Orientações {{Title: $title}}) "
#                                 f"MERGE (p)-[r:{relation_label}]->(a) "
#                             )
#                             session.run(relation_query, name=name, title=title)

#                             successful_advisory_creations += 1
#                         except Exception as e:
#                             print(f"Error processing advisory '{detail}': {e}")

#         # Inform the user about advisories
#         print(f"{successful_advisory_creations} orientações atualizadas com sucesso.")

In [ ]:
# from neo4j import GraphDatabase

# class DataRemovalHandler:

#     def __init__(self, uri, user, password):
#         """
#         Inicializa a classe DataRemovalHandler com informações de conexão ao banco de dados Neo4j.

#         Parâmetros:
#         - uri (str): URI de conexão ao Neo4j.
#         - user (str): Nome de usuário para autenticação.
#         - password (str): Senha para autenticação.
#         """
#         self._driver = GraphDatabase.driver(uri, auth=(user, password))

#     def close(self):
#         """
#         Fecha a conexão com o banco de dados Neo4j.
#         """
#         self._driver.close()

#     def delete_nodes_by_label(self, label):
#         """
#         Deleta todos os nós associados a um label específico no Neo4j.

#         Parâmetro:
#         - label (str): O label dos nós a serem deletados.

#         Retorna:
#         - int: O número de nós deletados.
#         """
#         with self._driver.session() as session:
#             # Esta consulta combina com todos os nós do label especificado e os deleta
#             result = session.run(f"MATCH (n:{label}) DETACH DELETE n RETURN count(n) as deleted_count")
#             deleted_count = result.single()["deleted_count"]
#             return deleted_count

## Interação dados do e-Lattes

- Fazer análise com lista dos nomes no e-lattes e baixar os arquivos gerados
- Salvar na pasta _data/in_zip

## Funções origem para classes

In [ ]:
# !pip3 install levenshtein
# !pip3 install editdistance
# !pip3 install seaborn
# !pip3 install pyjarowinkler

# import os
# import re
# import csv
# import json
# import time
# import json
# import zipfile
# import numpy as np
# import pandas as pd
# import plotly.express as px
# import plotly.graph_objects as go
# from string import Formatter
# from datetime import date, timedelta
# from datetime import datetime as dt
# from unidecode import unidecode
# from plotly.subplots import make_subplots
# from pyjarowinkler.distance import get_jaro_distance
# from IPython.display import clear_output, display, HTML

# pd.set_option('display.max_colwidth', None)
# pd.set_option('colheader_justify', 'left')

# class PreparadorDePublicacoes:
#     def __init__(self):
#         self.data = []
#         self.colunas = ['idLattes', 'nome', 'tipo', 'titulo_do_capitulo', 'idioma', 'titulo_do_livro', 'ano', 'doi', 'pais_de_publicacao', 'isbn', 
#         'nome_da_editora', 'numero_da_edicao_revisao', 'organizadores', 'paginas', 'autores', 'autores-endogeno', 'autores-endogeno-nome', 'tags', 
#         'Hash', 'tipo_producao', 'natureza', 'titulo', 'nome_do_evento', 'ano_do_trabalho', 'pais_do_evento', 'cidade_do_evento', 'classificacao', 
#         'periodico', 'volume', 'issn', 'estrato_qualis', 'editora', 'numero_de_paginas', 'numero_de_volumes']

#     def extrair_dados(self, registro, tipo_producao):
#         linha = {coluna: None for coluna in self.colunas}
#         linha['tipo_producao'] = tipo_producao  # Define o tipo de produção com base na chave do dicionário
        
#         # Mapear diretamente os campos do registro para a linha, assegurando que todos os campos desejados sejam extraídos
#         for campo in ['titulo', 'idioma', 'periodico', 'ano', 'volume', 'issn', 'estrato_qualis', 'pais_de_publicacao', 'paginas', 'doi']:
#             linha[campo] = registro.get(campo, '')

#         # Tratar os autores como uma string concatenada se eles existirem
#         linha['autores'] = '; '.join(registro.get('autores', []))

#         # Tratar os campos 'autores-endogeno' e 'autores-endogeno-nome'
#         if 'autores-endogeno' in registro and registro['autores-endogeno']:
#             id_endogeno = registro['autores-endogeno'][0]
#             linha['idLattes'] = id_endogeno
#             linha['nome'] = registro['autores-endogeno-nome'][0].get(id_endogeno, None)
        
#         # Adicionar os outros campos conforme necessário aqui
#         # Por exemplo, tratamento de 'tags', 'Hash', etc., quando necessário

#         return linha

#     def processar_publicacoes(self):
#         linhas = []
#         # Itera diretamente sobre cada registro em self.data
#         for registro in self.data:
#             linha = self.extrair_dados(registro, registro.get('tipo_producao', 'Desconhecido'))
#             linhas.append(linha)
#         return linhas

#     def extract_zips(self, pathzip):
#         destination = os.path.join(os.getcwd(), '_data', 'in_json')
#         if not os.path.exists(destination):
#             os.makedirs(destination)
#             print(f"Criada pasta para armazenar dados descompactados: {destination}")
#         else:
#             print(f"Descompactando arquivos para: {destination}")

#         with zipfile.ZipFile(pathzip, 'r') as zip_ref:
#             zip_ref.extractall(destination)
        
#         print("Descompactação concluída...")
#         return destination  # Retorna o caminho onde os arquivos foram descompactados

#     def find_and_merge_publication_json_files(self, pathjson):
#         all_data = []
#         for filename in os.listdir(pathjson):
#             if 'publication.json' in filename:
#                 print(f"Extraindo dados do arquivo '{filename}'...")
#                 with open(os.path.join(pathjson, filename), 'r', encoding='utf-8') as file:
#                     file_data = json.load(file)
#                     for tipo_producao in file_data:  # Para cada tipo de produção no arquivo
#                         for ano in file_data[tipo_producao]:  # Para cada ano dentro de um tipo de produção
#                             for registro in file_data[tipo_producao][ano]:  # Itera sobre cada registro
#                                 # Adicionar ou atualizar o campo 'tipo_producao' em cada registro
#                                 registro_atualizado = registro.copy()  # Fazer cópia para evitar modificar o original
#                                 registro_atualizado['tipo_producao'] = tipo_producao  # Atualizar ou adicionar o campo 'tipo_producao'
#                                 all_data.append(registro_atualizado)  # Adicionar o registro atualizado à lista

#         # Salva a lista unificada em um novo arquivo JSON
#         unified_json_path = os.path.join(pathjson, 'unified_pub.json')
#         with open(unified_json_path, 'w', encoding='utf-8') as unified_file:
#             json.dump(all_data, unified_file, ensure_ascii=False, indent=4)
        
#         print(f"Arquivo unificado criado em: {unified_json_path}")

#         # Atualiza self.data com os dados unidos
#         self.data = all_data

#     def merge_publication_json_files(self, pathjson):
#         """
#         This function receives a path to a JSON folder, accesses the folder's contents, searches for files
#         containing 'publication.json' in their filename, merges their contents and saves the resulting
#         data as a CSV file in destination folder.
#         """
#         data = []
#         # Looping through the files in the given path
#         for filename in os.listdir(pathjson):
#             if 'publication.json' in filename:
#                 print(f"Extraindo dados do arquivo {filename}...")
#                 # Opening the file and appending its data to the list
#                 with open(os.path.join(pathjson, filename), 'r', encoding='utf-8') as file:
#                     data.append(json.load(file))

#         # Creating the output directory if it doesn't exist
#         destination = os.path.join(os.getcwd(), '_data','powerbi')
#         if not os.path.exists(destination):
#             os.mkdir(destination)

#         # Writing the merged data to a CSV file
#         print(f"Criando arquivo CSV...")
#         with open(os.path.join(destination, 'publication.csv'), 'w', encoding='utf-8', newline='') as csv_file:
#             writer = csv.writer(csv_file)
#             # Writing the header based on the keys of the first item in the list
#             writer.writerow(data[0].keys())
#             # Looping through the items in the list and writing them as rows in the CSV file
#             for item in data:
#                 writer.writerow(item.values())

#     def exportar_para_csv(self, nome_arquivo='publicacoes.csv'):
#         linhas = self.processar_publicacoes()
#         df = pd.DataFrame(linhas, columns=self.colunas)
#         filepathcsv = os.path.join("./","_data","powerbi",nome_arquivo)
#         df.to_csv(filepathcsv, index=False)
#         print(f'Arquivo criado com sucesso em {filepathcsv}')

#     def ler_csv_dados(self, pathdata,filename):
#         filepath = os.path.join(pathdata,filename)
#         df_pub=pd.read_csv(filepath)
#         tipos = df_pub['tipo_producao'].value_counts()
#         qualis=df_pub['estrato_qualis'].value_counts()  
#         quantidade_nan = df_pub['estrato_qualis'].isna().sum()
#         tipos_qualis = qualis.count()
#         percentual_nan=np.round(quantidade_nan/tipos.sum()*100,1)
#         print(f"\n{tipos.sum()} linhas no total, distribuídas nos seguintes tipos de produção:")
#         print(f"{quantidade_nan} linhas ({percentual_nan}% do total de linhas) com NaN no campo estrato_qualis")
#         print(tipos)
#         ano_min=df_pub['ano'].min()
#         ano_max=df_pub['ano'].max()
#         print(f"\n{tipos.get('PERIODICO', 0)} publicações em periódicos, no período de {int(ano_min)} a {int(ano_max)}")
#         percentual=np.round(qualis.sum()/tipos.get('PERIODICO', 0)*100,1)
#         print(f"{qualis.sum()} publicações ({percentual}%) classificadas no qualis periodicos conforme estratificação:")
#         quantidade_nan_periodico = df_pub[df_pub['tipo_producao'] == 'PERIODICO']['estrato_qualis'].isna().sum()
#         percentual_nan_periodico = np.round(quantidade_nan_periodico/tipos.get('PERIODICO', 0)*100,1)
#         print(f"{quantidade_nan_periodico} publicações em periódicos ({percentual_nan_periodico}%) com valor 'NaN' no estrato_qualis\n")
#         print(qualis)
#         return df_pub

#     def ler_xls_dados(self, pathdata,filename):
#         filepath = os.path.join(pathdata,filename)
#         df_pub=pd.read_excel(filepath)
#         tipos = df_pub['tipo_producao'].value_counts()
#         qualis=df_pub['estrato_qualis'].value_counts()
#         tipos_qualis = qualis.count()
#         print(f"\n{tipos.sum()} linhas no total, distribuídas nos seguintes tipos de produção:")
#         print(tipos)
#         ano_min=df_pub['ano'].min()
#         ano_max=df_pub['ano'].max()
#         print(f"\n{tipos.get('PERIODICO', 0)} publicações em periódicos, no período de {int(ano_min)} a {int(ano_max)}")
#         percentual=np.round(qualis.sum()/tipos.get('PERIODICO', 0)*100,1)
#         print(f"{qualis.sum()} publicações ({percentual}%) classificadas no qualis periodicos conforme estratificação:")
#         print(qualis)
#         return df_pub

#     def sigla_producao(self, tipo_producao, separador=""):
#         """
#         Função para converter os valores da coluna 'tipo_producao' em siglas, desconsiderando preposições,
#         fazendo split de 'tipo_producao' em palavras também pelo caractere "_".
        
#         Parâmetros:
#         - tipo_producao: O valor da coluna 'tipo_producao'.
#         - separador: O caractere para separar as iniciais. Padrão é "_".
        
#         Retorna:
#         - Uma string que é a sigla formada pelas iniciais das palavras em 'tipo_producao', desconsiderando preposições.
#         """
#         # Lista de preposições para serem ignoradas
#         preposicoes = ['e', 'de', 'do', 'da', 'dos', 'das', 'em', 'na', 'no', 'nas', 'nos', 'por', 'para', 'com']

#         # Mapeamento de exemplo conforme as siglas fornecidas
#         mapeamento_siglas = {
#             "DTPB": 1, #DEMAIS_TIPOS_DE_PRODUCAO_BIBLIOGRAFICA 
#             "TJ": 2, #TEXTO_EM_JORNAIS
#             "E": 3, #EVENTO
#             "CL": 4, #CAPITULO_DE_LIVRO
#             "L": 5, #LIVRO
#             "AA": 6, #ARTIGO_ACEITO
#             "P": 7, #PERIODICO
#         }

#         # Fazendo split por espaço e por underscore
#         palavras = tipo_producao.replace('_', ' ').replace('-', ' ').split()

#         # Inicializar a lista de iniciais
#         iniciais = []

#         for palavra in palavras:
#             # Verificar se a palavra não é uma preposição e não está vazia
#             if palavra.lower() not in preposicoes and palavra:
#                 # Adicionar a inicial em maiúsculo à lista de iniciais
#                 iniciais.append(palavra[0].upper())

#         # Juntar as iniciais para formar a sigla
#         sigla = "".join(iniciais)

#         # Aplicar o mapeamento para encontrar o número correspondente à sigla
#         numero = mapeamento_siglas.get(sigla, "")

#         # Retornar a string formatada com o número e a sigla
#         return f"{numero}-{sigla}"  

#     def sigla_qualis(self, estrato_qualis, separador=""):
#         """
#         Função para converter os valores da coluna 'estrato_qualis' em siglas com números de ordenação,
        
#         Parâmetros:
#         - estrato_qualis: O valor da coluna 'estrato_qualis'.
#         - separador: O caractere para separar as iniciais. Padrão é "_".
        
#         Retorna:
#         - Uma string que é a sigla formada pelas iniciais das palavras em 'estrato_qualis' antecedida por seu número de ordenação.
#         """

#         # Mapeamento de exemplo conforme as siglas fornecidas
#         mapeamento_siglas = {
#             "C": 1,
#             "B4": 2,
#             "B3": 3,
#             "B2": 4,
#             "B1": 5,
#             "B2": 6,
#             "B1": 7,
#             "A4": 8,
#             "A3": 9,
#             "A2": 10,
#             "A1": 11,
#         }

#         # Aplicar o mapeamento para encontrar o número correspondente à sigla
#         numero = mapeamento_siglas.get(estrato_qualis, "")

#         # Retornar a string formatada com o número e a sigla
#         return f"{numero}-{estrato_qualis}"

#     def agrupar_publicacoes(self, filename):
#         # Caminho para o arquivo CSV
#         pathfilename = os.path.join(os.getcwd(), '_data', 'powerbi', filename)
#         df = pd.read_csv(pathfilename)

#         # Use .loc para modificar o DataFrame diretamente e evitar o aviso
#         df.loc[:, 'sigla_producao'] = df['tipo_producao'].apply(lambda x: self.sigla_producao(x))
#         df_publicacoes = df[['idLattes','ano','sigla_producao']]

#         # Agrupar por 'ano', 'natureza' e orientador e contar as ocorrências
#         contagem_publicacoes = df_publicacoes.groupby(['ano','sigla_producao','idLattes']).size().reset_index(name='contagem')

#         # Retornar a contagem de orientações por tipo e por ano
#         return contagem_publicacoes

#     def agrupar_qualis(self, filename):
#         # Caminho para o arquivo CSV
#         pathfilename = os.path.join(os.getcwd(), '_data', 'powerbi', filename)
#         df = pd.read_csv(pathfilename)

#         # # Use .loc para modificar o DataFrame diretamente e evitar o aviso
#         df.loc[:, 'estrato_qualis'] = df['estrato_qualis'].apply(lambda x: self.sigla_qualis(x))
#         df_publicacoes = df[['idLattes','ano','estrato_qualis']]

#         # Remover todas as linhas que contêm pelo menos um valor NaN
#         df_publicacoes_limpo = df_publicacoes.dropna()

#         # Agrupar por 'ano', 'natureza' e orientador e contar as ocorrências
#         contagem_qualis = df_publicacoes_limpo.groupby(['ano','estrato_qualis','idLattes']).size().reset_index(name='contagem')

#         # Retornar a contagem de orientações por tipo e por ano
#         return contagem_qualis

#     def plotar_producoes_barras_empilhadas(self, filename):
#         contagem_publicacoes = self.agrupar_publicacoes(filename)
#         fig = make_subplots(rows=1, cols=1)
#         anos = sorted(contagem_publicacoes['ano'].unique())

#         mapeamento_siglas_para_numeros = {
#             "1-DTPB": 1, # Demais tipos de produção bibliográfica
#             "2-TJ": 2, # Texto em jornais
#             "3-E": 3, # Evento
#             "4-CL": 4, # Capítulo de Livro
#             "5-L": 5, # Livro
#             "6-AA": 6, # Artigo Aceito
#             "7-P": 7, # Periódico
#         }

#         naturezas_ordenadas = sorted(contagem_publicacoes['sigla_producao'].unique(), key=lambda x: mapeamento_siglas_para_numeros.get(x, 999))

#         for natureza in naturezas_ordenadas:
#             contagem_por_ano = []
#             labels_por_ano = [] # Para armazenar os rótulos de dados
#             for ano in anos:
#                 contagem = contagem_publicacoes[(contagem_publicacoes['ano'] == ano) & (contagem_publicacoes['sigla_producao'] == natureza)]['contagem'].sum()
#                 if mapeamento_siglas_para_numeros.get(natureza, 999) in [1, 2, 3, 4]:
#                     contagem = -contagem
#                 contagem_por_ano.append(contagem)
#                 labels_por_ano.append(str(contagem)) # Convertendo a contagem em string para usar como rótulo
            
#             # Adicionar a barra ao gráfico com rótulos de dados
#             fig.add_trace(go.Bar(x=anos, y=contagem_por_ano, name=natureza, text=labels_por_ano, textposition='auto'))

#         # Atualizar o layout para permitir barras empilhadas, ajustar o eixo Y para mostrar valores negativos, e garantir que todos os anos sejam mostrados no eixo X
#         fig.update_layout(
#             barmode='relative',
#             title_text='Contagem de Produções por Tipo e Ano (Produção de divulgação plotadas abaixo do eixo X)',
#             xaxis_title="Ano",
#             yaxis_title="Quantidade de Produções Biliográficas",
#             yaxis=dict(zeroline=True, zerolinewidth=2, zerolinecolor='black'),
#         )        
#         # Garantir que todos os anos apareçam na barra de rótulos do eixo X
#         fig.update_xaxes(tickmode='array', tickvals=anos)
#         fig.show()


#     def plotar_qualis_barras_empilhadas(self, filename):
#         contagem_publicacoes = self.agrupar_qualis(filename)
#         contagem_publicacoes.replace("-nan", np.nan, inplace=True)
#         contagem_publicacoes.dropna(inplace=True)
#         fig = make_subplots(rows=1, cols=1)
#         anos = sorted(contagem_publicacoes['ano'].unique())

#         mapeamento_siglas_para_numeros = {
#             "1-C": 1, "2-B4": 2, "3-B3": 3, "4-B2": 4, "5-B1": 5,
#             "6-B2": 6, "7-B1": 7, "8-A4": 8, "9-A3": 9, "10-A2": 10, "11-A1": 11,
#         }
#         naturezas_ordenadas = sorted(contagem_publicacoes['estrato_qualis'].unique(), key=lambda x: mapeamento_siglas_para_numeros.get(x, 999))
        
#         # Obter a paleta de cores 'Greens'
#         cores = px.colors.sequential.Greens
#         # Certificar que temos cores suficientes para todas as barras, repetindo a paleta se necessário
#         num_barras = len(naturezas_ordenadas)
#         cores_repetidas = cores * (num_barras // len(cores) + 1)
        
#         for index, natureza in enumerate(naturezas_ordenadas):
#             contagem_por_ano = []
#             for ano in anos:
#                 contagem = contagem_publicacoes[(contagem_publicacoes['ano'] == ano) & (contagem_publicacoes['estrato_qualis'] == natureza)]['contagem'].sum()
#                 if mapeamento_siglas_para_numeros.get(natureza, 999) in [1, 2, 3, 4, 5, 6, 7]:
#                     contagem = -contagem
#                 contagem_por_ano.append(contagem)
            
#             # Usar uma cor da paleta para cada barra
#             fig.add_trace(go.Bar(x=anos, y=contagem_por_ano, name=natureza, marker_color=cores_repetidas[index]))

#         fig.update_layout(
#             barmode='relative',
#             title_text='Contagem de Produções por Estrato Qualis e Ano (Qualis abaixo de B plotado do eixo X)',
#             xaxis_title="Ano",
#             yaxis_title="Quantidade de Publicações",
#             yaxis=dict(zeroline=True, zerolinewidth=2, zerolinecolor='black'),
#         )
#         # Garantir que todos os anos apareçam na barra de rótulos do eixo X
#         fig.update_xaxes(tickmode='array', tickvals=anos)        
#         fig.show()

# class PreparadorDeOrientacoes():
#     def __init__(self):
#         self.data = []
#         self.colunas = ['id_lattes_orientadores', 'tipo_orientacao', 'natureza', 'titulo', 'idioma', 'ano', 'id_lattes_aluno', 'nome_aluno', 'instituicao', 'pais', 'curso', 'codigo_do_curso', 'bolsa', 'agencia_financiadora', 'codigo_agencia_financiadora', 'nome_orientadores', 'tags', 'Hash']
#         self.pathjson = os.path.join('_data','in_json')
#         # self.filename = '863.advise.json'

#         # Abrir o arquivo e carregando o JSON
#     def open_file(self, filename):
#         with open(os.path.join(self.pathjson, filename), 'r', encoding='utf-8') as file:
#             data = json.load(file)
        
#         linhas_achatadas = self.extrair_orientacoes(data)
#         df = pd.DataFrame(linhas_achatadas)
#         df.to_csv('orientacoes_achatadas.csv', index=False)
#         return df
    
#     def agrupar_orientacoes(self, filename):
#         # Caminho para o arquivo JSON
#         pathfilename = os.path.join('_data', 'in_json', filename)
#         # dict_orientacoes = pd.read_json(pathfilename)

#         # Carregar o JSON e aplicar a função
#         with open(pathfilename, 'r', encoding='utf-8') as file:
#             data = json.load(file)

#         linhas_achatadas = self.extrair_orientacoes(data)
#         df = pd.DataFrame(linhas_achatadas)

#         # Salvar os dados achatados em um CSV
#         df.to_csv('orientacoes_achatadas.csv', index=False)

#         # Use .loc para modificar o DataFrame diretamente e evitar o aviso
#         df.loc[:, 'sigla_natureza'] = df['natureza'].apply(lambda x: self.sigla_natureza(x))
#         df_orientacoes = df[['id_lattes_orientadores','ano','sigla_natureza']]

#         # Agrupar por 'ano', 'natureza' e orientador e contar as ocorrências
#         contagem_orientacoes = df_orientacoes.groupby(['ano','sigla_natureza','id_lattes_orientadores']).size().reset_index(name='contagem')

#         # Retornar a contagem de orientações por tipo e por ano
#         return contagem_orientacoes

#     # Prosseguir com a definição e uso da função para extrair as orientações
#     def extrair_orientacoes(self, json_data):
#         colunas = self.colunas
#         linhas = []

#         # Iterar sobre cada tipo de orientação e ano
#         for tipo_orientacao, anos in json_data.items():
#             for ano, orientacoes in anos.items():
#                 for orientacao in orientacoes:
#                     # Preparar um dicionário para cada linha de acordo com as colunas definidas
#                     linha = {}
#                     # Adicionar dados específicos da orientação
#                     for campo in orientacao:
#                         if campo in colunas:
#                             linha[campo] = orientacao[campo]
#                     # Tratar 'id_lattes_orientadores' como uma lista, juntar os IDs com vírgula se houver mais de um
#                     linha['id_lattes_orientadores'] = ', '.join(orientacao.get('id_lattes_orientadores', []))
#                     # Adicionar o tipo de orientação como uma coluna
#                     linha['tipo_orientacao'] = tipo_orientacao
#                     # Adicionar o ano, garantindo que sobreponha qualquer valor de 'ano' nos dados individuais
#                     linha['ano'] = ano
#                     linhas.append(linha)

#         return linhas

#     def sigla_natureza(self, natureza, separador=""):
#         """
#         Função para converter os valores da coluna 'natureza' em siglas, desconsiderando preposições,
#         fazendo split de 'natureza' em palavras também pelo caractere "_".
        
#         Parâmetros:
#         - natureza: O valor da coluna 'natureza'.
#         - separador: O caractere para separar as iniciais. Padrão é "_".
        
#         Retorna:
#         - Uma string que é a sigla formada pelas iniciais das palavras em 'natureza', desconsiderando preposições.
#         """
#         # Lista de preposições para serem ignoradas
#         preposicoes = ['e', 'de', 'do', 'da', 'dos', 'das', 'em', 'na', 'no', 'nas', 'nos', 'por', 'para', 'com']

#         # Mapeamento de exemplo conforme as siglas fornecidas
#         mapeamento_siglas = {
#             "OON": 1, #Orientações de Outra Natureza
#             "IC": 2, #Iniciação Científica
#             "MCCAE": 3, #Monografia de Conclusão Curso de Atualização ou Especialização
#             "SPD": 4, #
#             "TCCG": 5, #Trabalho de Conclusão de Curso de Graduação
#             "DM": 6, #Dissertação de Mestrado
#             "TD": 7, #Tese de Doutorado
#         }

#         # Fazendo split por espaço e por underscore
#         palavras = natureza.replace('_', ' ').replace('-', ' ').split()

#         # Inicializar a lista de iniciais
#         iniciais = []

#         for palavra in palavras:
#             # Verificar se a palavra não é uma preposição e não está vazia
#             if palavra.lower() not in preposicoes and palavra:
#                 # Adicionar a inicial em maiúsculo à lista de iniciais
#                 iniciais.append(palavra[0].upper())

#         # Juntar as iniciais para formar a sigla
#         sigla = "".join(iniciais)

#         # Aplicar o mapeamento para encontrar o número correspondente à sigla
#         numero = mapeamento_siglas.get(sigla, "Desconhecido")

#         # Retornar a string formatada com o número e a sigla
#         return f"{numero}-{sigla}"     

#     def plotar_orientacoes_barras_agrupadas(self, filename):
#         # montar dataframe com agrupamento de orientações por tipo por ano no programa
#         contagem_orientacoes = self.agrupar_orientacoes(filename)

#         # Criar uma figura com subplots
#         fig = make_subplots(rows=1, cols=1)

#         # Encontrar anos e naturezas únicos para as orientações
#         anos = sorted(contagem_orientacoes['ano'].unique())

#         # Mapeamento de exemplo conforme as siglas fornecidas
#         mapeamento_siglas = {
#             "OON": 1,
#             "IC": 2,
#             "MCCAE": 3,
#             "SPD": 4,
#             "TCCG": 5,
#             "DM": 6,
#             "TD": 7,
#         }

#         # Ordenar as naturezas com base nos números associados em mapeamento_siglas
#         mapeamento_siglas_para_numeros = {sigla: int(sigla.split('-')[0]) for sigla in contagem_orientacoes['sigla_natureza'].unique()}
#         naturezas_ordenadas = sorted(contagem_orientacoes['sigla_natureza'].unique(), key=lambda x: mapeamento_siglas_para_numeros.get(x, 999))

#         # Criar uma barra para cada tipo de orientação em cada ano
#         for natureza in naturezas_ordenadas:
#             contagem_por_ano = []
#             for ano in anos:
#                 # Somar as contagens para cada ano e natureza
#                 contagem = contagem_orientacoes[(contagem_orientacoes['ano'] == ano) & (contagem_orientacoes['sigla_natureza'] == natureza)]['contagem'].sum()
#                 contagem_por_ano.append(contagem)
            
#             # Adicionar a barra ao gráfico
#             fig.add_trace(go.Bar(x=anos, y=contagem_por_ano, name=natureza))

#         # Atualizar o layout para permitir barras agrupadas
#         fig.update_layout(barmode='group', title_text='Contagem de Orientações no Programa por Tipo e Ano', xaxis_title="Ano", yaxis_title="Quantidade de Orientações")

#         # Mostrar o gráfico
#         fig.show()


#     def plotar_orientacoes_barras_empilhadas(self, filename):
#         # montar dataframe com agrupamento de orientações por tipo por ano no programa
#         contagem_orientacoes = self.agrupar_orientacoes(filename)
        
#         # Criar uma figura com subplots
#         fig = make_subplots(rows=1, cols=1)

#         # Encontrar anos únicos para as orientações
#         anos = sorted(contagem_orientacoes['ano'].unique())

#         # Mapeamento para siglas de tipos de orientações
#         mapeamento_siglas = {
#             "OON": 1,
#             "IC": 2,
#             "MCCAE": 3,
#             "SPD": 4,
#             "TCCG": 5,
#             "DM": 6,
#             "TD": 7,
#         }

#         # Mapeamento para ordenar siglas por duração/complexidade
#         mapeamento_siglas_para_numeros = {
#             "1-OON": 1,
#             "2-IC": 2,
#             "3-MCCAE": 3,
#             "4-SPD": 4,
#             "5-TCCG": 5,
#             "6-DM": 6,
#             "7-TD": 7,
#         }

#         # Ordenar as naturezas baseando-se no número extraído da sigla
#         naturezas_ordenadas = sorted(contagem_orientacoes['sigla_natureza'].unique(), key=lambda x: mapeamento_siglas_para_numeros.get(x, 999))

#         # Criar uma barra para cada tipo de orientação em cada ano, seguindo a ordem definida
#         for natureza in naturezas_ordenadas:
#             contagem_por_ano = []
#             for ano in anos:
#                 # Somar as contagens para cada ano e natureza
#                 contagem = contagem_orientacoes[(contagem_orientacoes['ano'] == ano) & (contagem_orientacoes['sigla_natureza'] == natureza)]['contagem'].sum()
#                 # Se a sigla estiver associada ao número 1 ou 2, tornar a contagem negativa
#                 if mapeamento_siglas_para_numeros.get(natureza, 999) in [1, 2, 3, 4]:
#                     contagem = -contagem
#                 contagem_por_ano.append(contagem)
            
#             # Adicionar a barra ao gráfico
#             fig.add_trace(go.Bar(x=anos, y=contagem_por_ano, name=natureza))

#         # Atualizar o layout para permitir barras empilhadas e ajustar o eixo Y para mostrar valores negativos
#         fig.update_layout(
#             barmode='relative',  # Usar 'relative' para empilhar incluindo valores negativos
#             title_text='Contagem de Orientações por Tipo e Ano (Orientações de curta duração plotadas abaixo do eixo X)',
#             xaxis_title="Ano",
#             yaxis_title="Quantidade de Orientações",
#             yaxis=dict(zeroline=True, zerolinewidth=2, zerolinecolor='black'),  # Destacar a linha zero
#         )

#         # Mostrar o gráfico
#         fig.show()


In [ ]:
# path = "./"
# print(f"     Pasta corrente: {path}")
# pathjson = os.path.join(path,'_data','in_json')
# print(f"Pasta arquivos JSON: {pathjson}")
# try:
#     pathdata = os.path.join(path,'_data','powerbi')
#     print(f" Pasta de dados CSV: {pathdata}")
# except:
#     print('Pasta de dados ainda não existe.')

# print("\nConteúdo da pasta JSON:")
# list(os.listdir(pathjson))

In [ ]:
# ## Descompactar arquivo zipado na pasta JSON
# prep_pub = PreparadorDePublicacoes()
# pathfilezip = '_data/in_zip/890.files.zip'
# destination = prep_pub.extract_zips(pathfilezip)

# ## Unir todos aquivos de publicações (caso haja mais de um com final publication.json na pasta serão mesclados):
# prep_pub.find_and_merge_publication_json_files(pathjson)

# ## Mapear arquivo de dados para PowerBI a partir do JSON unificado
# linhas = prep_pub.processar_publicacoes()
# prep_pub.exportar_para_csv()

# ## Ler e montar análise exploratória
# filename='publicacoes.csv'
# df_pub = prep_pub.ler_csv_dados(pathdata,filename)

In [ ]:
# filename='890.advise.json'
# pathjson = os.path.join('_data','in_json')
# pathfilename = os.path.join(pathjson,filename)
# print(pathfilename)
# dict_orientacoes = pd.read_json(pathfilename)
# print(f'{len(dict_orientacoes):02} dicionários com dados de orientações')

In [ ]:
# dict_orientacoes.keys()

In [ ]:
# prep_ort = PreparadorDeOrientacoes()
# prep_ort.plotar_orientacoes_barras_agrupadas(filename)
# prep_ort.plotar_orientacoes_barras_empilhadas(filename)

In [ ]:
# pathcsv = os.path.join('_data','powerbi')
# os.listdir(pathcsv)

## Demais passos

Calcular índice de publicação em conjunto com alunos do programa

- Levantar nome dos discentes do programa
- Levantar os nomes de autores nas publicações de docentes
- Identificar por similadidade as publicações onde constam nome de alunos do programa

    Padronizar nomes de autores

In [ ]:
# def limpar_nomes(linha_texto):
#     '''
#     Retira erros e sujeira da string formada pela lista de nomes de autor dos artigos retirada do Lattes
#      Recebe: Uma string com os nomes de autor
#     Retorna: Uma string com os nomes de autor, removidas preposições, acentos, e demais erros pontuais
#     '''
#     import unicodedata
#     import re
#     # print('               Analisando:',linha_texto)
#     string = linha_texto.replace('Network for Genomic Surveillance in South Africa;Network for Genomic Surveillance in South Africa (NGS-SA);10.1002/jmv.27190;','')
#     string = string.replace('Autores: ','').replace('(Org)','').replace('(Org.)','').replace('et. al.','').replace('et al','').replace('(Org).','').replace('.','').replace('\'','')
#     string = string.replace(',,,',',').replace(',,',',').replace(';',', ').replace('-',' ').replace('S?', 'SA').replace('S?', 'SA').replace('ARA?JO', 'ARAUJO').replace('FL?VIO','FLAVIO').replace('F?BIO','FABIO').replace('VIT?RIO','VITORIO')
#     string = re.sub(r'[0-9]+', '', string)
#     partes_string = string.split(' ')

#     ## Retirar partes de nomes caso sejam preposições
#     preposicoes = ['da', 'de', 'do', 'das', 'dos', ' e ']
#     string = ' '.join(x for x in partes_string if x.lower() not in preposicoes)

#     ## Retirar símbolos não unicode, como acentuação gráfica e cedilha
#     string = ''.join(ch for ch in unicodedata.normalize('NFKD', string) if not unicodedata.combining(ch))
    
#     ## Retirar iniciais juntas, separando-as com espaço em branco
#     letras_duasconsnts = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{2}$')            # Duas Letras consoantes maiúsculas juntas do início ao final da string
#     letras_tresconsnts = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{3}$')            # Três Letras consoantes maiúsculas juntas do início ao final da string
#     letras_duasconsntsvirg = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{2},$')       # Duas Letras consoantes maiúsculas juntas do início ao final da string, seguidas de vírgula
#     letras_tresconsntsvirg = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{3},$')       # Três Letras consoantes maiúsculas juntas do início ao final da string, seguidas de vírgula
    
#     partes_nome=[]
#     for j in string.split(' '):
#         div_ltrduasconsnts = letras_duasconsnts.findall(j)
#         div_ltrtriplicadas = letras_tresconsnts.findall(j)
#         div_ltrduasconsntsvirg = letras_duasconsntsvirg.findall(j)
#         div_ltrtresconsntsvirg = letras_tresconsntsvirg.findall(j)
#         if div_ltrduasconsnts or div_ltrtriplicadas:
#             iniciais_separadas = ' '.join(x for x in j)
#             partes_nome.append(iniciais_separadas)
#         elif div_ltrduasconsntsvirg or div_ltrtresconsntsvirg:
#             iniciais_separadas = ' '.join(x for x in j[:-1])
#             partes_nome.append(iniciais_separadas+',')
#         else:
#             partes_nome.append(j)
#     string = ' '.join(x for x in partes_nome).strip()
#     return string



# def padronizar_nome(linha_texto):
#     '''
#     Procura sobrenomes e abreviaturas e monta nome completo
#      Recebe: String com todos os sobrenomes e nomes, abreviados ou não
#     Retorna: Nome completo no formato padronizado em SOBRENOME AGNOME, Partes de nomes
#       Autor: Marcos Aires (Mar.2022)
#     '''
#     import unicodedata
#     import re
#     # print('               Analisando:',linha_texto)
#     partes_string = linha_texto.split(' ')

#     ## Retirar partes de nomes caso sejam preposições
#     preposicoes = ['da', 'de', 'do', 'das', 'dos', ' e ']
#     string = ' '.join(x for x in partes_string if x.lower() not in preposicoes)

#     ## Retirar símbolos não unicode, como acentuação gráfica e cedilha
#     string = ''.join(ch for ch in unicodedata.normalize('NFKD', string) if not unicodedata.combining(ch))
    
#     ## Expressões regulares para encontrar padrões de divisão de nomes de autores
#     sobrenome_inicio   = re.compile(r'^[A-ZÀ-ú-a-z]+,')                  # Sequência de letras maiúsculas no início da string
#     sobrenome_composto = re.compile(r'^[A-ZÀ-ú-a-z]+[ ][A-ZÀ-ú-a-z]+,')  # Duas sequências de letras no início da string, separadas por espaço, seguidas por vírgula
#     letra_abrevponto   = re.compile(r'^[A-Z][.]')                        # Uma letra maiúscula no início da string, seguida por ponto
#     letra_abrevespaco  = re.compile(r'^[A-Z][ ]')                        # Uma letra maiúscula no início da string, seguida por espaço
#     letras_dobradas    = re.compile(r'[A-Z]{2}')                         # Duas letras maiúsculas juntas
#     letras_dobradasini = re.compile(r'[A-Z]{2}[ ]')                      # Duas letras maiúsculas juntas, seguidas por espaço
#     letras_dobradasfim = re.compile(r'[ ][A-Z]{2}')                      # Duas letras maiúsculas juntas, precedidas por espaço

#     ## Expressões regulares para encontrar iniciais juntas, separando-as com espaço em branco
#     letras_duasconsnts = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{2}$')            # Duas Letras consoantes maiúsculas juntas do início ao final da string
#     letras_tresconsnts = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{3}$')            # Três Letras consoantes maiúsculas juntas do início ao final da string
#     letras_duasconsntsvirg = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{2},$')       # Duas Letras consoantes maiúsculas juntas do início ao final da string, seguidas de vírgula
#     letras_tresconsntsvirg = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{3},$')       # Três Letras consoantes maiúsculas juntas do início ao final da string, seguidas de vírgula

#     ## Agnomes e preprosições a tratar, agnomes vão em maiúsculas para sobrenome e preposições vão em minúsculas para restante das partes de nomes
#     nomes=[]
#     agnomes       = ['NETO','JUNIOR','FILHO','SEGUNDO','TERCEIRO','SOBRINHO']
#     preposicoes   = ['de','da','do','das','dos', ' e ']
#     nome_completo = ''
    
#     ## Ajustar lista de termos, identificar sobrenomes compostos e ajustar sobrenome com ou sem presença de vírgula
#     div_sobrenome   = sobrenome_inicio.findall(string)
#     div_sbrcomposto = sobrenome_composto.findall(string)
    
#     # print('-'*100)
#     # print('                 Recebido:',string)
    
#     ## Caso haja vírgulas na string, tratar sobrenomes e sobrenomes compostos
#     if div_sobrenome != [] or div_sbrcomposto != []:
#         # print('CASO_01: Há víruglas na string')
#         div = string.split(', ')
#         sobrenome     = div[0].strip().upper()
#         try:
#             div_espaco    = div[1].split(' ')
#         except:
#             div_espaco    = ['']
#         primeiro      = div_espaco[0].strip('.').strip()
        
#         # print('     Dividir por vírgulas:',div)
#         # print('      Primeira DivVirgula:',sobrenome)
#         # print('Segunda DivVrg/DivEspaços:',div_espaco)
#         # print('      Primeira DivEspaços:',primeiro)
               
#         # Caso primeiro nome seja somente duas letras maiúsculas juntas, trata-se de duas iniciais
#         if len(primeiro)==2 or letras_tresconsnts.findall(primeiro) or letras_duasconsnts.findall(primeiro):
#             # print('CASO_01.a: Há duas letras ou três letras consoantes juntas, são iniciais')
#             primeiro_nome=primeiro[0].strip()
#             # print('          C01.a1_PrimNome:',primeiro_nome)
#             nomes.append(primeiro[1].strip().upper())
#             try:
#                 nomes.append(primeiro[2].strip().upper())
#             except:
#                 pass
#             try:
#                 nomes.append(primeiro[3].strip().upper())
#             except:
#                 pass            
#         else:
#             # print('CASO_01.b: Primeiro nome maior que 2 caracteres')
#             primeiro_nome = div_espaco[0].strip().title()
#             # print('          C01.a2_PrimNome:',primeiro_nome)
        
#         ## Montagem da lista de partes de nomes do meio
#         for nome in div_espaco:
#             # print('CASO_01.c: Para cada parte de nome da divisão por espaços após divisão por vírgula')
#             if nome not in nomes and nome.lower()!=primeiro_nome.lower() and nome.lower() not in primeiro_nome.lower() and nome!=sobrenome:   
#                 # print('CASO_01.c1: Se o nome não está nem como primeiro nome, nem sobrenomes')
#                 # print(nome, len(nome))
                
#                 ## Avaliar se é abreviatura seguida de ponto e remover o ponto
#                 if len(nome)<=2 and nome.lower() not in preposicoes:
#                     # print('    C01.c1.1_Nome<=02:',nome)
#                     for inicial in nome:
#                         # print(inicial)
#                         if inicial not in nomes and inicial not in primeiro_nome:
#                             nomes.append(inicial.replace('.','').strip().title())
#                 elif len(nome)==3 and nome.lower() not in preposicoes:
#                         # print('    C01.c1.2_Nome==03:',nome)
#                         for inicial in nome:
#                             if inicial not in nomes and inicial not in primeiro_nome:
#                                 nomes.append(inicial.replace('.','').strip().title())
#                 else:
#                     if nome not in nomes and nome!=primeiro_nome and nome!=sobrenome and nome!='':
#                         if nome.lower() in preposicoes:
#                             nomes.append(nome.replace('.','').strip().lower())
#                         else:
#                             nomes.append(nome.replace('.','').strip().title())
#                         # print(nome,'|',primeiro_nome)
                        
#         ## Caso haja sobrenome composto que não esteja nos agnomes considerar somente primeira parte como sobrenome
#         if div_sbrcomposto !=[] and sobrenome.split(' ')[1] not in agnomes and sobrenome.split(' ')[0].lower() not in preposicoes:
#             # print('CASO_01.d: Sobrenome composto sem agnomes')
#             # print(div_sbrcomposto)
#             # print('Sobrenome composto:',sobrenome)
            
#             nomes.append(sobrenome.split(' ')[1].title())
#             sobrenome = sobrenome.split(' ')[0].upper().strip()
#             # print('Sobrenome:',sobrenome)
            
#             for i in nomes:
#                 if i.lower() in sobrenome.lower():
#                     nomes.remove(i)
#             # print('    Nomes:',nomes)
        
#         ## Caso haja preposição como agnome desconsiderar e passar para final dos nomes
#         if div_sbrcomposto !=[] and sobrenome.split(' ')[0].lower() in preposicoes:
#             # print('CASO_01.e: Preposição no Sobrenome passar para o final dos nomes')
#             # print('   div_sbrcomposto:', div_sbrcomposto)
#             # print('Sobrenome composto:',div_sbrcomposto)
            
#             nomes.append(div_sbrcomposto[0].split(' ')[0].lower())
#             # print('    Nomes:',nomes)
#             sobrenome = div_sbrcomposto[0].split(' ')[1].upper().strip(',').strip()
#             # print('Sobrenome:',sobrenome)
            
#             for i in nomes:
#                 # print('CASO_01.e1: Para cada nome avaliar se o sobrenome está na lista')
#                 if i.lower() in sobrenome.lower():
#                     nomes.remove(i)
#             # print('  Nomes:',nomes)
        
#         # print('Ao final do Caso 01')
#         # print('    Sobrenome com vírgula:',sobrenome, len(sobrenome),'letras')
#         # print('Primeiro nome com vírgula:',primeiro_nome, len(primeiro_nome),'letras')
#         # print('           Lista de nomes:',nomes, len(nomes),'nomes')
        
#     ## Caso não haja vírgulas na string considera sobrenome o último nome da string dividida com espaço vazio
#     else:
#         # print('CASO_02: Não há víruglas na string')
#         try:
#             div = string.split(' ')
#             # print('      Divisões por espaço:',div)
            
#             if div[-1] in agnomes: # nome final é um agnome
#                 sobrenome     = div[-2].upper().strip()+' '+div[-1].upper().strip()
#                 for i in div[1:-2]:
#                     if i not in sobrenome and i not in preposicoes:
#                         nomes.append(i.title().strip())
#                     if i in preposicoes:
#                         nomes.append(i.lower().strip())
#             else:
#                 if len(div[-1]) > 2:
#                     sobrenome     = div[-1].upper().strip()
#                     primeiro_nome = div[1].title().strip()
#                     for i in div[1:-1]:
#                         if i != sobrenome and i not in preposicoes:
#                             nomes.append(i.title().strip())
#                         if i in preposicoes:
#                             nomes.append(i.lower().strip())
#                 else:
#                     sobrenome     = div[-2].upper().strip()
#                     for i in div[-1]:
#                         nomes.append(i.title())
#                     primeiro_nome = nomes[0].title().strip()
#                     for i in div[1:-1]:
#                         if i != sobrenome and i not in preposicoes:
#                             nomes.append(i.title().strip())
#                         if i in preposicoes:
#                             nomes.append(i.lower().strip())
#         except:
#             sobrenome = div[-1].upper().strip()
#             for i in div[1:-1]:
#                     if i != sobrenome and i not in preposicoes:
#                         nomes.append(i.title().strip())
#                     if i in preposicoes:
#                         nomes.append(i.lower().strip())
            
#         if sobrenome.lower() != div[0].lower().strip():
#             primeiro_nome=div[0].title().strip()
#         else:
#             primeiro_nome=''
        
#         # print('Ao final do Caso 02')
#         # print('    Sobrenome sem vírgula:',sobrenome, len(sobrenome),'letras')
#         # print('Primeiro nome sem vírgula:',primeiro_nome, len(primeiro_nome),'letras')
#         # print('Nomes do meio sem vírgula:',nomes, len(nomes),'nomes')
    
#     ## Encontrar e tratar como abreviaturas termos com apenas uma ou duas letras iniciais juntas, com ou sem ponto
#     for j in nomes:
#         # print('CASO_03: Avaliar cada nome armazenado na variável nomes')
#         # Procura padrões com expressões regulares na string
#         div_sobrenome      = sobrenome_inicio.findall(j)
#         div_sbrcomposto    = sobrenome_composto.findall(j)
#         div_abrevponto     = letra_abrevponto.findall(j)
#         div_abrevespaco    = letra_abrevespaco.findall(j)
#         div_ltrdobradasini = letras_dobradasini.findall(j)
#         div_ltrdobradasfim = letras_dobradasfim.findall(j)
#         div_ltrdobradas    = letras_dobradas.findall(j)
#         div_ltrduasconsnts = letras_duasconsnts.findall(j)
#         div_ltrtriplicadas = letras_tresconsnts.findall(j)
#         tamanho=len(j)
#         # print('\n', div_ltrdobradasini, div_ltrdobradasfim, tamanho, 'em:',j,len(j))
        
#         ## Caso houver abreviatura com uma letra em maiúscula nos nomes
#         if div_abrevponto !=[] or tamanho==1:
#             # print('CASO_03.1: Há abreviaturas uma letra maiúscula nos nomes')
#             nome = j.replace('.','').strip()
#             if nome not in nomes and nome != sobrenome and nome != primeiro_nome:
#                 # print('CASO_03.1a: Há abreviaturas uma letra maiúscula nos nomes')
#                 nomes.append(nome.upper())
        
#         ## Caso houver duas inicias juntas em maiúsculas
#         elif div_ltrdobradasini !=[] or div_ltrdobradasfim !=[] or div_ltrdobradas !=[] :
#             # print('CASO_03.2: Há abreviaturas uma letra maiúscula nos nomes')
#             for letra in j:
#                 # print('CASO_03.2a: Avaliar cada inicial do nome')
#                 if letra not in nomes and letra != sobrenome and letra != primeiro_nome:
#                     # print('CASO_03.2a.1: Se não estiver adicionar inicial aos nomes')
#                     nomes.append(letra.upper())
        
#         # Caso haja agnomes ao sobrenome
#         elif sobrenome in agnomes:
#             # print('CASO_03.3: Há agnomes nos sobrenomes')
#             sobrenome = nomes[-1].upper()+' '+sobrenome
#             # print(sobrenome.split(' '))
#             # print('Sobrenome composto:',sobrenome)
#             for i in nomes:
#                 if i.lower() in sobrenome.lower():
#                     nomes.remove(i)
#             # print('Nomes do meio:',nomes)
            
#         else:
#             # print('CASO_03.4: Não há agnomes nos sobrenomes')
#             if j not in nomes and j not in sobrenome and j != primeiro_nome:
#                 if len(nomes) == 1:
#                     nomes.append(j.upper())
#                 elif 1 < len(nomes) <= 3:
#                     nomes.append(j.lower())
#                 else:
#                     nomes.append(j.title())
         
#         # print('Ao final do Caso 03')
#         # print('    Sobrenome com vírgula:',sobrenome, len(sobrenome),'letras')
#         # print('Primeiro nome com vírgula:',primeiro_nome, len(primeiro_nome),'letras')
#         # print('Nomes do meio com vírgula:',nomes, len(nomes),'nomes')
        
#     nomes_meio=' '.join([str for str in nomes]).strip()
#     # print('        Qte nomes do meio:',nomes,len(nomes))
    
#     if primeiro_nome.lower() == sobrenome.lower():
#         # print('CASO_04: Primeiro nome é igual ao sobrenome')
#         try:
#             primeiro_nome=nomes_meio.split(' ')[0]
#         except:
#             pass
#         try:
#             nomes_meio.remove(sobrenome)
#         except:
#             pass
    
#         # print('Ao final do caso 04')
#         # print('    Sobrenome com vírgula:',sobrenome, len(sobrenome),'letras')
#         # print('Primeiro nome com vírgula:',primeiro_nome, len(primeiro_nome),'letras')
#         # print('Nomes do meio com vírgula:',nomes, len(nomes),'nomes')
    
#     ## Caso sobrenome seja só de 1 letra passá-lo para nomes e considerar o próximo nome como sobrenome
#     for i in range(len(div)):
#         if len(sobrenome)==1 or sobrenome.lower() in preposicoes:
#             # print('CASO_05: Mudar sobrenomes até o adequado')
#             div    = string.split(', ')
#             # print('Divisão por vírgulas:',div)
#             avaliar0       = div[0].split(' ')[0].strip()
#             if 1< len(avaliar0) < 3:
#                 # print('CASO_05.1: 1 < Sobrenome < 3 fica em minúsculas')
#                 sbrn0          = avaliar0.lower()
#             else:
#                 # print('CASO_05.2: Sobrenome de tamanho 1 ou maior que 3 fica em maiúsculas')
#                 sbrn0          = avaliar0.title()
#             # print('sbrn0:',sbrn0, len(sbrn0))
            
#             try:
#                 avaliar1=div[0].split(' ')[1].strip()
#                 # print('avaliar0',avaliar0)
#                 # print('avaliar1',avaliar1)
#                 if 1 < len(avaliar1) <=3:
#                     sbrn1     = avaliar1.lower()
#                 else:
#                     sbrn1     = avaliar1.title()
#                 # print('sbrn1:',sbrn1, len(sbrn1))

#             except:
#                 pass

#             if div != []:
#                 # print('CASO_05.3: Caso haja divisão por vírgulas na string')
#                 try:
#                     div_espaco     = div[1].split(' ')
#                 except:
#                     div_espaco     = div[0].split(' ')
#                 sobrenome      = div_espaco[0].strip().upper()
#                 try:
#                     primeiro_nome  = div_espaco[1].title().strip()
#                 except:
#                     primeiro_nome  = div_espaco[0].title().strip()
#                 if len(sbrn0) == 1:
#                     # print('CASO_05.3a: Avalia primeiro sobrenome de tamanho 1')
#                     # print('Vai pros nomes:',str(sbrn0).title())
#                     nomes_meio = nomes_meio+str(' '+sbrn0.title())
#                     # print('   NomesMeio:',nomes_meio)

#                 elif 1 < len(sbrn0) <= 3:
#                     # print('CASO_05.3b: Avalia primeiro sobrenome 1< tamanho <=3')
#                     # print('Vão pros nomes sbrn0:',sbrn0, 'e sbrn1:',sbrn1)

#                     div_tresconsoantes = letras_tresconsnts.findall(sobrenome)
#                     if div_tresconsoantes != []:
#                         # print('CASO_05.4: Três consoantes como sobrenome')
#                         for letra in sobrenome:
#                             nomes.append(letra)

#                         if len(sobrenome) >2:
#                             sobrenome=nomes[0]
#                         else:
#                             sobrenome=nomes[1]
#                         nomes.remove(sobrenome)
#                         primeiro_nome=nomes[0]
#                         nomes_meio=' '.join([str for str in nomes[1:]]).strip()
#                         nome_completo=sobrenome.upper()+', '+nomes_meio                
                    
#                     try:                       
#                         # print(' 05.3b    Lista de Nomes:',nomes_meio)
#                         nomes_meio=nomes_meio.replace(sbrn0,'')
#                         # print(' 05.3b ReplaceSobrenome0:',nomes_meio)
#                         nomes_meio=nomes_meio.replace(sbrn1,'')
#                         # print(' 05.3b ReplaceSobrenome1:',nomes_meio)
#                     except Exception as e:
#                         # print('   Erro ReplaceSobrenome:',e)
#                         pass
#                     try:
#                         nomes_meio.replace(primeiro_nome.title(),'')
#                         nomes_meio.replace(primeiro_nome.lower(),'')
#                         nomes_meio.replace(primeiro_nome,'')
#                         # print(' 05.3b Replace PrimNome:',nomes_meio)
#                     except Exception as e:
#                         print('Erro no try PrimeiroNome:',e)
#                         pass
#                     nomes_meio = nomes_meio.replace(sobrenome,'')
#                     try:
#                         for n,i in enumerate(avaliar1):
#                             nomes.append(i.upper())
#                             sbrn1     = avaliar1[0]
#                         else:
#                             sbrn1     = avaliar1.title()
#                         # print('sbrn1:',sbrn1, len(sbrn1))
#                         nomes_meio = nomes_meio+str(' '+sbrn0)+str(' '+sbrn1)
#                     except:
#                         nomes_meio = nomes_meio+str(' '+sbrn0)
#                     nomes      = nomes_meio.strip().strip(',').split(' ')
#                     # print(' 05.3b NomesMeio:',nomes_meio)
#                     # print(' 05.3b     Nomes:',nome)

#                 else:
#                     # print('CASO_05.3c: Avalia primeiro sobrenome >3')
#                     nomes_meio = nomes_meio+str(' '+div[0].strip().title())
#                     nomes      = nomes_meio.strip().split(' ')
#                     # print(' 05.3c NomesMeio:',nomes_meio)
#                     # print(' 05.3c     Nomes:',nomes)

#                 nomes_meio=nomes_meio.replace(sobrenome,'').replace(',','').strip()
#                 nomes_meio=nomes_meio.replace(primeiro_nome,'').strip()

#             # print('Ao final do caso 05')
#             # print('    Sobrenome com vírgula:',sobrenome, len(sobrenome),'letras')
#             # print('Primeiro nome com vírgula:',primeiro_nome, len(primeiro_nome),'letras')
#             # print('Nomes do meio com vírgula:',nomes, len(nomes),'nomes')
    
#     if sobrenome != '' and primeiro_nome !='':
#         nome_completo=sobrenome.upper().replace(',','')+', '+primeiro_nome.replace(',','')+' '+nomes_meio.replace(sobrenome,'').replace(',','')
#     elif sobrenome != '':
#         nome_completo=sobrenome.upper().replace(',','')+', '+nomes_meio.replace(sobrenome,'').replace(',','')
#     else:
#         nome_completo=sobrenome.upper()
    
# #     print('Após ajustes finais')
# #     print('     Sobrenome:',sobrenome)
# #     print(' Primeiro Nome:',primeiro_nome)
# #     print('         Nomes:',nomes)
# #     print('     NomesMeio:',nomes_meio)        
        
# #     print('                Resultado:',nome_completo)
    
#     return nome_completo.strip()



# def padronizar_titulo(titulo_bruto):
#     '''
#     Retira acentos, expressão (Org.) e espaços vazios do título da publicação
#     Autor: Marcos Aires (Fev.2022)
#     '''
#     import re
#     import unicodedata
    
#     ## Retirar caracteres não unicode
#     string = ''.join(ch for ch in unicodedata.normalize('NFKD', titulo_bruto) if not unicodedata.combining(ch))
#     string = string.replace('(Org)','').replace('(Org.)','').replace('(Org).','').replace('.',' ').replace('-',' ').replace('\'',' ').lower()
    
#     substitui_iniciais=[('rl,', 'r l,'), ('hs,', 'h s,'), ('gc,', 'g c,'), ('sf,', 's f,'), ('fo,', 'f o,'), (' oa,', ' o a,'), ('mss,', 'm s s,'), 
#                         ('lagares, ma', 'lagares, m a'), ('cota, gf', 'cota, g f'), ('cota gf,', 'cota, g f,'), ('diotaiut,', 'diotaiuti,'), ('grenfell, r f q','queiroz, rafaella fortini grenfell')]
#     for i in substitui_iniciais:
#         string = string.replace(i[0], i[1])
    
#     ## Retirar preposições
#     preposicoes = ['da', 'de', 'do', 'das', 'dos']
#     partes_string = string.split(' ')
#     string = ' '.join(x for x in partes_string if x.lower() not in preposicoes)
    
#     titulo_padronizado = string.strip().strip('"')
    
#     return titulo_padronizado



# def iniciais_nome(linha_texto):
#     '''
#     Função para retornar sobrenome+iniciais das partes de nome, na forma: SOBRENOME, X Y Z
#      Recebe: String com nome
#     Retorna: Tupla com nome e sua versão padronizada em sobrenome+agnome em maiúsculas, seguida de vírgula e das iniciais das demais partes de nome
#       Autor: Marcos Aires (Mar.2022)
#     '''
#     import unicodedata
#     import re
#     # print('               Analisando:',linha_texto)
    
#     ## Retirar caracteres não unicode
#     string = ''.join(ch for ch in unicodedata.normalize('NFKD', linha_texto) if not unicodedata.combining(ch))
#     string = string.replace('(Org)','').replace('(Org.)','').replace('(Org).','').replace('.','')
    
#     ## Retirar preposições
#     preposicoes   = ['da','de','do','das','dos']
#     partes_string = string.split(' ')
#     string = ' '.join(x for x in partes_string if x.lower() not in preposicoes)
        
#     ## Expressões regulares para encontrar padrões de divisão de nomes de autores
#     sobrenome_inicio   = re.compile(r'^[A-ZÀ-ú-a-z]+,')                 # Sequência de letras maiúsculas no início da string
#     sobrenome_composto = re.compile(r'^[A-ZÀ-ú-a-z]+[ ][A-ZÀ-ú-a-z]+,') # Duas sequências de letras no início da string, separadas por espaço, seguidas por vírgula
#     letra_abrevponto   = re.compile(r'^[A-Z][.]')                       # Uma letra maiúscula no início da string, seguida por ponto
#     letra_abrevespaco  = re.compile(r'^[A-Z][ ]')                       # Uma letra maiúscula no início da string, seguida por espaço
#     letras_dobradas    = re.compile(r'[A-Z]{2}')                        # Duas letras maiúsculas juntas no início da string, seguida por espaço
#     letras_dobradasini = re.compile(r'[A-Z]{2}[ ]')                     # Duas letras maiúsculas juntas no início da string, seguida por espaço
#     letras_dobradasfim = re.compile(r'[ ][A-Z]{2}')                     # Duas letras maiúsculas juntas no final da string, precedida por espaço
        
#     nomes=[]
#     agnomes       = ['NETO','JUNIOR','FILHO','SEGUNDO','TERCEIRO', 'SOBRINHO']
#     nome_completo = ''
    
#     ## Ajustar lista de termos, identificar sobrenomes compostos e ajustar sobrenome com ou sem presença de vírgula
#     div_sobrenome      = sobrenome_inicio.findall(string)
#     div_sbrcomposto    = sobrenome_composto.findall(string)
    
#     ## Caso haja vírgulas na string, tratar sobrenomes e sobrenomes compostos
#     if div_sobrenome != [] or div_sbrcomposto != []:
#         div   = string.split(', ')
#         sobrenome     = div[0].strip().upper()
#         try:
#             div_espaco    = div[1].split(' ')
#         except:
#             div_espaco  = ['']
#         primeiro      = div_espaco[0].strip('.')
        
#         ## Caso primeiro nome sejam somente duas letras maiúsculas juntas, trata-se de duas iniciais
#         if len(primeiro)==2:
#             primeiro_nome=primeiro[0].strip()
#             nomes.append(primeiro[1].strip())
#         else:
#             primeiro_nome = div_espaco[0].strip().title()
        
#         ## Montagem da lista de nomes do meio
#         for nome in div_espaco:
#             if nome not in nomes and nome.lower()!=primeiro_nome.lower() and nome.lower() not in primeiro_nome.lower() and nome!=sobrenome:   
#                 # print(nome, len(nome))
                
#                 ## Avaliar se é abreviatura seguida de ponto e remover o ponto
#                 if len(nome)<=2 and nome.lower() not in preposicoes:
#                     for inicial in nome:
#                         # print(inicial)
#                         if inicial not in nomes and inicial not in primeiro_nome:
#                             nomes.append(inicial.replace('.','').strip().title())
#                 else:
#                     if nome not in nomes and nome!=primeiro_nome and nome!=sobrenome and nome!='':
#                         if nome.lower() in preposicoes:
#                             nomes.append(nome.replace('.','').strip().lower())
#                         else:
#                             nomes.append(nome.replace('.','').strip().title())
#                         # print(nome,'|',primeiro_nome)
                        
#         ## Caso haja sobrenome composto que não esteja nos agnomes considerar somente primeira parte como sobrenome
#         if div_sbrcomposto !=[] and sobrenome.split(' ')[1] not in agnomes:
#             # print(div_sbrcomposto)
#             # print('Sobrenome composto:',sobrenome)
#             nomes.append(sobrenome.split(' ')[1].title())
#             sobrenome = sobrenome.split(' ')[0].upper()
#             # print('Sobrenome:',sobrenome.split(' '))
#             for i in nomes:
#                 if i.lower() in sobrenome.lower():
#                     nomes.remove(i)
#             # print('Nomes do meio:',nomes)
        
#         # print('    Sobrenome com vírgula:',sobrenome, len(sobrenome),'letras')
#         # print('Primeiro nome com vírgula:',primeiro_nome, len(primeiro_nome),'letras')
#         # print('Nomes do meio com vírgula:',nomes, len(nomes),'nomes')
        
#     ## Caso não haja vírgulas na string considera sobrenome o último nome da string dividida com espaço vazio
#     else:
#         try:
#             div       = string.split(' ')
#             if div[-2] in agnomes:
#                 sobrenome = div[-2].upper()+' '+div[-1].strip().upper()
#                 for i in nomes[1:-2]:
#                     if i not in sobrenome and i not in preposicoes:
#                         nomes.append(i.strip().title())
#                     if i in preposicoes:
#                         nomes.append(i.strip().lower())
#             else:
#                 sobrenome = div[-1].strip().upper()
#                 for i in div[1:-1]:
#                     if i not in sobrenome and i not in preposicoes:
#                         nomes.append(i.strip().title())
#                     if i in preposicoes:
#                         nomes.append(i.strip().lower())
#         except:
#             sobrenome = div[-1].strip().upper()
#             for i in div[1:-1]:
#                     if i not in sobrenome and i not in preposicoes:
#                         nomes.append(i.strip().title())
#                     if i in preposicoes:
#                         nomes.append(i.strip().lower())
            
#         if sobrenome.lower() != div[0].strip().lower():
#             primeiro_nome=div[0].strip().title()
#         else:
#             primeiro_nome=''
        
#         # print('    Sobrenome sem vírgula:',sobrenome)
#         # print('Primeiro nome sem vírgula:',primeiro_nome)
#         # print('Nomes do meio sem vírgula:',nomes)
    
#     # Encontrar e tratar como abreviaturas termos com apenas uma ou duas letras iniciais juntas, com ou sem ponto
#     for j in nomes:
#         # Procura padrões com expressões regulares na string
#         div_sobrenome      = sobrenome_inicio.findall(j)
#         div_sbrcomposto    = sobrenome_composto.findall(j)
#         div_abrevponto     = letra_abrevponto.findall(j)
#         div_abrevespaco    = letra_abrevespaco.findall(j)
#         div_ltrdobradasini = letras_dobradasini.findall(j)
#         div_ltrdobradasfim = letras_dobradasfim.findall(j)
#         div_ltrdobradas    = letras_dobradas.findall(j)
#         tamanho=len(j)
#         # print('\n', div_ltrdobradasini, div_ltrdobradasfim, tamanho, 'em:',j,len(j))
        
#         #caso houver abreviatura com uma letra em maiúscula nos nomes
#         if div_abrevponto !=[] or tamanho==1:
#             cada_nome = j.replace('.','').strip()
#             if cada_nome not in nomes and cada_nome != sobrenome and nome != primeiro_nome:
#                 nomes.append(cada_nome)
        
#         #caso houver duas inicias juntas em maiúsculas
#         elif div_ltrdobradasini !=[] or div_ltrdobradasfim !=[] or div_ltrdobradas !=[] :
#             for letra in j:
#                 if letra not in nomes and letra != sobrenome and letra != primeiro_nome:
#                     nomes.append(letra)
        
#         #caso haja agnomes ao sobrenome
#         elif sobrenome in agnomes:
#             sobrenome = nomes[-1].upper()+' '+sobrenome
#             # print(sobrenome.split(' '))
#             # print('Sobrenome composto:',sobrenome)
#             for i in nomes:
#                 if i.lower() in sobrenome.lower():
#                     nomes.remove(i)
#             # print('Nomes do meio:',nomes)
            
#         else:
#             if j not in nomes and j not in sobrenome and j != primeiro_nome:
#                 nomes.append(j)
    
#     nomes_meio=' '.join([str[0] for str in nomes]).strip()
#     # print('Qte nomes do meio',len(nomes),nomes)
#     if sobrenome != '' and primeiro_nome !='':
#         sobrenome_iniciais = sobrenome+', '+primeiro_nome[0]+' '+nomes_meio
#     elif sobrenome != '':
#         sobrenome_iniciais = sobrenome
    
#     return sobrenome_iniciais.strip()


# ## Agregar aprendizado supervisionado humano à medida que forem sendo identificados erros na situação atual
# lista_extra = [
#                 # ('ALBUQUERQUE, Adriano B', 'ALBUQUERQUE, Adriano Bessa'),
#                 # ('ALBUQUERQUE, Adriano', 'ALBUQUERQUE, Adriano Bessa'),
#                 # ('COELHO, Andre L V', 'COELHO, Andre Luis Vasconcelos'),
#                 # ('DUARTE, Joao B F', 'DUARTE, Joao Batista Furlan'),
#                 # ('FILHO, Raimir H','HOLANDA FILHO, Raimir'),
#                 # ('FILHO, Raimir','HOLANDA FILHO, Raimir'),
#                 # ('FORMIGO, A','FORMICO, Maria Andreia Rodrigues'),
#                 # ('FORMICO, A','FORMICO, Maria Andreia Rodrigues'),
#                 # ('FURLAN, J B D', 'FURLAN, Joao Batista Duarte'),
#                 # ('FURTADO, Elizabeth', 'FURTADO, Maria Elizabeth Sucupira'),
#                 # ('FURTADO, Elizabeth S', 'FURTADO, Maria Elizabeth Sucupira'),
#                 # ('FURTADO, Elizabeth Sucupira','FURTADO, Maria Elizabeth Sucupira'),
#                 # ('FURTADO, M E S', 'FURTADO, Maria Elizabeth Sucupira'),
#                 # ('FURTADO, Vasco', 'FURTADO, Joao Jose Vasco Peixoto'),
#                 # ('FURTADO, J P', 'FURTADO, Joao Jose Vasco Peixoto'),
#                 # ('FURTADO, J V P', 'FURTADO, Joao Jose Vasco Peixoto'),
#                 # ('FURTADO, Vasco', 'FURTADO, Joao Jose Vasco Peixoto'),
#                 # ('FURTADO, Elizabeth','FURTADO, Maria Elizabeth Sucupira'),
#                 # ('HOLANDA, Raimir', 'HOLANDA FILHO, Raimir'),
#                 # ('LEITE, G S', 'LEITE, Gleidson Sobreira'),
#                 # ('PEQUENO, T H C', 'PEQUENO, Tarcisio Haroldo Cavalcante'),
#                 # ('PEQUENO, Tarcisio','PEQUENO, Tarcisio Haroldo Cavalcante'),
#                 # ('PEQUENO, Tarcisio Cavalcante', 'PEQUENO, Tarcisio Haroldo Cavalcante'),
#                 # ('PINHEIRO, Placido R', 'PINHEIRO, Placido Rogerio'),
#                 # ('PINHEIRO, Vladia', 'PINHEIRO, Vladia Celia Monteiro'),
#                 # ('RODRIGUES, M A F', 'RODRIGUES, Maria Andreia Formico'),
#                 # ('RODRIGUES, Andreia', 'RODRIGUES, Maria Andreia Formico'),
#                 # ('JOAO, Batista F Duarte,', 'FURLAN, Joao Batista Duarte'),
#                 # ('MACEDO, Antonio Roberto M de', 'MACEDO, Antonio Roberto Menescal de'),
#                 # ('MACEDO, D V', 'MACEDO, Daniel Valente'),
#                 # ('MENDONCA, Nabor C', 'MENDONCA, Nabor das Chagas'),
#                 # ('PEQUENO, Tarcisio', 'PEQUENO, Tarcisio Haroldo Cavalcante'),
#                 # ('PEQUENO, Tarcisio H', 'PEQUENO, Tarcisio Haroldo Cavalcante'),
#                 # ('PINHEIRO, Mirian C D', 'PINHEIRO, Miriam Caliope Dantas'),
#                 # ('PINHEIRO, Mirian Caliope Dantas', 'PINHEIRO, Miriam Caliope Dantas'),
#                 # ('PINHEIRO, P G C D', 'PINHEIRO, Pedro Gabriel Caliope Dantas'),
#                 # ('PINHEIRO, Pedro G C', 'PINHEIRO, Pedro Gabriel Caliope Dantas'),
#                 # ('PINHEIRO, Placido R', 'PINHEIRO, Placido Rogerio'),
#                 # ('PINHEIRO, Vladia', 'PINHEIRO, Vladia Celia Monteiro'),
#                 # ('ROGERIO, Placido Pinheiro', 'PINHEIRO, Placido Rogerio'),
#                 # ('REBOUCRAS FILHO, Pedro', 'REBOUCAS FILHO, Pedro Pedrosa'),
#                 # ('SAMPAIO, A', 'SAMPAIO, Americo Tadeu Falcone'),
#                 # ('SAMPAIO, Americo', 'SAMPAIO, Americo Tadeu Falcone'),
#                 # ('SAMPAIO, Americo Falcone', 'SAMPAIO, Americo Tadeu Falcone'),
#                 # ('SUCUPIRA, Elizabeth Furtado','FURTADO, Maria Elizabeth Sucupira'),
#                 ]


# def converter_lista_set(lista):
#     set1 = set(lista)
#     return set1


# def jaccard_similarity(set1, set2):
#     '''
#     Recebe dois conjuntos como entradas e retorna a similaridade Jaccard entre eles. 
#     1. calcula a interseção dos dois conjuntos usando a função de interseção e, 
#     2. calcula a união dos dois conjuntos usando a função de união. 
#     3. retorna a razão entre o comprimento da interseção e o comprimento da união, que é a similaridade de Jaccard.
#     '''
#     intersection = set1.intersection(set2)
#     union        = set1.union(set2)
#     return len(intersection) / len(union)


# def similares(lista_autores, lista_grupo, limite_jarowinkler, distancia_levenshtein, lista_extra):
#     """Função para aplicar padronização no nome de autor da lista de pesquisadores e buscar similaridade na lista de coautores
#      Recebe: Lista de pesquisadores do grupo em análise gerada pela lista de nomes dos coautores das publicações em análise
#     Utiliza: get_jaro_distance(), editdistance()
#     Retorna: Lista de autores com fusão de nomes cuja similaridade esteja dentro dos limites definidos nesta função
#       Autor: Marcos Aires (Fev.2022)
      
#     Refazer: Inserir crítica de, mantendo sequência ordem alfabética, retornar no final nome mais extenso em caso de similaridade;
#     """
#     from pyjarowinkler.distance import get_jaro_distance
#     from IPython.display import clear_output
#     import editdistance
#     import numpy as np
#     import time
    
#     t0=time.time()
    
#     # limite_jarowinkler=0.85
#     # distancia_levenshtein=6
#     similares_jwl=[]
#     similares_regras=[]
#     similares=[]
#     tempos=[]
    
#     count=0
#     t1=time.time()
#     for i in lista_autores:
#         count+=1
#         if count > 0:
#             tp=time.time()-t1
#             tmed=tp/count*2
#             tempos.append(tp)
#         # print("Analisar similaridades com: ", nome_padronizado)
        
#         count1=0
#         for nome in lista_autores:
#             if count1 > 0:
#                 resta=len(lista_autores)-count
#                 print(f'Analisando {count1:3}/{len(lista_autores)} resta analisar {resta:3} nomes. Previsão de término em {np.round(tmed*resta/60,1)} minutos')
#             else:
#                 print(f'Analisando {count1:3}/{len(lista_autores)} resta analisar {len(lista_autores)-count1} nomes.')
            
#             t2=time.time()
#             count1+=1            

#             try:
#                 similaridade_jarowinkler = get_jaro_distance(i, nome)
#                 print(f'{i:40} | {nome:40} | Jaro-Winkler: {np.round(similaridade_jarowinkler,2):4} Levenshtein: {editdistance.eval(i, nome)}')
#                 similaridade_levenshtein = editdistance.eval(i, nome)

#                 # inferir similaridade para nomes que estejam acima do limite ponderado definido, mas não idênticos e não muito distantes em edição
#                 if  similaridade_jarowinkler > limite_jarowinkler and similaridade_jarowinkler!=1 and similaridade_levenshtein < distancia_levenshtein:
#                     # Crítica no nome mais extenso como destino no par (origem, destino)
                    
#                     similares_jwl.append((i,nome))

#             except:
#                 pass

#             clear_output(wait=True)
    
#     # Conjunto de regras de validação de similaridade
#     # Monta uma lista de nomes a serem retirados antes de montar a lista de troca
#     trocar=[]
#     retirar=[]
#     for i in similares_jwl:
#         sobrenome_i = i[0].split(',')[0]
#         sobrenome_j = i[1].split(',')[0]

#         try:
#             iniciais_i  = iniciais_nome(i[0]).split(',')[1].strip()
#         except:
#             iniciais_i  = ''

#         try:
#             iniciais_j  = iniciais_nome(i[1]).split(',')[1].strip()
#         except:
#             iniciais_j  = ''

#         try:
#             primnome_i = i[0].split(',')[1].strip().split(' ')[0].strip()
#         except:
#             primnome_i = ''

#         try:
#             primnome_j = i[1].split(',')[1].strip().split(' ')[0].strip()
#         except:
#             primnome_j = ''    

#         try:
#             inicial_i = i[0].split(',')[1].strip()[0]
#         except:
#             inicial_i = ''

#         try:
#             resto_i   = i[0].split(',')[1].strip().split(' ')[0][1:]
#         except:
#             resto_i   = ''

#         try:
#             inicial_j = i[1].split(',')[1].strip()[0]
#         except:
#             inicial_j = ''

#         try:
#             resto_j   = i[1].split(',')[1].strip().split(' ')[0][1:]
#         except:
#             resto_j = ''

#         # Se a distância de edição entre os sobrenomes
#         if editdistance.eval(sobrenome_i, sobrenome_j) > 2 or inicial_i!=inicial_j:
#             retirar.append(i)
#         else:
#             if primnome_i!=primnome_j and len(primnome_i)>1:
#                 retirar.append(i)
#             if primnome_i!=primnome_j and len(primnome_i)>1 and len(primnome_j)>1:
#                 retirar.append(i)
#             if resto_i!=resto_j and resto_i!='':
#                 retirar.append(i)
#             if len(i[1]) < len(i[0]):
#                 retirar.append(i)
#             if len(iniciais_i) != len(iniciais_j):
#                 retirar.append(i)

#     for i in similares_jwl:
#         if i not in retirar:
#             trocar.append(i)

#         if iniciais_nome(i[0]) in iniciais_nome(i[1]) and len(i[0]) < len(i[1]):
#             trocar.append(i)

#         if iniciais_nome(i[0]) == iniciais_nome(i[1]) and len(i[0]) < len(i[1]):
#              trocar.append(i)
    
#     trocar=trocar+lista_extra
#     trocar.sort()
    
#     return trocar



# def extrair_variantes(df_dadosgrupo):
#     ''' Utiliza campo de Nome em Citações do currículo como filtro para obter variantes do nome de cada membro
#      Recebe: Dataframe com os dados brutos do grupo de pesquisa agrupados; lista de nomes de pesquisadores de interesse
#     Retorna: Lista de tuplas com pares a serem trocados da variante pelo nome padronizado na forma (origem, destino)
#     '''
#     filtro1   = 'Nome'
#     lista_nomes = df_dadosgrupo[(df_dadosgrupo.ROTULOS == filtro1)]['CONTEUDOS'].values

#     variantes=[]
#     filtro='Nome em citações bibliográficas'
#     variantes=df_dadosgrupo[(df_dadosgrupo.ROTULOS == filtro)]['CONTEUDOS'].to_list()

#     trocar=[]
#     for j in range(len(variantes)):
#         padrao_destino = padronizar_nome(lista_nomes[j])
#         trocar.append((lista_nomes[j], padrao_destino))
#         for k in variantes[j]:
#             padrao_origem = padronizar_nome(k)
#             trocar.append((k, padrao_destino))
#             trocar.append((padrao_origem, padrao_destino))
    
#     return trocar

    Apurar colaborações docente/discente

In [ ]:
# def converter_lista_set(lista):
#     set1 = set(lista)
#     return set1

# def montardf_producao(lista_csv):
#     print(f'{len(lista_csv):02} nomes a extrair')
#     df_public=pd.DataFrame()
#     for nome_csv in lista_csv:
#         if 'colaboradores' in nome_csv.lower():
#             tipo='colaboradores'
#         else:
#             tipo='permanentes'
        
#         df_pub = pd.read_csv(pathcsv+nome_csv)
#         print(len(df_pub.index))
#         print(df_pub.keys())

#         pat='\t\t\t\t\t\t\t\t\t\t\t\t \t\t\t\t\t\t\t\t\t\t\t\t\t'
#         df_temp1 = df_pub.Data.str.split(pat=pat,expand=True)
#         df_temp1.columns = (['TITULO','RevAut'])

#         pat1='\t\t\t\t\t\t\t\t\t\t\t\t \t\t\t\t\t\t\t\t\t\t\t\t'
#         df_temp2 = df_temp1.RevAut.str.split(pat=pat1,expand=True)
#         df_temp2.columns = (['REVISTA','AUTORES'])

#         df_temp0 = df_pub.drop(['Data'], axis=1)
#         df_pub=df_temp0.merge(df_temp1['TITULO'],left_index=True,right_index=True)
#         df_pub=df_pub.merge(df_temp2,left_index=True,right_index=True)
#         try:
#             df_pub.drop(['Issn','Natureza'], axis=1, inplace=True)
#         except:
#             pass
#         try:
#             df_pub.drop(['Tipo','Idioma'], axis=1, inplace=True)
#         except:
#             pass

#         df_public = pd.concat([df_public, df_pub], ignore_index=True)
#         print(len(df_public.index))
#         print(df_public.keys())
        
#     ## Extrai o período com base nos dados
#     inicio = min(df_public['Ano'])
#     final  = max(df_public['Ano'])
    
#     total_artigos=len(df_public.index)
#     # print(f'{total_artigos:4} publicações de artigos de docentes do programa no período de {inicio} a {final} carregadas...') 
    
#     return df_public

# def ler_nomesdocentes():    
#     print(pathcsv)
#     import os, sys

#     lista_csv=[]
#     dirs = os.listdir(pathcsv)
#     for file in dirs:
#         if 'nomes_docentes' in file:
#             lista_csv.append(file)
#     lista_csv.sort()
    
#     for i in lista_csv:
#         print(i)

#     return lista_csv


# ## ler arquivo com as orientações para gerar a lista de discentes
# def ler_lista_orientacoes():
#     try:
#         l1='lista_orientadores-discentes.csv'
#         df_orientacoes = pd.read_csv(pathcsv+l1, delimiter=';', header=None)
        
#         lista_orientadores = df_orientacoes.iloc[:,0].unique()
#         lista_discentes    = df_orientacoes.iloc[:,1].unique()
#         print(f'{len(lista_orientadores):4} orientadores, com {len(lista_discentes)} discentes encontrados')
#     except Exception as e:
#         print('Erro ao gerar lista de orientações:')
#         print(e)
#         return df_orientacoes
        
#     return lista_orientadores, lista_discentes 


# ## montar um dataframe com nome dos discentes de cada orientador
# def montardf_orientacoes():
#     try:
#         l1='lista_orientadores-discentes.csv'
#         df_orientacoes = pd.read_csv(pathcsv+l1, delimiter=';', header=None)
#         df_orientacoes.columns=['ORIENTADOR','DISCENTE']
        
#     except Exception as e:
#         print('Erro ao dividir dataframe de orientações:')
#         print(e)
#         return
        
#     return df_orientacoes



# def montardf_docentes_permanentes_colaboradores():
#     try:
#         l1='lista_docentes_colaboradores.csv'
#         l2='lista_docentes_permanentes.csv'
#         df_docclbr = pd.read_csv(os.path.join(pathcsv,l1), header=None)
#         df_docperm = pd.read_csv(os.path.join(pathcsv,l2), header=None)
#         df_docentes = pd.concat([df_docperm, df_docclbr], ignore_index=True)
#         print(f'{len(df_docentes.index):4} docentes permanentes e colaboradores encontrados')
#     except Exception as e:
#         print(e)
        
#     return df_docentes


# def jaccard_similarity(set1, set2):
#     '''
#     Recebe dois conjuntos (sets) como entradas e retorna a similaridade Jaccard entre eles e avalia: 
#     1. calcula a interseção dos dois conjuntos usando a função de interseção 
#     2. calcula a união dos dois conjuntos usando a função de união 
#     3. retorna a razão entre o comprimento da interseção e o comprimento da união, que é a similaridade de Jaccard.
#     '''
#     intersection = set1.intersection(set2)
#     union        = set1.union(set2)
#     return len(intersection) / len(union)
    
# def montardf_docentes(lista_nomes1=False, lista_nomes2=False):
#     # print(lista_nomes1)
#     # print(lista_nomes2)

#     ## Montagem do dataframe de participação docente
#     if (lista_nomes1 and lista_nomes2) != False:
#         ## Criar dataframe com os nomes do grupo de docentes permanentes
#         file_path = os.path.join(pathcsv,'lista_docentes_permanentes.csv')
#         df_docentes_permanentes   = pd.read_csv(file_path, header=None)
#         # df_docentes_permanentes['GRUPO']='Permanente'
#         # try:
#         #     df_docentes_permanentes.drop(columns=([1,2]), inplace=True)
#         # except:
#         #     pass
#         # df_docentes_permanentes.columns = ['DOCENTE','GRUPO']
#         df_docentes_permanentes.columns = ['DOCENTE','IDLATES','PROGRAMA','GRUPO']

#         ## Criar dataframe com os nomes do grupo de docentes colaboradores
#         file_path = os.path.join(pathcsv,'lista_docentes_colaboradores.csv')
#         df_docentes_colaboradores = pd.read_csv(file_path, header=None)
#         # df_docentes_colaboradores['GRUPO']='Colaborador'
#         # try:
#         #     df_docentes_colaboradores.drop(columns=([1,2]), inplace=True)
#         # except:
#         #     pass
#         df_docentes_colaboradores.columns = ['DOCENTE','IDLATES','PROGRAMA','GRUPO']

#         ## Criar um dataframe único com todos grupos de docentes juntos
#         df_docentes = pd.concat([df_docentes_permanentes, df_docentes_colaboradores]).reset_index(drop=True)
#         return df_docentes

#     elif 'permanentes' in lista_nomes1.lower():
#         ## Criar dataframe com os nomes do grupo de docentes permanentes
#         file_path = os.path.join(pathcsv,lista_nomes1)       
#         df_docentes_permanentes   = pd.read_csv(file_path, header=None)
#         # df_docentes_permanentes['GRUPO']='Permanente'
#         # try:
#         #     df_docentes_permanentes.drop(columns=([1,2]), inplace=True)
#         # except:
#         #     pass
#         df_docentes_permanentes.columns = ['DOCENTE','IDLATES','PROGRAMA','GRUPO']
#         return df_docentes_permanentes

#     elif 'colaboradores' in lista_nomes1.lower():
#         ## Criar dataframe com os nomes do grupo de docentes colaboradores
#         file_path = os.path.join(pathcsv,lista_nomes1)
#         df_docentes_colaboradores = pd.read_csv(file_path, header=None)
#         # df_docentes_colaboradores['GRUPO']='Colaborador'
#         # try:
#         #     df_docentes_colaboradores.drop(columns=([1,2]), inplace=True)
#         # except:
#         #     pass
#         df_docentes_colaboradores.columns = ['DOCENTE','IDLATES','PROGRAMA','GRUPO']
#         return df_docentes_colaboradores
#     else:
#         print('Erro ao montar dataframe de docentes, verifique os nomes de arquivo.')
#         return
        
# def montar_listas(lista_csv, csv_permanentes=None, csv_colaboradores=None):
#     if csv_permanentes == None and csv_colaboradores == None:
#         csv_permanentes   = 'lista_docentes_permanentes.csv'
#         csv_colaboradores = 'lista_docentes_colaboradores.csv'
#         print(f'\nNomes de docentes não informados, utilizando caminho e nomes padrão:')
#         print(f'     Docentes   permanentes de {pathcsv}{csv_permanentes}')
#         print(f'     Docentes colaboradores de {pathcsv}{csv_colaboradores}')
#         try:
#             file_path = os.path.join(pathcsv,csv_permanentes)
#             df_docperm = pd.read_csv(file_path, header=None)
#             file_path = os.path.join(pathcsv,csv_colaboradores)
#             df_docclbr = pd.read_csv(file_path, header=None)
#             lista_docentes = pd.concat([df_docperm, df_docclbr], ignore_index=True)[0].values
#             print(f'{len(lista_docentes):4} docentes permanentes e colaboradores encontrados')
#         except Exception as e:
#             print(f'Erro ao ler listas de docentes, verificar se os arquivos CSV estão na pasta {pathcsv}')
#             print(e)
#     elif 'permanentes' in csv_permanentes.lower():
#         print(f'\nArquivo docentes   permanentes informado: {csv_permanentes}')
#         try:
#             file_path = os.path.join(pathcsv,csv_permanentes)
#             lista_docentes = pd.read_csv(file_path, header=None)[0].values
#             print(f'{len(lista_docentes)} docentes permanentes encontrados')
#         except Exception as e:
#             print(e)
#     elif 'colaboradores' in csv_permanentes.lower():
#         print(f'\nArquivo docentes colaboradores informado: {csv_colaboradores}')
#         try:
#             file_path = os.path.join(pathcsv,csv_permanentes)
#             lista_docentes = pd.read_csv(file_path, header=None)[0].values
#             print(f'{len(lista_docentes)} docentes colaboradores encontrados')
#         except Exception as e:
#             print(e)    
#     else:
#         print('Erro ao ler listas de docentes, verificar listas')

#     df_prod   = montardf_producao(lista_csv)
    
#     ## Montar a lista de autores com limpar_nomes remove caracteres, preposições e separa iniciais com espaço
#     lista_listas = df_prod['AUTORES'].tolist()
#     lista_autores_artigos = []
#     for i in lista_listas:
#         lista_autores_artigos.append(limpar_nomes(i))
    
#     ## Ler nomes de discentes e orientadores
#     lista_orientadores, lista_discentes = ler_lista_orientacoes()
    
#     return lista_autores_artigos, lista_docentes, lista_orientadores, lista_discentes

# def montardf_participacao_docente_discente(df_prod, dic_nomes_docentes, dic_nomes_discentes):
#     ## Montar dataframe de participação docente
#     df_participacao_docente = pd.DataFrame(dic_nomes_docentes).T
#     df_participacao_docente.columns = ['DOCENTE','INDICES_ARTIGOS']
#     df_participacao_docente['AUTORIAS'] = [len(x) for x in df_participacao_docente['INDICES_ARTIGOS']]

#     ## Montar dataframe de participação discente
#     df_participacao_discente = pd.DataFrame(dic_nomes_discentes).T
#     df_participacao_discente.columns = ['DISCENTE','INDICES_ARTIGOS']
#     df_participacao_discente['AUTORIAS'] = [len(x) for x in df_participacao_discente['INDICES_ARTIGOS']]

#     ## Criar lista com os artigos onde foi encontado nome de algum docente
#     artigos_com_docentes=[]
#     for m in df_participacao_docente['INDICES_ARTIGOS']:
#         for n in m:
#             if n not in artigos_com_docentes:
#                 artigos_com_docentes.append(n)
#     artigos_com_docentes.sort()
                
#     ## Criar lista com os artigos onde foi encontado nome de algum discente
#     artigos_com_discentes=[]
#     for m in df_participacao_discente['INDICES_ARTIGOS']:
#         for n in m:
#             if n not in artigos_com_discentes:
#                 artigos_com_discentes.append(n)
#     artigos_com_discentes.sort()
                
        
#     ## Criar lista com os artigos onde NÃO foi encontado nome de discente
#     lista_semparticipacaodiscente=[]
#     for i in range(len(df_prod.index)):
#         if i not in artigos_com_discentes and i not in lista_semparticipacaodiscente:
#             lista_semparticipacaodiscente.append(i)
            
#     ## Criar lista com os artigos onde NÃO foi encontado nome de docente
#     lista_semparticipacaodocente=[]
#     for i in range(len(df_prod.index)):
#         if i not in artigos_com_docentes and i not in lista_semparticipacaodocente:
#             lista_semparticipacaodocente.append(i)

#     ## Apresentar resultados das buscas por nomes de autores docentes e discentes
#     lista_titulos = pd.Series(df_prod['TITULO'].values).unique().tolist()
#     print(len(lista_titulos),'títulos únicos de artigo encontrados')
#     pdoc = np.round(100*len(artigos_com_docentes)/len(df_prod.index),2)
#     spdoc = np.round(100*len(lista_semparticipacaodocente)/len(df_prod.index),2)
#     print(f'{len(artigos_com_docentes):4} ({pdoc:6}%) artigos com nome de  docente encontrado, faltando {len(lista_semparticipacaodocente):3} ({spdoc:5}%)')

#     pdis = np.round(100*len(artigos_com_discentes)/len(df_prod.index),2)
#     spdis = np.round(100*len(lista_semparticipacaodiscente)/len(df_prod.index),2)
#     print(f'{len(artigos_com_discentes):4} ({pdis:6}%) artigos com nome de discente encontrado, faltando {len(lista_semparticipacaodiscente):3} ({spdis:5}%)')

#     return df_participacao_docente, df_participacao_discente, lista_semparticipacaodocente, lista_semparticipacaodiscente

    Ler arquivos de dados do disco local

In [ ]:
# ## ler arquivos de publicação de artigos na pasta de arquivos CSV
# def ler_artigostodosperiodos():    
#     print(pathcsv)
#     import os, sys

#     lista_csv=[]
#     dirs = os.listdir(pathcsv)
#     for file in dirs:
#         if 'Artigos' in file:
#             lista_csv.append(file)
#     lista_csv.sort()
    
#     for i in lista_csv:
#         print(i)

#     return lista_csv



# ## ler arquivos de publicação de de período determinado
# def ler_csvptg(inicio=False, final=False, tipo=False, grupo=False):    
#     import os, sys

#     print(pathcsv)
#     lista_csv=[]
#     dirs = os.listdir(pathcsv)
#     for file in dirs:
#         if (str(inicio) or str(final)) == False:
#             if tipo.lower() == False:
#                 if grupo.lower() == False:
#                     lista_csv.append(file)

#         elif (str(inicio) and str(final)) in file.lower():
#             if unidecode(tipo).lower() in unidecode(file).lower():
#                 if unidecode(grupo).lower() in unidecode(file).lower():
#                     lista_csv.append(file)
#     lista_csv.sort()
    
#     for i in lista_csv:
#         print(i)

#     return lista_csv

### Funções para avaliar a PCD e Pontuação de Impacto

In [ ]:
# def montardf_impacto_docente_discente(df_prod, dic_nomes_docentes, dic_nomes_discentes, inicio, final):
#     artigos_com_discentes=[]
#     artigos_com_docentes=[]
#     lista_semparticipacaodiscente=[]
#     lista_semparticipacaodocente=[]

#     try:
#         ## Montar dataframe de participação docente
#         df_impacto_docente = pd.DataFrame(dic_nomes_docentes).T
#         df_impacto_docente.columns = ['DOCENTE','INDICES_ARTIGOS','EXTRATOS_QUALIS']
#         df_impacto_docente['AUTORIAS'] = [len(x) for x in df_impacto_docente['INDICES_ARTIGOS']]

#         ## Criar lista com os artigos onde foi encontado nome de algum docente
#         for m in df_impacto_docente['INDICES_ARTIGOS']:
#             for n in m:
#                 if n not in artigos_com_docentes:
#                     artigos_com_docentes.append(n)
#         artigos_com_docentes.sort()

#         ## Criar lista com os artigos onde NÃO foi encontado nome de docente
#         for i in range(len(df_prod.index)):
#             if i not in artigos_com_docentes and i not in lista_semparticipacaodocente:
#                 lista_semparticipacaodocente.append(i)
#     except:
#         df_impacto_docente = pd.DataFrame()
#         print('Não foi possível encontrar nenhuma ocorrência dos nomes dos docentes com este conjunto de dados')
#         pass

#     try:
#         ## Montar dataframe de participação discente
#         df_impacto_discente = pd.DataFrame(dic_nomes_discentes).T
#         df_impacto_discente.columns = ['DISCENTE','INDICES_ARTIGOS','EXTRATOS_QUALIS']
#         df_impacto_discente['AUTORIAS'] = [len(x) for x in df_impacto_discente['INDICES_ARTIGOS']]

#         ## Criar lista com os artigos onde foi encontado nome de algum discente
#         for m in df_impacto_discente['INDICES_ARTIGOS']:
#             for n in m:
#                 if n not in artigos_com_discentes:
#                     artigos_com_discentes.append(n)
#         artigos_com_discentes.sort()
#     except:
#         df_impacto_discente = pd.DataFrame()
#         print('Não foi possível encontrar nenhuma ocorrência dos nomes dos discentes com este conjunto de dados')
#         pass
                
#     ## Criar lista com os artigos onde NÃO foi encontado nome de discente
#     for i in range(len(df_prod.index)):
#         if i not in artigos_com_discentes and i not in lista_semparticipacaodiscente:
#             lista_semparticipacaodiscente.append(i)

#     ## Apresentar resultados das buscas por nomes de autores docentes e discentes
#     lista_titulos = pd.Series(df_prod['TITULO'].values).unique().tolist()
#     print(len(lista_titulos),'títulos únicos de artigo encontrados')
#     pdoc  = np.round(100*len(artigos_com_docentes)/len(df_prod.index),2)
#     spdoc = np.round(100*len(lista_semparticipacaodocente)/len(df_prod.index),2)
#     print(f'{len(artigos_com_docentes):4} ({pdoc:6}%) artigos com nome de  docente encontrado, faltando {len(lista_semparticipacaodocente):3} ({spdoc:5}%)')

#     pdis = np.round(100*len(artigos_com_discentes)/len(df_prod.index),2)
#     spdis = np.round(100*len(lista_semparticipacaodiscente)/len(df_prod.index),2)
#     print(f'{len(artigos_com_discentes):4} ({pdis:6}%) artigos com nome de discente encontrado, faltando {len(lista_semparticipacaodiscente):3} ({spdis:5}%)')

#     ## A1=100, A2=80, B1=60, B2=40, B3=20, B4=10, B5=2
#     soma_impacto=[]
#     for linha in df_impacto_docente['EXTRATOS_QUALIS']:
#         impacto=0
#         for extrato in linha:
#             if extrato == 'A1':
#                 impacto+=100
#             elif extrato == 'A2':
#                 impacto+=80
#             elif extrato == 'B1':
#                 impacto+=60
#             elif extrato == 'B2':
#                 impacto+=40
#             elif extrato == 'B3':
#                 impacto+=20
#             elif extrato == 'B4':
#                 impacto+=10
#             elif extrato == 'B5':
#                 impacto+=2
#             elif extrato == 'C':
#                 impacto+=0
#             elif extrato == 'nan':
#                 impacto+=0
#         soma_impacto.append(impacto)

#     df_impacto_docente['SOMA_IMPACTO'] = soma_impacto
#     qte_anos = (final-inicio+1)
#     df_impacto_docente['ANOS'] = qte_anos
#     df_impacto_docente['IMPACTO_MEDIO_ANUAL'] = np.round(df_impacto_docente['SOMA_IMPACTO']/df_impacto_docente['ANOS'],1)

#     return df_impacto_docente, df_impacto_discente



# def apurar_pcd_impacto(df_docentes, df_impacto_docente, df_impacto_discente, meta_pcd=50.0, meta_impacto=150.0):
#     print(f'Total de nomes de docentes em análise: {len(df_docentes.index)}')
#     print(f'Total de nomes de docentes  encontrados nos artigos: {len(df_impacto_docente.index)}')
#     print(f'Total de nomes de discentes encontrados nos artigos: {len(df_impacto_discente.index)}')

#     df_docentes_pcd_impacto = df_docentes
#     ## Montar lista com os índices do dataframe de artigos onde foram achados nomes de discentes na lista de autores
#     lista_participacao_discente = []
#     for artigos_discentes in df_impacto_discente['INDICES_ARTIGOS']:
#         for indice in artigos_discentes:
#             lista_participacao_discente.append(indice)

#     ## Contar a quantidade de participações de discentes que ocorrem no dataframe de produção docente
#     qte_colab_discente=[]
#     for docente,artigos_docente in zip(df_impacto_docente['DOCENTE'], df_impacto_docente['INDICES_ARTIGOS']):
#         qte=0
#         for indice in artigos_docente:
#             if indice in lista_participacao_discente:
#                 qte+=1
            
#         qte_colab_discente.append(qte)

#     df_docentes_pcd_impacto['PUBLICAÇÕES']  = df_impacto_docente['AUTORIAS']
#     df_docentes_pcd_impacto['COM_DISCENTE'] = qte_colab_discente
#     df_docentes_pcd_impacto['PCD'] = np.round(100*(df_docentes_pcd_impacto['COM_DISCENTE']/df_impacto_docente['AUTORIAS']),1)
#     df_docentes_pcd_impacto['IMPACTO'] = df_impacto_docente['SOMA_IMPACTO']
#     df_docentes_pcd_impacto['IMPACTO_MEDIO_ANUAL'] = df_impacto_docente['IMPACTO_MEDIO_ANUAL']

#     ## Definir a meta de produção conjunta com discente e apurar o resultado
#     # meta_pcd=50.0
#     apuracao_pcd     = df_docentes_pcd_impacto.groupby([df_docentes_pcd_impacto.index,'PCD'])
#     df_abaixo_pcd    = apuracao_pcd.filter(lambda x: x['PCD'] < meta_pcd)
#     df_atingiram_pcd = apuracao_pcd.filter(lambda x: x['PCD'] >= meta_pcd)

#     total_docentes         = len(df_docentes_pcd_impacto.index)

#     contagem_abaixometa    = len(df_abaixo_pcd.index)
#     contagem_atingindometa = len(df_atingiram_pcd.index)
#     indicador_pcd = np.round(100*contagem_atingindometa/total_docentes,1)
#     print(f'{indicador_pcd}% dos docentes {contagem_atingindometa}/{total_docentes} atingem a meta de {meta_pcd}% publicação com discente')

#     ## Definir a meta de impacto por pesquisador e para o grupo
#     # meta_impacto=150
#     apuracao_impacto     = df_docentes_pcd_impacto.groupby([df_docentes_pcd_impacto.index,'IMPACTO'])
#     df_abaixo_impacto    = apuracao_impacto.filter(lambda x: x['IMPACTO_MEDIO_ANUAL'] < meta_impacto)
#     df_atingiram_impacto = apuracao_impacto.filter(lambda x: x['IMPACTO_MEDIO_ANUAL'] >= meta_impacto)

#     contagem_abaixometa_impacto    = len(df_abaixo_impacto.index)
#     contagem_atingindometa_impacto = len(df_atingiram_impacto.index)
#     indicador_impacto = np.round(100*contagem_atingindometa_impacto/total_docentes,1)
#     print(f'{indicador_impacto}% dos docentes {contagem_atingindometa_impacto}/{total_docentes} atingem a meta de {meta_impacto} pontos de impacto médio por ano das publicações')

#     return df_docentes_pcd_impacto, apuracao_pcd, df_abaixo_pcd, df_atingiram_pcd, indicador_pcd, indicador_impacto

### Funções para plotagem: 
    
    Plotar gráficos de percentual de participação discente

In [ ]:
import numpy as np
import seaborn as sns
from matplotlib import pyplot as plt
import matplotlib.patches as patches
from matplotlib.patches import Patch
from matplotlib.lines import Line2D
from matplotlib.patches import Circle
from matplotlib.offsetbox import (TextArea, DrawingArea, OffsetImage, AnnotationBbox)
from matplotlib.cbook import get_sample_data
plt.rcParams['font.size']      = 12
# plt.rcParams["figure.figsize"] = (15,9)



def plotar_pcd(df, grupo=False, inicio=False, final=False):
    N    = len(df.index)
    percentual = (df['PCD'].values.round(1))

    ind   = np.arange(N) # the x locations for the groups
    width = 0.75         # the width of the bars: can also be len(x) sequence

    # criar figura
    fig, ax = plt.subplots(figsize=(25,10))

    # plotar barras verticais com cores condicionais se abaixo do valor da variável para aceitação
    par = 50 
    cor = ['yellow' if (x < par) else 'green' for x in percentual]
    p1  = ax.bar(ind, percentual, width, 
                #  yerr=dsvpad, 
                 error_kw=dict(lw=0.3, capsize=2, capthick=1),
                 label='Percentual de publicação com discente', color=cor)

    # plotar os rótulos e título
    ax.axhline(par, color='red', linewidth=3, linestyle='dotted')
    ax.axhline(70, color='gray', linewidth=3, linestyle='dotted')
    if (grupo and inicio and final) != False:
        ax.set_title(f'Apuração do percentual de publicação de docentes {grupo.upper()} com discente no período de {inicio} a {final}')
    elif grupo == False:
        ax.set_title(f'Apuração do percentual de publicação de docentes com discente no período de {inicio} a {final}')
    else:
        ax.set_title(f'Apuração do percentual de publicação com discente')

    ax.set_ylabel('Percentual de artigos publicados com discente')
    ax.set_xticks(ind)
    
    labels_pos=np.arange(1,N+1)
    ax.set_xticklabels(labels_pos)

    # Label with label_type 'center' instead of the default 'edge'
    ax.bar_label(p1, label_type='center')
    # ax.bar_label(p1, dsvpad)
    # ax.set_yticks(range(0,100))
    
    # respectivo domínio de cada questão no AGREE II
    grupos = ['01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01',
              '02','02','02','02','02','02','02','02','02','02','02','02','02','02','02','02',]
    
    # calcular limites de retângulos dos domínios
    lista_dominios   = pd.Series(grupos)
    largura_dominios = lista_dominios.value_counts().sort_index().values   
    altura = 100
    rets=[]   
    
    for i in range(1,len(largura_dominios)+1):
        ret = patches.Rectangle((-0.5,0),
                                np.sum(largura_dominios[:i]), altura,
#                                 linestyle='dashdot',
                                linewidth=2,
                                edgecolor='b',
                                fill = False)
        rets.append(ret)
    
    # plotar os retângulos das dimensões na área do gráfico
    for i in rets:
        ax.add_patch(i)
        
    # plotar legenda, comentar para excluir
    # ax.legend(bbox_to_anchor=(0.75,-0.05), ncol=2)
    
    campo='04'
    # savefig_respostas(campo)
    
    plt.show()
    return 



def plotar_medias_impacto(df, grupo=False, inicio=False, final=False):
    N      = len(df.index)
    pontos = (df['IMPACTO_MEDIO_ANUAL'].values.round(1))

    ind   = np.arange(N) # the x locations for the groups
    width = 0.75         # the width of the bars: can also be len(x) sequence

    # criar figura
    fig, ax = plt.subplots(figsize=(25,10))

    # plotar barras verticais com cores condicionais se abaixo do valor da variável para aceitação
    par = 150 
    cor = ['yellow' if (x < par) else 'green' for x in pontos]
    p1  = ax.bar(ind, pontos, width, 
                #  yerr=dsvpad, 
                 error_kw=dict(lw=0.3, capsize=2, capthick=1),
                 label='Pontuação em impacto das publicações de docentes', color=cor)

    # plotar os rótulos e título
    ax.axhline(par, color='red', linewidth=3, linestyle='dotted')
    if (grupo and inicio and final) != False:
        ax.set_title(f'Apuração da pontuação de impacto das publicações de docentes {grupo.upper()} no período de {inicio} a {final}')
    elif (inicio and final) != False:
        ax.set_title(f'Apuração da pontuação de impacto das publicações de docentes no período de {inicio} a {final}')
    else:
        ax.set_title(f'Apuração da pontuação de impacto médio (total do impacto acumulado / quantidade de anos do período) das publicações de docentes')

    ax.set_ylabel('Pontuação ponderada pelo Qualis dos artigos publicados')
    ax.set_xticks(ind)
    
    labels_pos=np.arange(1,N+1)
    ax.set_xticklabels(labels_pos)

    # Label with label_type 'center' instead of the default 'edge'
    ax.bar_label(p1, label_type='center')
    # ax.bar_label(p1, dsvpad)
    vr_maximo = int(max(pontos)+50)
    # ax.set_yticks(range(0,vr_maximo))
    
    # respectivo domínio de cada questão no AGREE II
    grupos = ['01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01','01',
              '02','02','02','02','02','02','02','02','02','02','02','02','02','02','02','02',]
    
    # calcular limites de retângulos dos domínios
    lista_dominios   = pd.Series(grupos)
    largura_dominios = lista_dominios.value_counts().sort_index().values   
    altura = max(pontos)+50
    rets=[]   
    
    for i in range(1,len(largura_dominios)+1):
        ret = patches.Rectangle((-0.5,0),
                                np.sum(largura_dominios[:i]), altura,
#                                 linestyle='dashdot',
                                linewidth=2,
                                edgecolor='b',
                                fill = False)
        rets.append(ret)
    
    # plotar os retângulos das dimensões na área do gráfico
    for i in rets:
        ax.add_patch(i)
        
    # plotar legenda, comentar para excluir
    # ax.legend(bbox_to_anchor=(0.75,-0.05), ncol=2)
    
    campo='04'
    # savefig_respostas(campo)
    
    plt.show()
    return 

## Apurar participação discente e impacto artigos dos docentes
### Todos os períodos e grupos

In [ ]:
os.listdir(pathcsv)

In [ ]:
lista_nomes_docentes_permanentes   = 'lista_docentes_permanentes.csv'
lista_nomes_docentes_colaboradores = 'lista_docentes_colaboradores.csv'
df_docentes = montardf_docentes(lista_nomes_docentes_permanentes, lista_nomes_docentes_colaboradores)

## Escolha dos arquivos que alimentarão a análise da produção
lista_csv = ler_artigostodosperiodos()
lista_csv

In [ ]:
df_docentes

In [ ]:
pathfilename = os.path.join(pathcsv,'lista_docentes.csv')
lista_csv = pd.read_csv(pathfilename,header=None)[0].values

In [ ]:
df_prod   = montardf_producao(lista_csv)

## Mostrar quantitativos lidos
print(f'\nCarregado dataframe com {len(df_prod.index)} linhas:')
lista_titulos = pd.Series(df_prod['TITULO'].values).unique().tolist()
print(f'{len(lista_titulos):4} artigos distintos publicados no período')
lista_revistas = pd.Series(df_prod['REVISTA'].values).unique().tolist()
print(f'{len(lista_revistas):4} revistas distintas utilizadas no período')

## Ler nomes de docentes, discentes e papel de orientador
lista_autores_artigos, lista_docentes, lista_orientadores, lista_discentes = montar_listas(lista_csv)
qte_docentes=len(lista_docentes)
qte_discentes=len(lista_discentes)
total_iteracoes=(qte_docentes+qte_discentes)

In [ ]:
df_docentes

    Organizar lista de autores e iniciais de nomes
    PROBLEMA: não está quebrando no número de artigos 1115, mas sim em apenas 2 e última vazia

In [ ]:
## Montar a lista de autores a partir da lista de strings limpa com nomes de autores
def organizar_nomes(str_autores_artigo):
    erros_organizar  = []
    lista_organizada = []
    partes_nomes = str_autores_artigo.split(', ')
    n       = len(partes_nomes)
    pares   = range(0,n+1,2)
    impares = range(1,n+1,2)
    try:
        for i,j in zip(pares,impares):
            nome=[]
            try:
                nomes_ordenado = str(partes_nomes[j].lower()+' '+partes_nomes[i].lower()).replace('  ',' ').strip()
            except:
                if len(pares) > len(impares):
                    nomes_ordenado = str(partes_nomes[j].lower()).replace('  ',' ').strip()
                else:
                    nomes_ordenado = str(partes_nomes[i].lower()).replace('  ',' ').strip()
            lista_organizada.append(nomes_ordenado)
    
    except Exception as e1:
        print('Erro ao montar listas de nomes de autor:',e1)
        erros_organizar.append((i,str_autores_artigo))

    return lista_organizada, erros_organizar

## Quebrar um nome em seu sobrenome seguido das partes de nome
def quebrar_partesnomes(nome):
    padrao     = padronizar_nome(nome).lower()
    sobrenome  = padrao.split(',')[0].strip()
    restonomes = padrao.split(',')[1].strip().split(' ')
    try:
        partenome1 = restonomes[0].strip()
    except:
        partenome1 = np.NaN
    try:
        partenome2 = restonomes[1].strip()
    except:
        partenome2 = np.NaN
    try:
        partenome3 = restonomes[2].strip()
    except:
        partenome3 = np.NaN        
    # print(f'{sobrenome:15} | {partenome1:1} | {partenome2:1} | {partenome3}')
    
    return sobrenome, partenome1, partenome2, partenome3


## Quebrar um nome em seu sobrenome seguido as iniciais das partes de nome
def quebrar_iniciais(nome):
    padrao = iniciais_nome(nome).lower()
    sobrenome  = padrao.split(',')[0].strip()
    restonomes = padrao.split(',')[1].strip().split(' ')

    try:
        partenome1 = restonomes[0].strip()
    except:
        partenome1 = np.NaN
    try:
        partenome2 = restonomes[1].strip()
    except:
        partenome2 = np.NaN
    try:
        partenome3 = restonomes[2].strip()
    except:
        partenome3 = np.NaN        
    # print(f'{sobrenome:15} | {partenome1:1} | {partenome2:1} | {partenome3}')
    
    return sobrenome, partenome1, partenome2, partenome3


## compilar padrão regular expression para buscar ocorência de duas das quatro partes de nome dentro de janela de no máximo 2 palavras de distância
def compilar_partes(sobrenome, partenome1, partenome2, partenome3):
    return re.compile(r'\b({0}|{1}|{2}|{3})(?:\W+\w+){{0,2}}?\W+({1}&{2}|{2}&{3}|{0}&{1}|{0}&{3})\b'.format(sobrenome, partenome1, partenome2, partenome3), flags=re.IGNORECASE)

def compilar_iniciais(sobrenome, inicial1, inicial2, inicial3):
    return re.compile(r'\b({0})(?:\W+\w+){{0,1}}?\W+({1}|{2}|{3})\b'.format(sobrenome, inicial1, inicial2, inicial3), flags=re.IGNORECASE)

In [ ]:
def gerar_dicionarios(df_prod, lista_docentes, lista_discentes, inicio = min(df_prod['Ano']), final  = max(df_prod['Ano'])):
    qte_docentes     = len(lista_docentes)
    qte_discentes    = len(lista_discentes)
    total_iteracoes  = (qte_docentes+qte_discentes)
    
    ## Monta uma lista de strings com nomes dos autores de cada artigo na forma extraída pelo e-lattes
    lista_nomes_autores = [limpar_nomes(x) for x in df_prod['AUTORES'].values]
    qte_artigos         = len(lista_nomes_autores)
        
    ## Define os limites para considerar duas strings com nomes similares entre si
    limite_jaro_nome        = 0.88
    limite_jaro_iniciais    = 0.75
    limite_jaccard_iniciais = 0.32

    ## Função para calcular similaridade dos nomes de docentes com cada nome de autor da lista de autores de cada artigo
    t1 = time.time()
    dic_nomes_docentes  = {}
    dic_nomes_discentes = {}    
    erros=[]
    rot1='Comparando nome do docente'
    rot2='Sobren/Iniciais docen'
    rot3='Sobrenome/Iniciais autor'
    rot4='I.Doc'
    rot5='I.Aut'
    rot6='Jaro-Winkler'
    rot7='Jaccard'
    for m,docente in enumerate(lista_docentes):
        achados_docentes     = []
        lista_indice_docente = []
        lista_qualis_docente = []
        docentes_naoencontrados = []          
        contagem=m+1
        # clear_output(wait=True)       
        try:
            nome_docente_padronizado = padronizar_nome(docente).lower()
            iniciais_nome_docente    = iniciais_nome(docente).lower()
            string_iniciais_docente  = ' '.join(x.strip() for x in iniciais_nome_docente.split(',')[1:])
            set_iniciais_docente     = converter_lista_set([x.strip() for x in iniciais_nome_docente.split(',')[1:]])                
            print(f'\nCálculo das similaridades autores-docentes (nome/iniciais/Jaccard):')
            print(f'{rot1:^40} |{rot2:^20}| {rot3:^25}|{rot4:^5}|{rot5:^5}|{rot6:^15}|{rot7:^10}')
            ## Monta a lista de autores com a divisão da string organizada padronizada no formato: {sobrenome, iniciais de nomes}
            lst_autores_artigo = []
            lista_nomes_autores = [limpar_nomes(x) for x in df_prod['AUTORES'].values]
            for n,nomes_autor in enumerate(lista_nomes_autores):
                autores,erros = organizar_nomes(nomes_autor)
                for o,autor in enumerate(autores):
                    qte_autores_artigo = len(autores)
                    # print(f'{o+1:2}/{qte_autores_artigo:2} nomes de autor do artigo em análise, restando {qte_autores_artigo-o-1:2}')
                    nome_autor_padronizado = padronizar_nome(autor).lower()
                    try:    
                        iniciais_nome_autor    = iniciais_nome(autor).lower()
                        string_iniciais_autor  = ' '.join(x.strip() for x in iniciais_nome_autor.split(',')[1:])
                        set_iniciais_autor     = converter_lista_set([x.strip() for x in iniciais_nome_autor.split(',')[1:]])
                        # time.sleep(1)
                        ## Cálculos de similaridades entre os nomes do autor e do docente
                        if iniciais_nome_docente and iniciais_nome_autor != '':
                            similaridade_nome     = get_jaro_distance(iniciais_nome_docente, iniciais_nome_autor)
                            similaridade_iniciais = get_jaro_distance(string_iniciais_docente, string_iniciais_autor)
                            similaridade_jaccard  = np.round(jaccard_similarity(set_iniciais_docente, set_iniciais_autor),2)
                            print(f'\nCálculo das similaridades autores-discentes (nome/iniciais/Jaccard):')
                            print(f'{padronizar_nome(docente):^40} | {iniciais_nome_docente:<20}|{iniciais_nome_autor:<20} {similaridade_nome:^5}|{string_iniciais_docente:^5}|{string_iniciais_autor:^5}|{similaridade_iniciais:^15}|{similaridade_jaccard:^10}')
                            clear_output(wait=True)
                            if similaridade_nome > limite_jaro_nome and similaridade_iniciais > limite_jaro_iniciais and similaridade_jaccard > limite_jaccard_iniciais:
                                if n not in lista_indice_docente:
                                    print(f'Similaridade encontrada no artigo {n+1}/{qte_artigos}, docente {m+1}/{qte_docentes}')
                                    print(f'{rot1:^40} |{rot2:^20}| {rot3:^25}|{rot4:^5}|{rot5:^5}|{rot6:^15}|{rot7:^10}')
                                    print(f'{padronizar_nome(docente):^40} | {iniciais_nome_docente:<20}|{iniciais_nome_autor:<20} {similaridade_nome:^5}|{string_iniciais_docente:^5}|{string_iniciais_autor:^5}|{similaridade_iniciais:^15}|{similaridade_jaccard:^10}')
                                    achados_docentes.append(docente)
                                    lista_indice_docente.append(n)
                                    # print(len(lista_indice_docente))
                                    extrato = df_prod['Qualis'][n]
                                    lista_qualis_docente.append(extrato)
                                    clear_output(wait=True)                                    
                    except Exception as e1:
                        # print(f'Erro na etapa 1 de gerar_dicionarios, ao tratar iniciais do nome de autor/docente da linha  {n}/{o}/{qte_docentes}/{qte_artigos}')
                        # print(e1)
                        similaridade_iniciais = np.NaN
                        similaridade_jaccard  = np.NaN
                        erros.append(('e1_similaridadesdocente',m,n,o,e1))                    
                lst_autores_artigo.append(iniciais_nome_autor)
            # print(f'Lista organizada de nomes de autores: {len(lst_autores_artigo)} listas de autores de artigos publicados no período')

            ## Ao final da leitura todos artigos para cada docente, criar o dicionário de docentes quando docente tenha aparecido na linha de autores
            if lista_indice_docente != []:
                dic_nomes_docentes[m] = (docente, lista_indice_docente, lista_qualis_docente)
            else:
                docentes_naoencontrados.append(docente)

            tdec=time.time()-t1
            # tres=tdec/(m+1)*((qte_docentes-m)+qte_discentes)
            # print(f'Analisadas{m+1:4}/{total_iteracoes} iterações em {horas(tdec)}, restando {total_iteracoes-m}. Busca{m+1:4}/{qte_docentes:<4}docente: {docente.title():50}')
            # print(f'Nome do docente foi encontrado em {len(lista_indice_docente):2} artigos')
        except Exception as e2:
            # print(f'Erro na etapa 2 de gerar_dicionarios, ao calcular similaridades de autor/docente  da linha {n}/{o}/{qte_docentes}/{qte_artigos}')
            # print(e2)
            erros.append(('e2_padronizardocentes',m,n,o,e2)) 

    ## Função para calcular similaridade dos nomes de discentes com cada nome de autor da lista de autores de cada artigo
    for p,discente in enumerate(lista_discentes):
        achados_discentes     = []
        lista_indice_discente = []
        lista_qualis_discente = []
        discentes_naoencontrados = []
        contagem=m+p+1
        # clear_output(wait=True)       
        try:
            nome_discente_padronizado = padronizar_nome(discente).lower()
            iniciais_nome_discente    = iniciais_nome(discente).lower()
            string_iniciais_discente  = ' '.join(x.strip() for x in iniciais_nome_discente.split(',')[1:])
            set_iniciais_discente     = converter_lista_set([x.strip() for x in iniciais_nome_discente.split(',')[1:]])
            rot2='Sobren/Iniciais disce'
            rot4='I.Dis'            
            ## Monta a lista de autores com a divisão da string organizada padronizada no formato: {sobrenome, iniciais de nomes}
            lst_autores_artigo = []
            lista_nomes_autores = [limpar_nomes(x) for x in df_prod['AUTORES'].values]
            for n,nomes_autor in enumerate(lista_nomes_autores):
                # clear_output(wait=True)
                # print(f'Procurando {nome_discente_padronizado.title()} em {n+1:2}/{qte_artigos:<2} artigos, restando {qte_artigos-n-1:<2}')
                autores,erros = organizar_nomes(nomes_autor)
                for q,autor in enumerate(autores):
                    qte_autores_artigo = len(autores)
                    nome_autor_padronizado = padronizar_nome(autor).lower()
                    # print(f'{q+1:2}/{qte_autores_artigo:2} nomes de autor do artigo em análise, restando {qte_autores_artigo-q-1:2}')
                    nome_autor_padronizado = padronizar_nome(autor).lower()
                    try:    
                        iniciais_nome_autor    = iniciais_nome(autor).lower()
                        string_iniciais_autor  = ' '.join(x.strip() for x in iniciais_nome_autor.split(',')[1:])
                        set_iniciais_autor     = converter_lista_set([x.strip() for x in iniciais_nome_autor.split(',')[1:]])   
                        ## Cálculos de similaridades entre os nomes do autor e do discente
                        if iniciais_nome_discente and iniciais_nome_autor != '':
                            similaridade_nome     = get_jaro_distance(iniciais_nome_discente, iniciais_nome_autor)
                            similaridade_iniciais = get_jaro_distance(string_iniciais_discente, string_iniciais_autor)
                            similaridade_jaccard  = np.round(jaccard_similarity(set_iniciais_discente, set_iniciais_autor),2)
                            print(f'{padronizar_nome(discente):^40} | {iniciais_nome_discente:<20}|{iniciais_nome_autor:<20} {similaridade_nome:^5}|{string_iniciais_docente:^5}|{string_iniciais_autor:^5}|{similaridade_iniciais:^15}|{similaridade_jaccard:^10}')                            
                            if similaridade_nome > limite_jaro_nome and similaridade_iniciais > limite_jaro_iniciais and similaridade_jaccard > limite_jaccard_iniciais:
                                if n not in lista_indice_discente:
                                    print(f'Similaridade encontrada no artigo {n+1}/{qte_artigos}, discente {p+1}/{qte_discentes}')
                                    print(f'{rot1:^40} |{rot2:^20}| {rot3:^25}|{rot4:^5}|{rot5:^5}|{rot6:^15}|{rot7:^10}')
                                    print(f'{padronizar_nome(discente):^40} | {iniciais_nome_discente:<20}|{iniciais_nome_autor:<20} {similaridade_nome:^5}|{string_iniciais_discente:^5}|{string_iniciais_autor:^5}|{similaridade_iniciais:^15}|{similaridade_jaccard:^10}')
                                    achados_discentes.append(discente)
                                    lista_indice_discente.append(n)
                                    # print(len(lista_indice_discente))
                                    extrato = df_prod['Qualis'][n]
                                    lista_qualis_discente.append(extrato)
                                    clear_output(wait=True)
                    except Exception as e3:
                        similaridade_iniciais = np.NaN
                        similaridade_jaccard  = np.NaN
                        # print(f'Erro na etapa 3 de gerar_dicionarios, ao calcular similaridades de nomes de autor/discente da linha {n}/{o}/{qte_discentes}/{qte_artigos}')
                        # print(e3)
                        erros.append(('e3_buscadiscentes',p,n,q,e3))
        
            ## Ao final da leitura todos artigos para cada discente, criar o dicionário de discente quando docente tenha aparecido na linha de autores
            if lista_indice_discente != []:
                dic_nomes_discentes[o] = (discente, lista_indice_discente, lista_qualis_discente)
            else:
                discentes_naoencontrados.append(discente)            
            
            tdec=time.time()-t1
            # tres=tdec/(o+p+1)*((qte_discentes-p)+qte_discentes)
            # print(f'Analisadas{contagem+1:4}/{total_iteracoes} iterações em {horas(tdec)}, restando {horas(tres)} para iterar {total_iteracoes-contagem-1}. Busca{p+1:4}/{qte_discentes:<4}discente: {discente.title():50}')
            # print(f'Nome do discente foi encontrado em {len(lista_indice_discente):2} artigos')   
        except Exception as e4:
            # print('Erro na etapa 4 de gerar_dicionarios, ao finalizar montagem dos dicionários:',e4)
            erros.append(('e4_padronizardiscente',m,n,e4))

    return dic_nomes_docentes, dic_nomes_discentes, docentes_naoencontrados, discentes_naoencontrados, erros

In [ ]:
dic_nomes_docentes, dic_nomes_discentes, docentes_naoencontrados, discentes_naoencontrados, erros = gerar_dicionarios(df_prod, lista_docentes, lista_discentes)

In [ ]:
# dic_nomes_docentes

In [ ]:
print(len(docentes_naoencontrados),'total de nomes de  docentes não encontrados nos artigos')
print(len(discentes_naoencontrados),'total de nomes de discentes não encontrados nos artigos')

In [ ]:
discentes_naoencontrados

In [ ]:
len(erros)

In [ ]:
erros[:3]

In [ ]:
# lista_artigos_problemas = []
# lista_autores_problemas = []
# for etapa,docente,i,discente,artigo in erros:
#     if i not in lista_artigos_problemas:
#         lista_artigos_problemas.append(i)
#         lista_autores_problemas.append(df_prod['AUTORES'][i])

# df_artigos_problemas=pd.DataFrame(lista_artigos_problemas).reset_index(drop=True)
# df_artigos_problemas['LISTA_AUTORES'] = lista_autores_problemas
# df_artigos_problemas

In [ ]:
# ## Lista ordenada alfabeticamente pelos sobrenomes de docentes
# lista_docentes_sobrenome=[]
# for i in lista_docentes:
#     lista_docentes_sobrenome.append(iniciais_nome(i))
    
# lista_docentes_sobrenome.sort()
# for j in lista_docentes_sobrenome:
#     print(f'{j.lower()}')

In [ ]:
inicio = 2017
final  = 2022
df_impacto_docente, df_impacto_discente = montardf_impacto_docente_discente(df_prod, dic_nomes_docentes, dic_nomes_discentes, inicio, final)
df_impacto_docente

In [ ]:
df_docentes = montardf_docentes(lista_nomes_docentes_permanentes, lista_nomes_docentes_colaboradores)
df_docentes_pcd_impacto, apuracao_pcd, df_abaixo_pcd, df_atingiram_pcd, indicador_pcd, indicador_impacto = apurar_pcd_impacto(df_docentes, df_impacto_docente, df_impacto_discente, meta_pcd=50.0, meta_impacto=150.0)

In [ ]:
plotar_pcd(df_docentes_pcd_impacto)
plotar_medias_impacto(df_docentes_pcd_impacto, grupo=False, inicio=False, final=False)

### Funções avaliação PCD e Impacto Médio Anual: 
    Avaliar indicadores PCD e Somatório do Fator de Impacto

In [ ]:
def avaliar_completo(inicio, final, tipo, grupo, lista_nomes_docentes):
    ## Ler arquivos de dados
    lista_csv   = ler_csvptg(inicio, final, tipo, grupo)
    df_public   = montardf_producao(lista_csv)
    df_docentes = montardf_docentes(lista_nomes_docentes)
    lista_autores_artigos, lista_docentes, lista_orientadores, lista_discentes = montar_listas(lista_csv, lista_nomes_docentes)

    ## Avaliação da Publicação Conjunta com Discentes (PCD) e do Impacto Médio Anual (IMA)
    dic_nomes_docentes, dic_nomes_discentes, docentes_naoencontrados, discentes_naoencontrados, erros = gerar_dicionarios(df_public, lista_docentes, lista_discentes, inicio, final)
    df_impacto_docente, df_impacto_discente = montardf_impacto_docente_discente(df_public, dic_nomes_docentes, dic_nomes_discentes, inicio, final)

    ## Gerar gráfico de apuração de impacto médio anual por docente
    df_docentes_pcd_impacto, apuracao_pcd, df_abaixo_pcd, df_atingiram_pcd, indicador_pcd, indicador_impacto = apurar_pcd_impacto(df_docentes, df_impacto_docente, df_impacto_discente)
    plotar_pcd(df_docentes_pcd_impacto, grupo, inicio, final)
    plotar_medias_impacto(df_docentes_pcd_impacto, grupo, inicio, final)

    return df_public, df_impacto_docente, df_impacto_discente, df_docentes_pcd_impacto, indicador_pcd, indicador_impacto

### Testes

In [ ]:
# a,b='',''
# get_jaro_distance(a, b)

In [ ]:
a,b='1','0'
get_jaro_distance(a, b)

In [ ]:
lista_nomes_autores = [limpar_nomes(x) for x in df_prod['AUTORES'].values]
print(len(lista_nomes_autores))
print(lista_nomes_autores[0])

## Verifica se a divisão em nomes de autor é par (sobrenome separado de nomes por vírgula)
for i in lista_nomes_autores[:14]:
    qte_nomes_autor = len(i.split(','))
    if qte_nomes_autor/2 != qte_nomes_autor//2:
        print(qte_nomes_autor,'\n')

In [ ]:
for m,docente in enumerate(lista_docentes):
    nome_docente_padronizado = padronizar_nome(docente).lower()
    iniciais_nome_docente    = iniciais_nome(docente).lower()
    print(iniciais_nome_docente)

In [ ]:
    # ## Monta a lista de autores com a divisão da string de nomes acima por: sobrenome, nomes
    # lst_autores_artigo = []
    # lista_nomes_autores = [limpar_nomes(x) for x in df_prod['AUTORES'].values]
    # for n,nomes_autor in enumerate(lista_nomes_autores):
    #     autores,erros = organizar_nomes(nomes_autor)
    #     # print(autores,'\n')
    #     for o,autor in enumerate(autores):
    #         # print(autor)
    #         # print(f'{o+1:2}/{qte_autores_artigo:2} nomes de autor do artigo em análise, restando {qte_autores_artigo-o-1:2}')
    #         sobrenome_iniciais_autor = iniciais_nome(autor).lower()
    #         string_iniciais_autor    = ' '.join(x.strip() for x in sobrenome_iniciais_autor.split(',')[1:])
    #         set_iniciais_autor       = converter_lista_set([x.strip() for x in sobrenome_iniciais_autor.split(',')[1:]])
    #         print(f'{sobrenome_iniciais_autor:20}|{string_iniciais_autor:^9}|{set_iniciais_autor}')
    #     lst_autores_artigo.append(sobrenome_iniciais_autor)
    # print(f'Lista organizada de nomes de autores: {len(lst_autores_artigo)} listas de autores de artigos publicados no período')

In [ ]:
qte_docentes     = len(lista_docentes)
qte_discentes    = len(lista_discentes)
total_iteracoes  = (qte_docentes+qte_discentes)

## Monta uma lista de strings com nomes dos autores de cada artigo
lista_nomes_autores = [limpar_nomes(x) for x in df_prod['AUTORES'].values]
qte_artigos         = len(lista_nomes_autores)

## Monta a lista de autores com a divisão da string de nomes acima por: sobrenome, nomes
lst_autores_artigo = []
for cada_lista_autores in lista_nomes_autores:
    lista_organizada, erros_organizar = organizar_nomes(cada_lista_autores)
    lst_autores_artigo.append(lista_organizada)
print(f'{len(lst_autores_artigo)} listas de autores de {qte_artigos} artigos publicados no período')

In [ ]:
lista_nomes_autores[:3]

In [ ]:
lst_autores_artigo[:3]

In [ ]:
a='a b c de oliveira'
padronizar_nome(a)
iniciais_nome(a)

## Apuração segmentada por períodos e grupos

In [ ]:
evolucao_pcd=[]
evolucao_impacto=[]
tipo_analise=[]
grupo_analise=[]
periodo_analise=[]

## Quadriênio 2017-2020 de Docentes Permanentes

In [ ]:
lista_nomes_docentes_permanentes   = 'lista_docentes_permanentes.csv'
lista_nomes_docentes_colaboradores = 'lista_docentes_colaboradores.csv'
df_docentes = montardf_docentes(lista_nomes_docentes_permanentes, lista_nomes_docentes_colaboradores)

In [ ]:
inicio = 2017
final  = 2020
tipo   = 'artigos'
grupo  = 'permanentes'
lista_nomes_docentes = 'lista_docentes_permanentes.csv'

df_public, df_impacto_docente, df_impacto_discente, df_docentespcd, indicador_pcd, indicador_impacto = avaliar_completo(inicio, final, tipo, grupo, lista_nomes_docentes)
evolucao_pcd.append(indicador_pcd)
evolucao_impacto.append(indicador_impacto)
tipo_analise.append(tipo)
grupo_analise.append(grupo)
periodo_analise.append([inicio,final])

## .
## Quadriênio 2017-2020 de Docentes Colaboradores

In [ ]:
inicio = 2017
final  = 2020
tipo   = 'artigos'
grupo  = 'colaboradores'
lista_nomes_docentes = 'lista_docentes_colaboradores.csv'

df_public, df_impacto_docente, df_impacto_discente, df_docentespcd, indicador_pcd, indicador_impacto = avaliar_completo(inicio, final, tipo, grupo, lista_nomes_docentes)
evolucao_pcd.append(indicador_pcd)
evolucao_impacto.append(indicador_impacto)
tipo_analise.append(tipo)
grupo_analise.append(grupo)
periodo_analise.append([inicio,final])

## Avaliação de meio termo biênio [2021-2022]

## Biênio 2021-2022 de Docentes Permanentes

In [ ]:
inicio = 2021
final  = 2022
tipo   = 'artigos'
grupo  = 'permanentes'
lista_nomes_docentes = 'lista_docentes_permanentes.csv'
# lista_nomes_docentes = 'lista_docentes_colaboradores.csv'

df_public, df_impacto_docente, df_impacto_discente, df_docentespcd, indicador_pcd, indicador_impacto = avaliar_completo(inicio, final, tipo, grupo, lista_nomes_docentes)
evolucao_pcd.append(indicador_pcd)
evolucao_impacto.append(indicador_impacto)
tipo_analise.append(tipo)
grupo_analise.append(grupo)
periodo_analise.append([inicio,final])

## Biênio 2021-2022 de Docentes Colaboradores

In [ ]:
inicio = 2021
final  = 2022
tipo   = 'artigos'
grupo  = 'colaboradores'
# lista_nomes_docentes = 'lista_docentes_permanentes.csv'
lista_nomes_docentes = 'lista_docentes_colaboradores.csv'

df_public, df_impacto_docente, df_impacto_discente, df_docentespcd, indicador_pcd, indicador_impacto = avaliar_completo(inicio, final, tipo, grupo, lista_nomes_docentes)
evolucao_pcd.append(indicador_pcd)
evolucao_impacto.append(indicador_impacto)
tipo_analise.append(tipo)
grupo_analise.append(grupo)
periodo_analise.append([inicio,final])

## Evolução de indicadores de gestão do programa

In [ ]:
df_indicadores = pd.DataFrame({
    'TIPO': pd.Series(tipo_analise),
    'GRUPO': pd.Series(grupo_analise),
    'PERIODOS': pd.Series(periodo_analise),
    'META_PCD_50%': pd.Series(evolucao_pcd),
    'META_IMPACTO_150ANO': pd.Series(evolucao_impacto),
    })

In [ ]:
df_indicadores.sort_values(by=['GRUPO'], ascending=True).reset_index(drop=True)

## Conferência em detalhes

In [ ]:
inicio = 2021
final  = 2022
tipo   = 'artigos'
grupo  = 'permanentes'
lista_nomes_docentes = 'lista_docentes_permanentes.csv'
# lista_nomes_docentes = 'lista_docentes_colaboradores.csv'

df_public, df_impacto_docente, df_impacto_discente, df_docentespcd, indicador_pcd, indicador_impacto = avaliar_completo(inicio, final, tipo, grupo, lista_nomes_docentes)

In [ ]:
# df_impacto_docente[:60]

## Conferência dos achados de nomes de discentes

In [ ]:
def mostrar_partes_achadas(lista_discentes, lista_autores, verbose=False):
    partes_achadas=[]
    discentes_achados=[]
    erros=[]
    if verbose == True:
        print(f'{padronizar_titulo(lista_autores).lower()}')
    try:
        ## Buscar pelas partes de nomes de autor em cada linha de autores de artigo
        for nome in lista_discentes:
            sobrenome, partenome1, partenome2, partenome3 = quebrar_partesnomes(nome)
            if verbose == True:
                print(f'{sobrenome}, {partenome1} {partenome2} {partenome3}')
            strbusca_partes = compilar_partes(sobrenome, partenome1, partenome2, partenome3)
            try:
                achados_partes = re.search(strbusca_partes, padronizar_titulo(lista_autores).lower())
                if achados_partes.span() !=None:
                    partes_achadas.append(achados_partes.groups())
                    discentes_achados.append(nome)
            except Exception as e:
                # print(e)
                pass

        ## Buscar pelas iniciais de partes de nomes de autor, que seguem um sobrenome em cada linha de autores de artigo
        for nome in lista_discentes:
            sobrenome, inicial1, inicial2, inicial3 = quebrar_iniciais(nome)
            if verbose == True:
                print(f'{sobrenome}, {inicial1} {inicial2} {inicial3}')
            strbusca_iniciais = compilar_iniciais(sobrenome, inicial1, inicial2, inicial3)
            try:
                achados_iniciais = re.search(strbusca_iniciais, padronizar_titulo(lista_autores).lower())
                if achados_iniciais.span() !=None and achados_iniciais.groups() not in discentes_achados:
                    partes_achadas.append(achados_iniciais.groups())
                    discentes_achados.append(nome)
            except Exception as e:
                # print(e)
                pass
    except Exception as e:
        # print(f'Erro ao buscar partes de nome; {e}')
        print(e)
    
    return partes_achadas, discentes_achados

def listar_achados(docente):
    lista_csv = ler_artigostodosperiodos()
    lista_autores_artigos, lista_docentes, lista_orientadores, lista_discentes = montar_listas(lista_csv)

    df_filtrado = df_impacto_docente[(df_impacto_docente.DOCENTE==docente)]

    lista_indices = df_filtrado['INDICES_ARTIGOS'].values.tolist()[0]
    n=100
    print('-'*n)
    print(f'\nDocente: {docente} | {len(lista_indices)} Publicações identificadas para no período [{inicio} a {final}]')
    print()
    for indice in lista_indices:
        print('-'*n)
        print(f'Índice da publicação: {indice}')
        print(df_public.iloc[indice].values[:3])
        lista_autores = padronizar_titulo(df_public.iloc[indice].values[4])
        partes_achadas, discentes_achados = mostrar_partes_achadas(lista_discentes, lista_autores, verbose=False)
        print()
        print(lista_autores)
        print('\nPartes de nomes de alunos encontrados na lista de autores:')
        print(partes_achadas)
        print('\nNomes de alunos considerados como encontrados na lista de autores:')
        print(discentes_achados)

def separar_iniciais(nome):
    import re
    letras_duasconsnts = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{2}$')            # Duas Letras consoantes maiúsculas juntas do início ao final da string
    letras_tresconsnts = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{3}$')            # Três Letras consoantes maiúsculas juntas do início ao final da string
    letras_duasconsntsvirg = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{2},$')       # Duas Letras consoantes maiúsculas juntas do início ao final da string, seguidas de vírgula
    letras_tresconsntsvirg = re.compile(r'^[B-DF-HJ-NP-TV-XZ-r]{3},$')       # Três Letras consoantes maiúsculas juntas do início ao final da string, seguidas de vírgula
    partes_nome=[]
    for j in nome.split(' '):
        div_ltrduasconsnts = letras_duasconsnts.findall(j)
        div_ltrtriplicadas = letras_tresconsnts.findall(j)
        div_ltrduasconsntsvirg = letras_duasconsntsvirg.findall(j)
        div_ltrtresconsntsvirg = letras_tresconsntsvirg.findall(j)
        if div_ltrduasconsnts or div_ltrtriplicadas:
            iniciais_separadas = ' '.join(x for x in j)
            partes_nome.append(iniciais_separadas)
        elif div_ltrduasconsntsvirg or div_ltrtresconsntsvirg:
            iniciais_separadas = ' '.join(x for x in j[:-1])
            partes_nome.append(iniciais_separadas+',')
        else:
            partes_nome.append(j)
    nome_separado = ' '.join(x for x in partes_nome).strip()
    return nome_separado

In [ ]:
docente = 'Olindo Assis Martins Filho'
listar_achados(docente)

## Outras funcionalidades

    Formatar tempo (h:min:seg)

In [ ]:
def tempo(start, end):
    t=end-start

    tempo = timedelta(
        weeks   = t//(3600*24*7),
        days    = t//(3600*24),
        seconds = t,
        minutes = t//(60),
        hours   = t//(3600),
        microseconds=t//1000000,
        )
    fmt='{H:2}:{M:02}:{S:02}'
    return strfdelta(tempo)


def horas(segundos): 
    return time.strftime("%H:%M:%S", time.gmtime(segundos)) 


def dias_horas_minutos(td):
    x = (td.days, td.seconds//3600, (td.seconds//60)%60, td.seconds)
    return x #(days, hrs, mins, seconds)


def strfdelta(tdelta, fmt='{H:02}h {M:02}m {S:02}s', inputtype='timedelta'):
    """Convert a datetime.timedelta object or a regular number to a custom-formatted string, 
    just like the stftime() method does for datetime.datetime objects.

    The fmt argument allows custom formatting to be specified.  Fields can 
    include seconds, minutes, hours, days, and weeks.  Each field is optional.

    Some examples:
        '{D:02}d {H:02}h {M:02}m {S:02}s' --> '05d 08h 04m 02s' (default)
        '{W}w {D}d {H}:{M:02}:{S:02}'     --> '4w 5d 8:04:02'
        '{D:2}d {H:2}:{M:02}:{S:02}'      --> ' 5d  8:04:02'
        '{H}h {S}s'                       --> '72h 800s'

    The inputtype argument allows tdelta to be a regular number instead of the  
    default, which is a datetime.timedelta object.  Valid inputtype strings: 
        's', 'seconds', 
        'm', 'minutes', 
        'h', 'hours', 
        'd', 'days', 
        'w', 'weeks'
    """

    # Convert tdelta to integer seconds.
    if inputtype == 'timedelta':
        remainder = int(tdelta.total_seconds())
    elif inputtype in ['s', 'seconds']:
        remainder = int(tdelta)
    elif inputtype in ['m', 'minutes']:
        remainder = int(tdelta)*60
    elif inputtype in ['h', 'hours']:
        remainder = int(tdelta)*3600
    elif inputtype in ['d', 'days']:
        remainder = int(tdelta)*86400
    elif inputtype in ['w', 'weeks']:
        remainder = int(tdelta)*604800

    f = Formatter()
    desired_fields = [field_tuple[1] for field_tuple in f.parse(fmt)]
    possible_fields = ('W', 'D', 'H', 'M', 'S')
    constants = {'W': 604800, 'D': 86400, 'H': 3600, 'M': 60, 'S': 1}
    values = {}
    
    for field in possible_fields:
        if field in desired_fields and field in constants:
            values[field], remainder = divmod(remainder, constants[field])
    
    return f.format(fmt, **values)


# print (timedelta(days=365, hours=8, minutes=15))
# print ("   Hoje é: " + str(date.today()))
# print ("Agora são: " + str(datetime.now()))
# print ("Um ano no futuro estaremos em:" + str(dt.today() + timedelta(days=365)))
# hoje = date.today()
# print(hoje)
# hora = dt.now()
# print(hora)
# dias_ano = date(hoje.year, 1, 1)
# if dias_ano < hoje:
#     print ("Decoridos %d dias do ano" % ((hoje - dias_ano).days))
    
# from datetime import datetime
# now= datetime.now() #get the current date and time

# #%c - local date and time, %x-local's date, %X- local's time
# print(now.strftime("%c"))
# print(now.strftime("%x"))
# print(now.strftime("%X"))

# ##### Time Formatting ####
# #%I/%H - 12/24 Hour, %M - minute, %S - second, %p - local's AM/PM
# print(now.strftime("%I:%M:%S %p")) # 12-Hour:Minute:Second:AM
# print(now.strftime("%H:%M")) # 24-Hour:Minute

In [ ]:
# import logging
# from neo4j import GraphDatabase
# from neo4j.exceptions import Neo4jError

# logging.basicConfig(level=logging.INFO, format='%(asctime)s %(levelname)s: %(message)s', filename='logs/persister.log')
# logger = logging.getLogger(__name__)

# class Neo4jPersister:
#     def __init__(self, uri, user, password):
#         self._uri = uri
#         self._user = user
#         self._password = password
#         self._driver = GraphDatabase.driver(self._uri, auth=(self._user, self._password))
#         self.logger = logger

#         # Devem ser persistidos como 
#         self.tipos = [
#             'Identificação',
#             'Idiomas',
#             'Formação',
#             'Atuação Profissional',
#             'Linhas de Pesquisa',
#             'Áreas',
#             'Produções',
#             'ProjetosPesquisa',
#             'ProjetosExtensão',
#             'ProjetosDesenvolvimento',
#             'ProjetosOutros',
#             'Bancas',
#             'Orientações',
#             ]

#         self.subtipos= [
#             'Acadêmica',
#             'Pos-Doc',
#             'Complementar',
#             'Artigos completos publicados em periódicos',
#             'Resumos publicados em anais de congressos',
#             'Apresentações de Trabalho',
#             'Outras produções bibliográficas',
#             'Entrevistas, mesas redondas, programas e comentários na mídia',
#             'Concurso público',
#             'Outras participações',
#             'Livros publicados/organizados ou edições',
#             'Capítulos de livros publicados',
#             'Resumos expandidos publicados em anais de congressos',
#             'Resumos publicados em anais de congressos (artigos)',
#             'Trabalhos técnicos',
#             'Demais trabalhos',
#             'Mestrado',
#             'Teses de doutorado',
#             'Qualificações de Doutorado',
#             'Qualificações de Mestrado',
#             'Monografias de cursos de aperfeiçoamento/especialização',
#             'Trabalhos de conclusão de curso de graduação',
#             'Orientações e supervisões concluídas',
#             'Citações',
#             'Trabalhos completos publicados em anais de congressos',
#             'Produtos tecnológicos',
#             'Artigos  aceitos para publicação',
#             'Assessoria e consultoria',
#             'Programas de computador sem registro',
#             'Professor titular',
#             'Avaliação de cursos',
#             'Orientações e supervisões em andamento',
#             'Processos ou técnicas',
#             'Outras produções artísticas/culturais',
#             'Textos em jornais de notícias/revistas',
#             'Redes sociais, websites e blogs',
#             'Artes Visuais'            
#             ]

#         self.propriedades = [
#             'Nome',
#             'ID Lattes',
#             'Última atualização',
#             ]
       
#     def close(self):
#         self._driver.close()
    
#     def persistir_revistas_da_planilha(self):
#         """
#         Persiste dados de revistas a partir da planilha 'classificações_publicadas_todas_as_areas_avaliacao1672761192111.xlsx' no Neo4j.

#         Args:
#             session: Objeto de sessão do Neo4j.
#         """
#         # Leitura da planilha
#         dados_qualis = pd.read_excel(os.path.join(LattesScraper.find_repo_root(),'_data','in_xls','classificações_publicadas_todas_as_areas_avaliacao1672761192111.xlsx'))

#         # Extração e persistência de dados de revista
#         with self._driver.session() as session:
#             for index, row in dados_qualis.iterrows():
#                 issn = row['ISSN'].replace('-','')
#                 nome_revista = row['Título']
#                 area_avaliacao = row['Área de Avaliação']
#                 estrato = row['Estrato']

#                 # Verificação de existência da revista
#                 revista_node = session.run("""
#                     MATCH (j:Revista {issn: $issn})
#                     RETURN j
#                 """, issn=issn).single()

#                 if not revista_node:
#                     # Criação da revista se não existir
#                     session.run("""
#                         CREATE (j:Revista {issn: $issn, nome_revista: $nome_revista, area_avaliacao: $area_avaliacao, estrato: $estrato})
#                     """, nome_revista=nome_revista, issn=issn, area_avaliacao=area_avaliacao,  estrato=estrato)

#     # Testes Ok! 
#     def persist_pessoa_nodes(self, dict_list):
#         query_pessoa = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         ON CREATE SET p.nome = $nome, p.ultima_atualizacao = $ultima_atualizacao
#         ON MATCH SET p.nome = $nome, p.ultima_atualizacao = $ultima_atualizacao
#         """
#         try:
#             with self._driver.session() as session:
#                 for item in dict_list:
#                     identificacao = item.get('Identificação')
#                     nome = identificacao.get('Nome')
#                     id_lattes = identificacao.get('ID Lattes')
#                     ultima_atualizacao = identificacao.get('Última atualização')
#                     if nome:
#                         session.run(query_pessoa, id_lattes=id_lattes, nome=nome, ultima_atualizacao=ultima_atualizacao)
#         except Exception as e:
#             self.logger.error('Erro ao criar node "Pesquisador": {}'.format(e))

#     # Testes Ok!         
#     def persist_pesquisador_grande_area_relationships(self, dict_list):
#         query_rel_pessoa_grande_area = """
#         MATCH (p:Pesquisador {id_lattes: $id_lattes})
#         MATCH (ga:GrandeArea {nome: $grande_area_nome})
#         MERGE (p)-[:ATUA_EM]->(ga)
#         """

#         with self._driver.session() as session:
#             for item in dict_list:
#                 identificacao = item.get('Identificação')
#                 id_lattes = identificacao.get('ID Lattes')
#                 areas = item.get('Áreas').values()
#                 for area_string in areas:
#                     grande_area_nome, _, _ = self.extract_area_info(area_string)
#                     if grande_area_nome:
#                         session.run(query_rel_pessoa_grande_area, id_lattes=id_lattes, grande_area_nome=grande_area_nome)

#     # Testes Ok! 
#     def persist_areas_nodes(self, dict_list):
#         query_grande_area = """
#         MERGE (ga:GrandeArea {nome: $nome})
#         """
#         query_area = """
#         MATCH (ga:GrandeArea {nome: $grande_area_nome})
#         MERGE (a:Area {nome: $nome}) ON CREATE SET a:Area
#         MERGE (ga)-[:CONTEM]->(a)
#         """
#         query_subarea = """
#         MATCH (a:Area {nome: $area_nome})
#         MERGE (sa:Subarea {nome: $nome}) ON CREATE SET sa:Subarea
#         MERGE (a)-[:CONTEM]->(sa)
#         """
#         query_rel_pessoa_grande_area = """
#         MATCH (p:Pesquisador {id_lattes: $id_lattes})
#         MATCH (ga:GrandeArea {nome: $grande_area_nome})
#         MERGE (p)-[:ATUA_EM]->(ga)    
#         """

#         with self._driver.session() as session:
#             for item in dict_list:
#                 areas = item.get('Áreas').values()
#                 for area_string in areas:
#                     grande_area_nome, area_nome, subarea_nome = self.extract_area_info(area_string)
                    
#                     # Verificar se o nome não está vazio
#                     if grande_area_nome:
#                         session.run(query_grande_area, nome=grande_area_nome)
#                     if area_nome:
#                         session.run(query_area, grande_area_nome=grande_area_nome, nome=area_nome)
#                     if subarea_nome:
#                         session.run(query_subarea, area_nome=area_nome, nome=subarea_nome)
                    
#                     # Adicionar relacionamento Pesquisador - GrandeÁrea
#                     id_lattes = item['Identificação']['ID Lattes']
#                     if grande_area_nome:
#                         session.run(query_rel_pessoa_grande_area, id_lattes=id_lattes, grande_area_nome=grande_area_nome)

#     # Testes Ok! 
#     @staticmethod
#     def extract_area_info(area_string):
#         # Extraindo os nomes de GrandeÁrea, Área e Subárea da string
#         try:
#             grande_area_nome = area_string.split('/')[0].strip().split(': ')[1]
#         except:
#             grande_area_nome = ''
#         try:
#             area_nome = area_string.split('/')[1].strip().split(': ')[1]
#         except:
#             area_nome = ''
#         try:
#             subarea_nome = area_string.split('/')[2].strip().split(': ')[1]
#         except:
#             subarea_nome = ''
#         return grande_area_nome, area_nome, subarea_nome

#     ## PRODUÇÕES
#     def persist_producoes_pesquisador(self, dict_list):
#         with self._driver.session() as session:
#             for pesq in dict_list:
#                 identificacao = pesq.get('Identificação')
#                 id_lattes = identificacao.get('ID Lattes')
#                 producoes = pesq.get('Produções')

#                 if not isinstance(producoes, dict):
#                     print(f"Erro!! Dicionário da seção 'Produções' não encontrado para {id_lattes}")
#                     continue

#                 for chave_producao, valores_producao in producoes.items():
#                     print(f'{chave_producao} | {valores_producao}')
#                     if chave_producao == 'Artigos completos publicados em periódicos':
#                         # self.persistir_artigos_completos(session, id_lattes, valores_producao)
#                         self.persistir_artigos_revistas(session, id_lattes, valores_producao)

#     def _get_or_create_node(self, session, label, properties):
#         properties = [x.rstrip('.') for x in properties]
#         node = session.run("MATCH (n: {label}) WHERE {properties} RETURN n", {"label": label, "properties": properties}).single()

#         if not node:
#             node = session.run("CREATE (n: {label} {properties}) RETURN n", {"label": label, "properties": properties}).single()["n"]
#             self._node_created_count += 1

#         return node

#     def persist_tipo_producao(self, session, id_lattes, tipo_producao):
#         query_create_node = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         MERGE (t:TipoProducao {nome: $tipo_producao})
#         MERGE (p)-[:PRODUZ]->(t)
#         """
#         result = session.run(query_create_node, id_lattes=id_lattes, tipo_producao=tipo_producao)
#         summary = result.consume()
#         return summary.counters.nodes_created, summary.counters.nodes_deleted, summary.counters.relationships_created, summary.counters.relationships_deleted

#     def persist_subtipo_producao(self, session, id_lattes, tipo_producao, subtipo_producao, dados_producao):
#         def checar_e_serializar(dados):
#             """ Verifica e serializa dicionários recursivamente """
#             if isinstance(dados, dict):
#                 for chave, valor in dados.items():
#                     if isinstance(valor, dict):
#                         dados[chave] = json.dumps(valor)
#                     # Checagem adicional para outros tipos inválidos, se necessário
#             return dados
#         # Serialização recursiva do dicionário
#         dados_producao = checar_e_serializar(dados_producao)

#         query_create_node = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         MERGE (t:TipoProducao {nome: $tipo_producao})
#         MERGE (s:SubtipoProducao {nome: $subtipo_producao})
#         MERGE (p)-[PRODUZ:]->(t)-[:DO_TIPO]->(s)
#         """

#         if subtipo_producao in ["ArtigoCompleto", "ResumoCongresso", "ApresentacaoTrabalho", "OutrasProducoesBibliograficas"]:
#             query_create_node += """
#             MERGE (o:Ocorrencia {tipo: $subtipo_producao, dados: $dados})
#             MERGE (s)-[:OCORRENCIA]->(o)
#             """

#         result = session.run(query_create_node, id_lattes=id_lattes, tipo_producao=tipo_producao, 
#                             subtipo_producao=subtipo_producao, dados=dados_producao)

#         # Obtendo as informações de contadores
#         summary = result.consume()

#         return summary.counters.nodes_created, summary.counters.nodes_deleted, summary.counters.relationships_created, summary.counters.relationships_deleted

#     def persistir_artigos_completos(self, session, id_lattes, dados):
#         created_nodes = 0
#         updated_nodes = 0
#         created_relations = 0
#         updated_relations = 0
        
#         for dados_artigo in dados:
#             dados_artigo['dados'] = json.dumps(dados_artigo)  # Conversão para JSON da estrutura completa
#             query_create_node_artigo = """
#                 MERGE (p:Pesquisador {id_lattes: $id_lattes})
#                 CREATE (a:ArtigoPublicado {
#                     ano: $ano,
#                     fator_impacto_jcr: $fator_impacto_jcr,
#                     ISSN: $ISSN,
#                     titulo: $titulo,
#                     revista: $revista,
#                     autores: $autores,
#                     Qualis: $Qualis,
#                     DOI: $DOI,
#                     dados: $dados_artigo
#                 })
#                 CREATE (p)-[:PRODUZ]->(a)

#                 MERGE (j:Revista {nome: $revista, issn: $ISSN})
#                 CREATE (a)-[:PUBLICADO_EM]->(j)
#             """

#             result_artigo = session.run(query_create_node_artigo, 
#                                 id_lattes=id_lattes, 
#                                 ano=dados_artigo['ano'],
#                                 fator_impacto_jcr=dados_artigo['fator_impacto_jcr'],
#                                 ISSN=dados_artigo['ISSN'],
#                                 titulo=dados_artigo['titulo'],
#                                 revista=dados_artigo['revista'],
#                                 autores=dados_artigo['autores'],
#                                 Qualis=dados_artigo['Qualis'],
#                                 DOI=dados_artigo['DOI'],
#                                 dados_artigo=dados_artigo
#                                 )
#             summary_artigo = result_artigo.consume()
#             created_nodes += summary_artigo.counters.nodes_created
#             updated_nodes += summary_artigo.counters.nodes_deleted
#             created_relations += summary_artigo.counters.relationships_created
#             updated_relations += summary_artigo.counters.relationships_deleted

#         return created_nodes, updated_nodes, created_relations, updated_relations


#     def persistir_artigos_completos(self, session, id_lattes, dados):
#         created_nodes = 0
#         updated_nodes = 0
#         created_relations = 0
#         updated_relations = 0
                
#         for dados_artigo in dados:
#             ano = dados_artigo['ano']
#             impact_jcr = dados_artigo['fator_impacto_jcr']
#             issn = dados_artigo['ISSN']
#             titulo = dados_artigo['titulo']
#             revista = dados_artigo['revista']
#             autores = dados_artigo['autores']
#             qualis = dados_artigo['Qualis']
#             doi = dados_artigo['DOI']

#             query_create_node_artigo = """
#                 MERGE (p:Pesquisador {id_lattes: $id_lattes})
#                 CREATE (a:ArtigoPublicado {ano: $ano, impact_jcr: $impact_jcr, issn: $issn, titulo: $titulo, revista: $revista, autores: $autores, qualis: $qualis, doi: $doi})
#                 CREATE (p)-[:PRODUZ]->(a)
#                 MERGE (j:Revista {nome: $revista, issn: $issn})
#                 CREATE (a)-[:PUBLICADO_EM]->(j)
#             """
#             print(query_create_node_artigo)
#             result_artigo = session.run(query_create_node_artigo, 
#                                 id_lattes=id_lattes, 
#                                 ano=ano,
#                                 impact_jcr=impact_jcr,
#                                 issn=issn,
#                                 titulo=titulo,
#                                 revista=revista,
#                                 autores=autores,
#                                 qualis=qualis,
#                                 doi=doi,
#                                 )
#             summary_artigo = result_artigo.consume()
#             created_nodes += summary_artigo.counters.nodes_created
#             updated_nodes += summary_artigo.counters.nodes_deleted
#             created_relations += summary_artigo.counters.relationships_created
#             updated_relations += summary_artigo.counters.relationships_deleted

#         return created_nodes, updated_nodes, created_relations, updated_relations

#     def buscar_revista_por_issn(self, session, issn):
#         query = """
#             MATCH (revista:Revista {issn: $issn})
#             RETURN revista
#         """

#         try:
#             result = session.run(query, issn=issn)
#             return result.single()
#         except Neo4jError as e:
#             print(f"Erro Neo4j ao buscar a revista por ISSN: {e}")
#             return None
        
#     def persistir_artigos_revistas(self, session, id_lattes, dados):
#         """
#         Função para persistir os dados de artigos completos publicados em periódicos.

#         Args:
#             session (neo4j.Session): Sessão Neo4j.
#             id_lattes (str): ID do Lattes do pesquisador.
#             dados (dict): Dicionário contendo os dados dos artigos.

#         Returns:
#             None
#         """

#         for artigo in dados:
#             # Extraindo informações do artigo
#             revista_nome  = ''
#             created_nodes = ''
#             ano = artigo['ano']
#             impact_jcr = artigo['fator_impacto_jcr']
#             issn = artigo['ISSN']
#             titulo = artigo['titulo']
#             revista = artigo['revista']
#             autores = artigo['autores']
#             data_issn = artigo['data_issn']
#             doi = artigo['DOI']
#             qualis = artigo['Qualis']

#             query_create_node_artigo = """
#                 MERGE (p:Pesquisador {id_lattes: $id_lattes})
#                 CREATE (a:ArtigoPublicado {ano: $ano, impact_jcr: $impact_jcr, issn: $issn, titulo: $titulo, revista: $revista, autores: $autores, qualis: $qualis, doi: $doi})
#                 CREATE (p)-[:PRODUZ]->(a)
#                 MERGE (j:Revista {nome: $revista, issn: $issn})
#                 CREATE (a)-[:PUBLICADO_EM]->(j)
#             """
            
#             # Buscando o nó da revista
#             revista_node = self.buscar_revista_por_issn(session, issn)

#             # Criando o nó do artigo
#             with session.begin_transaction() as tx:
#                 tx.run(query_create_node_artigo,
#                     id_lattes=id_lattes,
#                     ano=ano,
#                     impact_jcr=impact_jcr,
#                     issn=issn,
#                     titulo=titulo,
#                     revista=revista,
#                     autores=autores,
#                     data_issn=data_issn,
#                     doi=doi,
#                     qualis=qualis
#                     )

#                 # Criando o relacionamento PUBLICADO_EM
#                 if revista_node is not None:
#                     node_revista = revista_node[0][1]
#                     if node_revista is not None:
#                         revista_nome = node_revista['nome_revista']
#                         revista_issn = node_revista['issn']
#                         revista_area_avaliacao = node_revista['area_avaliacao']
#                         revista_estrato = node_revista['estrato']

#                     if revista_nome:
#                         tx.run("""
#                             MATCH (a:ArtigoPublicado {doi: $doi}), (j:Revista {nome_revista: $revista_nome, issn: $revista_issn, area_avaliacao: $revista_area_avaliacao, estrato: $revista_estrato})
#                             CREATE (a)-[:PUBLICADO_EM]->(j)
#                         """, doi=doi, revista_nome=revista_nome, revista_issn=revista_issn, revista_area_avaliacao=revista_area_avaliacao, revista_estrato=revista_estrato)

#                     else:
#                         print("Erro: O nó da revista não foi encontrado para o ISSN", issn)
#                         # Lógica de tratamento de erro (opcional)
#                 else:
#                     print("Erro: O retorno para a revista com ISSN", issn, "é None.")

#                 tx.commit()

#         # Atualização dos contadores
#         with session.begin_transaction() as tx:
#             created_nodes += tx.run("MATCH (n) WHERE n:ArtigoPublicado RETURN count(n)").single()[0]
#             updated_nodes += tx.run("MATCH (n) WHERE n:ArtigoPublicado SET n.updated_at = datetime() RETURN count(n)").single()[0]
#             created_relations += tx.run("MATCH (r) WHERE r:PUBLICADO_EM RETURN count(r)").single()[0]

#     def persistir_resumos_congressos(self, session, id_lattes, dados):
#         query_create_node = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         MERGE (r:ResumoCongresso {titulo: $titulo, ano: $ano, evento: $evento, autores: $autores, data_issn: $data_issn, doi: $doi})
#         MERGE (p)-[:PRODUZ]->(r)
#         """
#         result = session.run(query_create_node, id_lattes=id_lattes, **dados)
#         # Obtendo as informações de contadores
#         summary = result.consume()
#         created_nodes = summary.counters.nodes_created
#         updated_nodes = summary.counters.nodes_deleted  
#         created_relations = summary.counters.relationships_created
#         updated_relations = summary.counters.relationships_deleted 

#         return created_nodes, updated_nodes, created_relations, updated_relations

#     def persistir_apresentacoes_trabalho(self, session, id_lattes, dados):
#         query_create_node = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         MERGE (a:ApresentacaoTrabalho {
#             titulo: $titulo,
#             ano: $ano,
#             evento: $evento,
#             autores: $autores
#         })
#         MERGE (p)-[:PRODUZ]->(a)
#         """
#         result = session.run(query_create_node, id_lattes=id_lattes, **dados)

#         # Obtendo as informações de contadores
#         summary = result.consume()
#         created_nodes = summary.counters.nodes_created
#         updated_nodes = summary.counters.nodes_deleted  
#         created_relations = summary.counters.relationships_created
#         updated_relations = summary.counters.relationships_deleted 

#         return created_nodes, updated_nodes, created_relations, updated_relations

#     def persistir_outras_producoes_bibliograficas(self, session, id_lattes, dados):
#         query_create_node = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         MERGE (o:OutrasProducoesBibliograficas {
#             titulo: $titulo,
#             ano: $ano,
#             autores: $autores,
#             doi: $doi
#         })
#         MERGE (p)-[:PRODUZ]->(o)
#         """
#         result = session.run(query_create_node, id_lattes=id_lattes, **dados)

#         # Obtendo as informações de contadores
#         summary = result.consume()
#         created_nodes = summary.counters.nodes_created
#         updated_nodes = summary.counters.nodes_deleted  
#         created_relations = summary.counters.relationships_created
#         updated_relations = summary.counters.relationships_deleted 

#         return created_nodes, updated_nodes, created_relations, updated_relations

#     def persistir_orientacoes_concluidas(self, session, id_lattes, dados):
#         query_create_node = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         MERGE (o:OrientacaoConcluida {
#             tipo: $tipo,
#             titulo: $titulo,
#             ano: $ano,
#             autor: $autor,
#             instituicao: $instituicao
#         })
#         MERGE (p)-[:ORIENTA]->(o)
#         """
#         result = session.run(query_create_node, id_lattes=id_lattes, **dados)

#         # Obtendo as informações de contadores
#         summary = result.consume()
#         created_nodes = summary.counters.nodes_created
#         updated_nodes = summary.counters.nodes_deleted  
#         created_relations = summary.counters.relationships_created
#         updated_relations = summary.counters.relationships_deleted 

#         return created_nodes, updated_nodes, created_relations, updated_relations

#     def persistir_participacoes_bancas(self, session, id_lattes, dados):
#         query_create_node = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         MERGE (b:Banca {
#             tipo: $tipo,
#             titulo: $titulo,
#             ano: $ano,
#             instituicao: $instituicao
#         })
#         MERGE (p)-[:PARTICIPA_BANCA]->(b)
#         """
#         result = session.run(query_create_node, id_lattes=id_lattes, **dados)

#         # Obtendo as informações de contadores
#         summary = result.consume()
#         created_nodes = summary.counters.nodes_created
#         updated_nodes = summary.counters.nodes_deleted  
#         created_relations = summary.counters.relationships_created
#         updated_relations = summary.counters.relationships_deleted 

#         return created_nodes, updated_nodes, created_relations, updated_relations

#     def persistir_projetos_pesquisa(self, session, id_lattes, dados):
#         query_create_node = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         MERGE (pr:ProjetoPesquisa {
#             titulo: $titulo,
#             ano_inicio: $ano_inicio,
#             ano_fim: $ano_fim,
#             agencia_financiadora: $agencia_financiadora,
#             valor_financiamento: $valor_financiamento
#         })
#         MERGE (p)-[:COORDENA]->(pr)
#         """
#         result = session.run(query_create_node, id_lattes=id_lattes, dados=dados)

#         # Obtendo as informações de contadores
#         summary = result.consume()
#         created_nodes = summary.counters.nodes_created
#         updated_nodes = summary.counters.nodes_deleted  
#         created_relations = summary.counters.relationships_created
#         updated_relations = summary.counters.relationships_deleted 

#         return created_nodes, updated_nodes, created_relations, updated_relations

#     def persistir_premios_distincoes(self, session, id_lattes, dados):
#         query_create_node = """
#         MERGE (p:Pesquisador {id_lattes: $id_lattes})
#         MERGE (pd:PremioDistincao {
#             titulo: $titulo,
#             ano: $ano,
#             instituicao: $instituicao,
#         })
#         MERGE (p)-[:RECEBE]->(pd)
#         """
#         result = session.run(query_create_node, id_lattes=id_lattes, **dados)

#         # Obtendo as informações de contadores
#         summary = result.consume()
#         created_nodes = summary.counters.nodes_created
#         updated_nodes = summary.counters.nodes_deleted  
#         created_relations = summary.counters.relationships_created
#         updated_relations = summary.counters.relationships_deleted 

#         return created_nodes, updated_nodes, created_relations, updated_relations

# uri = "bolt://localhost:7687"
# user = "neo4j"
# password = "password"
# persister = Neo4jPersister(uri, user, password)


    # def run(self, query, **parameters):
    #     with self.driver.session() as session:
    #         return session.run(query, **parameters)

    ## Agrupando nós de artigos por revista
    # def persistir_artigos_revistas(self, session, id_lattes, dados):
    #     created_nodes = 0
    #     updated_nodes = 0
    #     created_relations = 0
    #     updated_relations = 0

    #     for dados_artigo in dados:
    #         ano = dados_artigo['ano']
    #         impact_jcr = dados_artigo['fator_impacto_jcr']
    #         issn = dados_artigo['ISSN']
    #         titulo = dados_artigo['titulo']
    #         revista = dados_artigo['revista']
    #         autores = dados_artigo['autores']
    #         qualis = dados_artigo['Qualis']
    #         doi = dados_artigo['DOI']
            
    #         query_create_node_artigo = """
    #             MERGE (p:Pesquisador {id_lattes: $id_lattes})
    #             CREATE (a:ArtigoPublicado {ano: $ano, impact_jcr: $impact_jcr, issn: $issn, titulo: $titulo, revista: $revista, autores: $autores, qualis: $qualis, doi: $doi})
    #             CREATE (p)-[:PRODUZ]->(a)
    #             MERGE (j:Revista {nome: $revista, issn: $issn})
    #             CREATE (a)-[:PUBLICADO_EM]->(j)
    #         """

    #         with session.begin_transaction() as tx:
    #             print("DEBUG: ISSN da revista:", issn)
    #             # Verificação de existência da revista
    #             revista_node = tx.run("""
    #                 MATCH (j:Revista {issn: $issn})
    #                 RETURN j
    #             """, issn=issn).single()

    #             if not revista_node:
    #                 # Revista não encontrada, crie-a
    #                 tx.run("""
    #                     CREATE (j:Revista {nome: $revista, issn: $issn})
    #                 """, revista=revista, issn=issn)

    #                 revista_node = tx.run("""
    #                     MATCH (j:Revista {issn: $issn})
    #                     RETURN j
    #                 """, issn=issn).single()

    #             if revista_node is not None:
    #                 print("DEBUG: Propriedades do nó Revista:", revista_node.items())  
    #                 node_revista = revista_node[0]  # Extrair o objeto Node
    #                 print(f"revista_node[0] {node_revista}")
    #                 issn = node_revista['issn']  # Acessar a propriedade 'issn'
    #                 print(f"node_revista['issn'] {issn}")
    #                 revista_nome = node_revista['nome_revista']
    #                 revista_area_avaliacao = node_revista['area_avaliacao']
    #                 revista_estrato = node_revista['estrato']
    #             else:
    #                 print("Erro: O retorno para a revista com ISSN", issn, "é None.")

    #             # Criação do nó do artigo
    #             tx.run(query_create_node_artigo, 
    #                 id_lattes=id_lattes, 
    #                 ano=ano,
    #                 impact_jcr=impact_jcr,
    #                 issn=issn,
    #                 titulo=titulo,
    #                 revista=revista,
    #                 autores=autores,
    #                 qualis=qualis,
    #                 doi=doi)

    #             # Criação do relacionamento PUBLICADO_EM
    #             tx.run("""
    #                 MATCH (a:ArtigoPublicado {doi: $doi}), (j:Revista {nome_revista: $revista_nome, issn: $issn, area_avaliacao: $revista_area_avaliacao, estrato: $revista_estrato})
    #                 CREATE (a)-[:PUBLICADO_EM]->(j)
    #             """, doi=doi, revista_nome=revista_nome, issn=issn, revista_area_avaliacao=revista_area_avaliacao, revista_estrato=revista_estrato)

    #             tx.commit()

    #         # Atualização dos contadores
    #         created_nodes += tx.run("MATCH (n) WHERE n:ArtigoPublicado RETURN count(n)").single()[0]
    #         updated_nodes += tx.run("MATCH (n) WHERE n:ArtigoPublicado SET n.updated_at = datetime() RETURN count(n)").single()[0]
    #         created_relations += tx.run("MATCH (r) WHERE r:PUBLICADO_EM RETURN count(r)").single()[0]
    #         updated_relations += tx.run("MATCH (r) WHERE r:PUBLICADO_EM SET r.updated_at = datetime() RETURN count(r)").single()[0]

    #     return created_nodes, updated_nodes, created_relations, updated_relations

In [ ]:
# import json
# import logging

# from neo4j import GraphDatabase

# class Neo4jDataPersister:
#     def __init__(self, uri, user, password):
#         self._uri = uri
#         self._user = user
#         self._password = password
#         self._driver = GraphDatabase.driver(self._uri, auth=(self._user, self._password))
#         self.logger = logging.getLogger(__name__)

#         self._node_created_count = 0
#         self._node_updated_count = 0
#         self._node_deleted_count = 0

#         self._relationship_created_count = 0
#         self._relationship_updated_count = 0
#         self._relationship_deleted_count = 0

#     def close(self):
#         self._driver.close()

#     def persist_data_from_json(self, json_data):
#         with self._driver.session() as session:
#             self._persist_data(session, json_data)

#         self.logger.info("Total nodes created: %d", self._node_created_count)
#         self.logger.info("Total nodes updated: %d", self._node_updated_count)
#         self.logger.info("Total nodes deleted: %d", self._node_deleted_count)

#         self.logger.info("Total relationships created: %d", self._relationship_created_count)
#         self.logger.info("Total relationships updated: %d", self._relationship_updated_count)
#         self.logger.info("Total relationships deleted: %d", self._relationship_deleted_count)

#     def _persist_data(self, session, data):
#         if isinstance(data, dict):  # Check if it's a dictionary
#             for key, value in data.items():
#                 if key == 'Identificação':
#                     self._handle_identificacao(session, value)
#                 elif key == 'Atuação Profissional':
#                     self._handle_atuacao_profissional(session, value)
#                 elif key == 'Atuação Profissional':
#                     self._handle_atuacao_profissional(session, value)                    
#                 elif key == 'Produções':
#                     self._handle_producoes(session, value)
#                 elif isinstance(value, list) and not value:
#                     # Ignore empty lists
#                     pass
#                 elif isinstance(value, dict):
#                     if 'JCR2' in value:
#                         # Ignore the 'JCR2' subdictionary
#                         del value['JCR2']

#                     self._persist_data(session, value)

#         elif isinstance(data, list):  # Check if it's a list
#             for item in data:
#                 self._persist_data(session, item)  # Recurse on list items

#         else:
#             # Handle other data types (strings, numbers, etc.) or raise an error
#             self.logger.warning("Unexpected data type: %s", type(data))


#     def _handle_identificacao(self, session, data):
#         for item in data:
#             if item['campo'] == 'ID Lattes':
#                 node_id = item['valor']
#                 node = self._get_or_create_node(session, 'Pesquisador', {'ID Lattes': node_id})
#                 self._persist_other_properties(session, node, data)
#             else:
#                 node = self._get_or_create_node(session, 'Pesquisador', {data.items()})

#     def _handle_atuacao_profissional(self, session, data):
#         for item in data:
#             node = self._create_node(session, 'AtuaçãoProfissional', item)

#     def _handle_producoes(self, session, data):
#         for production_type, production_data in data.items():
#             if production_type == 'Artigos completos publicados em periódicos':
#                 for article in production_data:
#                     node = self._create_node(session, production_type, article)
#             elif production_type.startswith('1.'):
#                 for index, article in enumerate(production_data):
#                     node = self._create_node(session, production_type, article)
#                     node['OrdemCronológica'] = index + 1

#     def _get_or_create_node(self, session, label, properties):
#         node = session.run("MATCH (n: {label}) WHERE {properties} RETURN n", {"label": label, "properties": properties}).single()

#         if not node:
#             node = session.run("CREATE (n: {label} {properties}) RETURN n", {"label": label, "properties": properties}).single()["n"]
#             self._node_created_count += 1

#         return node

#     def _create_node(self, session, label, properties):
#         node = session.run("CREATE (n: {label} {properties}) RETURN n", {"label": label, "properties": properties}).single()["n"]
#         self._node_created_count += 1

#         return node

#     def _persist_other_properties(self, session, node, data):
#         for key, value in data.items():
#             if key not in ['campo', 'valor']:
#                 node[key] = value  

#     def _create_relationship(self, session, start_node, relationship_type, end_node, properties={}):
#         session.run("MATCH (a), (b) WHERE ID(a) = {start_node_id} AND ID(b) = {end_node_id} CREATE (a)-[r:{type} {props}]->(b) RETURN r", 
#                     {"start_node_id": id(start_node), "end_node_id": id(end_node), "type": relationship_type, "props": properties})
#         self._relationship_created_count += 1


In [ ]:
# tipos=[]
# subtipos=[]
# for dict_pesq in dict_list:
#     # Avaliando elementos da lista de dicionários do arquivo JSON de entrada
#     if isinstance(dict_pesq, dict):
#         for key1,val1 in dict_pesq.items():
#             if key1 not in tipos:
#                 tipos.append(key1)            
#             print(f'N01: Elementos armazenados em dicionário:')
#             print(f'     {key2:25} | Tipo dos valores: {type(val2)}')
#             print(f'       Conteúdo disponível nos valores do dicionário de Nível 01:')
#             # Avaliando filhos de primeiro nível na hierarquia (Seções)
#             if isinstance(val1, list):
#                 print(f'N01: Elementos armazenados em lista:')
#                 print(f'     Conteúdo disponível nos valores:')
#                 print(f'       {[x for x in val1]}')
#             elif isinstance(val1, dict):
#                 for key2,val2 in val1.items():
#                     if key2 not in subtipos:
#                         subtipos.append(key2)
#                     print(f'       Chave: {key2:25} | Tipo dos valores: {type(val2)}')
#                     print(f'         Conteúdo disponível nos valores do dicionário de Nível 02:')
#                     # Avaliando filhos de segundo nível na hierarquia (Tipos de Seções)
#                     if isinstance(val2, dict):
#                         for key3,val3 in val2.items():
#                             if key3 not in tipos:
#                                 print(f'         Chave: {key3:25} | Tipo dos valores: {type(val3)}')
#                                 print(f'          Conteúdo disponível nos valores do dicionário de Nível 03:')
#                                 # Avaliando filhos de terceiro nível na hierarquia (Ocorrências de Tipos de Seções)
#                                 if isinstance(val3, dict):
#                                     print(f'               Chave: {key3:25} | Tipo dos valores: {type(val3)}')
#                                     print(f'                 Conteúdo disponível nos valores do dicionário de Nível 04:')
#                                     # print(val3)
#             else:
#                 print(f'N01: Elementos armazenados em {type(val1)}')
#     else:
#         print('ERRO NA ESTRUTURA DO JSON!!')

In [ ]:
# # Create a Neo4jDataPersister instance
# data_persister = Neo4jDataPersister('neo4j://localhost:7687', 'neo4j', 'password')
# filename = 'dict_list.json'
# json_data, formatted_creation_date, formatted_modification_date, time_count, unit = jfm.load_from_json(os.path.join(folder_data_input,filename))
# print(f"\n{len(dict_list)} currículos carregados na lista de dicionários '{filename}'")

# # Persist the data to Neo4j
# data_persister.persist_data_from_json(json_data)

In [ ]:
# for pesq in json_data:
#     print(len(pesq.get('Produções').keys()))

In [ ]:
# class ProjectsHandler:

#     def __init__(self, uri, user, password):
#         self._driver = GraphDatabase.driver(uri, auth=(user, password))

#     def close(self):
#         self._driver.close()

#     def consult_data_by_property(self, name, property_name):
#         with self._driver.session() as session:
#             result = session.run(f"MATCH (p:Person {{name: $name}}) RETURN p.`{property_name}` as data", name=name)
#             record = result.single()
#             return record['data'] if record else None

#     def create_projects_relations(self, name):
#         successful_creations = 0

#         with self._driver.session() as session:
#             # Process 'Atuação Profissional' data
#             professional_data = self.consult_data_by_property(name, 'Atuação Profissional')
#             if professional_data:
#                 for institution_name, _ in json.loads(professional_data).items():
#                     session.run("MERGE (i:Instituição {name: $institution_name})", institution_name=institution_name)
#                     print(f"Institution node created/merged for: {institution_name}")

#                     session.run("MATCH (p:Person {name: $name}), (i:Instituição {name: $institution_name}) MERGE (p)-[:TEM]->(i)", name=name, institution_name=institution_name)
#                     print(f"Relationship established between {name} and {institution_name}.")

#             # Process other dynamic nodes
#             key_labels_to_check = ['Linhas de pesquisa', 'Projetos de pesquisa', 'Projetos de extensão', 'Projetos de desenvolvimento']
#             for key in key_labels_to_check:
#                 formatted_key = f"`{key}`"  # Wrap the key with backticks
#                 project_data = self.consult_data_by_property(name, key)
#                 if project_data:
#                     for project_time, project_name in json.loads(project_data).items():
#                         if project_name:  # to avoid empty names
#                             session.run(f"MERGE (p:{formatted_key} {{name: $project_name}})", project_name=project_name)
#                             print(f"{key} node created/merged for: {project_name}")

#                             session.run(f"MATCH (a:Person {{name: $name}}), (p:{formatted_key} {{name: $project_name}}) MERGE (a)-[:TEM]->(p)", name=name, project_name=project_name)
#                             print(f"Relationship established between {name} and {project_name} ({key}).")
#                             successful_creations += 1
#                 else:
#                     print(f"'{key}' data not found for {name}")

#         print(f"{successful_creations} projetos atualizados com sucesso.")


In [ ]:
# import json
# import re
# from neo4j import GraphDatabase

# class ArticleHandler:

#     def __init__(self, uri, user, password):
#         self._driver = GraphDatabase.driver(uri, auth=(user, password))

#     def close(self):
#         self._driver.close()

#     def fetch_person_productions(self, name):
#         with self._driver.session() as session:
#             result = session.run("MATCH (p:Person {name: $name}) RETURN p.Produções as produções", name=name)
#             record = result.single()
#             return record['produções'] if record else None

#     def extract_article_info(self, input_str):
#         # Encontre todas as abreviaturas de iniciais em maiúsculas e seus índices
#         abbreviations = [(match.group(), match.start()) for match in re.finditer(r'\b[A-Z]\.', input_str)]

#         # Encontre a posição da maior ocorrência de abreviaturas de iniciais, se houver
#         if abbreviations:
#             max_abbr_position = max(abbreviations, key=lambda x: x[1])

#             # Encontre a primeira ocorrência de '. ' ou ' . ' após a maior ocorrência de abreviaturas de iniciais
#             first_separator_candidates = [
#                 input_str.find('. ', max_abbr_position[1] + 3),
#                 input_str.find(' . ', max_abbr_position[1] + 3),
#                 input_str.find('.. ')
#             ]
#             first_separator_candidates = [pos for pos in first_separator_candidates if pos != -1]

#             if first_separator_candidates:
#                 first_separator = min(first_separator_candidates)

#                 # Encontre a primeira ocorrência de '. ' após o primeiro separador
#                 second_separator = input_str.find('. ', first_separator + 2)

#                 # Encontre a primeira ocorrência de ', ' após o segundo separador
#                 third_separator = input_str.find(', ', second_separator + 2)
#             else:
#                 first_separator = second_separator = third_separator = -1
#         else:
#             first_separator = second_separator = third_separator = -1

#         # Defina o padrão para encontrar "p." e o conteúdo até a próxima vírgula
#         pages_match = re.search(r' p\.\s*(.*?),', input_str)
#         pages = pages_match.group(1) if pages_match else ""

#         # Defina o padrão para encontrar "v." e o conteúdo até a próxima vírgula
#         volume_match = re.search(r' v\.\s*(.*?),', input_str)
#         volume = volume_match.group(1) if volume_match else ""

#         # Encontre a primeira ocorrência de um ano de quatro dígitos seguido de ponto final após o terceiro separador
#         year_match = re.search(r' \d{4}\.', input_str[third_separator + 2:])
#         year = year_match.group().strip('.').strip() if year_match else ""

#         # Extraia os dados com base nas posições dos separadores
#         authors = input_str[:first_separator].strip()
#         title = input_str[first_separator + 2:second_separator].strip()
#         journal = input_str[second_separator + 2:third_separator].strip()

#         # Verifique se a lista de autores e o título não estão vazios
#         if not authors or not title:
#             return None  # Retorna None para indicar falha

#         # Crie um dicionário com os dados extraídos
#         article_info = {
#             "authors": authors,
#             "title": title,
#             "original_title": journal,
#             "pages": pages,
#             "volume": volume,
#             "year": year
#         }

#         return article_info
    
#     def deserialize_and_create_nodes(self, name):
#         print(f"Fetching 'Produções' data for {name}...")
#         productions_data = self.fetch_person_productions(name)
        
#         if not productions_data:
#             print(f"'Produções' data not found or empty for {name}.")
#             return

#         print(f"Attempting to deserialize 'Produções' data for {name}...")
#         try:
#             productions_data = json.loads(productions_data)
#         except json.JSONDecodeError as e:
#             print(f"Failed to deserialize 'Produções' data for {name}: {e}")
#             return

#         successful_articles = 0
#         unsuccessful_articles = []

#         with self._driver.session() as session:
#             print(f"Processing 'Produção bibliográfica' for {name}...")
#             bibliographic_production = productions_data.get("Produção bibliográfica", {})
            
#             if isinstance(bibliographic_production, str):
#                 print(f"Attempting to deserialize 'Produção bibliográfica' for {name}...")
#                 try:
#                     bibliographic_production = json.loads(bibliographic_production)
#                 except json.JSONDecodeError as e:
#                     print(f"Failed to deserialize 'Produção bibliográfica' for {name}: {e}")
#                     return

#             articles = json.loads(bibliographic_production.get("Artigos completos publicados em periódicos", "{}"))

#             for _, article_str in articles.items():
#                 article_details = self.extract_article_info(article_str)

#                 # Vamos imprimir os detalhes de cada artigo e verificar se os autores estão presentes.
#                 print(f"Original Article: {article_str}")
#                 print(f"Extracted Details: {article_details}")

#                 if article_details:
#                     article_details["title"] = article_details["title"].strip()
#                     article_details["original_title"] = article_details["original_title"].strip()

#                     session.run(f"MERGE (a:Artigo {{title: $title}}) SET a += $details", title=article_details["title"], details=article_details)
#                     session.run(f"MATCH (p:Person {{name: $name}}), (a:Artigo {{title: $title}}) MERGE (p)-[:PUBLICOU]->(a)", name=name, title=article_details["title"])
#                     successful_articles += 1
#                 else:
#                     unsuccessful_articles.append(article_str)

#         print(f"Processed {successful_articles} articles successfully for {name}.")

#         if unsuccessful_articles:
#             print("Failed to process the following articles:")
#             for article in unsuccessful_articles:
#                 print(article)

#     def process_articles(self, name):
#         self.deserialize_and_create_nodes(name)

In [ ]:
# class JcrHandler:
#     def __init__(self, uri, user, password):
#         self._driver = GraphDatabase.driver(uri, auth=(user, password))

#     def close(self):
#         self._driver.close()

#     def _consultar_propriedades_jcr(self, tx, name):
#         query = (
#             "MATCH (p:Person {name: $name})"
#             "RETURN p.JCR AS jcr"
#         )
#         result = tx.run(query, name=name)
#         return [record["jcr"] for record in result]
   
#     ## Versão para usar com criação de nós secundários retorna JSON
#     def consultar_propriedades_jcr(self, name):
#         with self._driver.session() as session:
#             query = (
#                 "MATCH (p:Person {name: $name})"
#                 "RETURN p.JCR AS jcr"
#             )
#             result = session.run(query, name=name)
#             jcr_data = result.single()["jcr"]
#             jcr_properties_list = json.loads(jcr_data)
#             return jcr_properties_list

#     @staticmethod
#     def _convert_list_to_dict(lst):
#         """
#         Converts a list into a dictionary with indices as keys.
        
#         Parameters:
#         - lst: list, input list to be transformed.
        
#         Returns:
#         - dict: Transformed dictionary.
#         """
#         return {str(i): item for i, item in enumerate(lst)}
    
#     def create_person_with_jcr(self, name, jcr_properties):
#         with self._driver.session() as session:
#             session.write_transaction(self._create_person_with_jcr, name, jcr_properties)

#     @staticmethod
#     def _create_person_with_jcr(tx, name, jcr_properties):
#         # Cria o nó Person
#         person_query = (
#             "CREATE (p:Person {name: $name}) "
#             "RETURN p"
#         )
#         person_result = tx.run(person_query, name=name)
#         person_node = person_result.single()[0]

#         # Cria os nós secundários para cada valor único de data-issn
#         data_issn_values = set(prop.get("data-issn") for prop in jcr_properties)
#         for data_issn in data_issn_values:
#             if data_issn:
#                 secondary_node_query = (
#                     "CREATE (s:SecondaryNode {data_issn: $data_issn}) "
#                     "RETURN s"
#                 )
#                 tx.run(secondary_node_query, data_issn=data_issn)

#                 # Cria a relação entre o nó Person e o nó secundário
#                 relation_query = (
#                     "MATCH (p:Person {name: $name}), (s:SecondaryNode {data_issn: $data_issn}) "
#                     "CREATE (p)-[:HAS_JCR]->(s)"
#                 )
#                 tx.run(relation_query, name=name, data_issn=data_issn)

#     def createJournalsNodes(self, name):
#         # Get JCR properties
#         jcr_properties = self.consultar_propriedades_jcr(name)

#         # Convert the serialized JSON strings back into dictionaries
#         deserialized_jcr_properties = [json.loads(prop) for prop in jcr_properties.values()]

#         # Inform the user about the total number of JCR property entries
#         total_entries = len(deserialized_jcr_properties)
#         print(f"Read {total_entries} entries from JCR properties of Person '{name}'.")

#         # Extract relevant journal properties and their count
#         journal_counts = Counter(prop.get("data-issn") for prop in deserialized_jcr_properties)
        
#         # Number of unique ISSNs
#         unique_issns = len(journal_counts)
#         print(f"Identified {unique_issns} unique ISSN values.")

#         null_count = journal_counts.pop(None, 0)  # Remove None (null) ISSN and get its count
#         null_count += journal_counts.pop("NULL", 0)  # Also account for "NULL" as a string

#         # Counters for journals
#         successful_journal_creations = 0

#         with self._driver.session() as session:
#             for data_issn, count in journal_counts.items():
#                 if data_issn and data_issn != "NULL":
#                     representative_entry = next(prop for prop in deserialized_jcr_properties if prop.get("data-issn") == data_issn)
#                     journal_name = representative_entry.get("original_title")
#                     fator_impacto = representative_entry.get("impact-factor")
#                     jcr_year = representative_entry.get("jcr-year")

#                     # Create or merge the Journal node
#                     journal_node_query = (
#                         "MERGE (j:Revistas {ISSN: $data_issn}) "
#                         "ON CREATE SET j.name = $journal_name, j.FatorImpacto = $impact_factor, j.JCRYear = $jcr_year "  # Corrected this line
#                         "RETURN j"
#                     )
#                     session.run(journal_node_query, data_issn=data_issn, journal_name=journal_name, impact_factor=fator_impacto, jcr_year=jcr_year)  # And this line

#                     # Create or update the "PUBLICOU_EM" relationship
#                     relation_query = (
#                         "MATCH (p:Person {name: $name}), (j:Revistas {ISSN: $data_issn}) "  # corrected this line
#                         "MERGE (p)-[r:PUBLICOU_EM]->(j) "
#                         "ON CREATE SET r.QuantidadePublicações = $count "
#                         "ON MATCH SET r.QuantidadePublicações = r.QuantidadePublicações + $count"
#                     )
#                     session.run(relation_query, name=name, data_issn=data_issn, count=count)
                    
#                     successful_journal_creations += 1
                
#                 if null_count:
#                     # For example, to print the count:
#                     pass
        
#         # Inform the user about journals
#         print(f"{successful_journal_creations} Revistas adicionadas com sucesso.")
#         print(f"{null_count} Revistas não foram criadas por terem valor NULL de ISSN.")

## Teste extrair homônimos

In [ ]:
## Teste de extração para homônimos
# t1 = time.time()
# lista_homonimos = [
#     'Tania Maria Alves de Almeida',
#     'Rodrigo Corrêa de Oliveira',
# ]

# scraper = LattesScraper(termos_busca, 'bolt://localhost:7687', 'neo4j', 'password', only_doctors=True)
# dom_dict_homonimos = scraper.scrape(lista_homonimos, termos_busca)

In [ ]:
df_geral_orientacoes, df_geral_orientacoes_ano = atualizador.apurar_orientacoes(dict_list_docents, ano_inicio, ano_final)
df_geral_orientacoes

In [ ]:
df_geral_orientacoes_ano

In [ ]:
df_geral_orientacoes_old, df_geral_orientacoes_ano_old = atualizador.apurar_orientacoes_old(dict_list_docents, ano_inicio, ano_final)

df_geral_orientacoes_old

In [ ]:
df_geral_orientacoes_ano_old

In [ ]:
print(f'Pontuação dos Orientadores por artigos publicados ponderados pelo JCR no período {ano_inicio} a {ano_final}')
df_artigos_orientadores = atualizador.apurar_jcr_orientadores(df_resultado, orientadores)
df_artigos_orientadores